# V. CELLS QUANTIFICATION AND CLASSIFICATION

## V.1. PACKAGES IMPORT

In [1]:
import os
import random
import re
import pandas as pd
import numpy as np
import seaborn as sb
import matplotlib.pyplot as plt
import matplotlib.colors as mplc
import plotly.graph_objects as go
import warnings
import plotly.express as px

from scipy.stats.stats import pearsonr

from my_modules import *

/var/folders/5g/xq32h5h56rj2qzygbnhjg65h0000gn/T/ipykernel_22409/1860222382.py:13: DeprecationWarning: Please import `pearsonr` from the `scipy.stats` namespace; the `scipy.stats.stats` namespace is deprecated and will be removed in SciPy 2.0.0.
  from scipy.stats.stats import pearsonr


In [2]:
#Silence FutureWarnings & UserWarnings
warnings.filterwarnings('ignore', category= FutureWarning)
warnings.filterwarnings('ignore', category= UserWarning)

## V.2. *DIRECTORIES

In [5]:
# Set base directory

##### MAC WORKSTATION #####
#base_dir = r'/Volumes/LaboLabrie/Projets/OC_TMA_Pejovic/Temp/Zoe/CyCIF_pipeline/'
###########################

##### WINDOWS WORKSTATION #####
#base_dir = r'C:\Users\LaboLabrie\gerz2701\Cyc-IF_pipeline\Set_B'
###############################

##### LOCAL WORKSTATION #####
base_dir = r'/Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431'
#############################

#set_name = 'Set_A'
set_name = 'test'

In [6]:
project_name = set_name                 # Project name
step_suffix = 'cqc'                     # Curent part (here part V)
previous_step_suffix_long = "_mt"       # Previous part (here MT NOTEBOOK)

# Initial input data directory
input_data_dir = os.path.join(base_dir, project_name + previous_step_suffix_long) 

# BS output directories
output_data_dir = os.path.join(base_dir, project_name + "_" + step_suffix)
# BS images subdirectory
output_images_dir = os.path.join(output_data_dir,"images")

# Data and Metadata directories
# Metadata directories
metadata_dir = os.path.join(base_dir, project_name + "_metadata")
# images subdirectory
metadata_images_dir = os.path.join(metadata_dir,"images")

# Create directories if they don't already exist
for d in [base_dir, input_data_dir, output_data_dir, output_images_dir, metadata_dir, metadata_images_dir]:
    if not os.path.exists(d):
        print("Creation of the" , d, "directory...")
        os.makedirs(d)
    else :
        print("The", d, "directory already exists !")

os.chdir(input_data_dir)

The /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431 directory already exists !
The /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_mt directory already exists !
Creation of the /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_cqc directory...
Creation of the /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_cqc/images directory...
The /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_metadata directory already exists !
The /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_metadata/images directory already exists !


In [7]:
# Verify paths
print('base_dir :', base_dir)
print('input_data_dir :', input_data_dir)
print('output_data_dir :', output_data_dir)
print('output_images_dir :', output_images_dir)
print('metadata_dir :', metadata_dir)
print('metadata_images_dir :', metadata_images_dir)

base_dir : /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431
input_data_dir : /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_mt
output_data_dir : /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_cqc
output_images_dir : /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_cqc/images
metadata_dir : /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_metadata
metadata_images_dir : /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_metadata/images


## V.3. FILES

### V.3.1. METADATA

In [8]:
# Import all metadata we need from the BS chapter

filename = "marker_intensity_metadata.csv"
filename = os.path.join(metadata_dir, filename)

# Check file exists
if not os.path.exists(filename):
    print("WARNING: Could not find desired file: "+filename)
else :
    print("The",filename,"file was imported for further analysis!")

# Open, read in information
metadata = pd.read_csv(filename)

# Verify size with verify_line_no() function in my_modules.py
#verify_line_no(filename, metadata.shape[0] + 1)

# Verify headers
exp_cols = ['Round','Target','Channel','target_lower','full_column','marker','localisation']
compare_headers(exp_cols, metadata.columns.values, "Marker metadata file")

metadata = metadata.dropna()
metadata.head()

The /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_metadata/marker_intensity_metadata.csv file was imported for further analysis!
['Exp']


Round Target   Exp Channel target_lower                        full_column  \
0    R0  AF488   300      c2        af488       AF488_Cell_Intensity_Average   
1    R0  AF488   300      c2        af488  AF488_Cytoplasm_Intensity_Average   
2    R0  AF488   300      c2        af488    AF488_Nucleus_Intensity_Average   
3    R0  AF555  1500      c3        af555       AF555_Cell_Intensity_Average   
4    R0  AF555  1500      c3        af555  AF555_Cytoplasm_Intensity_Average   

  marker localisation  
0  AF488         cell  
1  AF488    cytoplasm  
2  AF488      nucleus  
3  AF555         cell  
4  AF555    cytoplasm

### V.3.2. NOT_INTENSITIES

In [9]:
filename = "not_intensities.csv"
filename = os.path.join(metadata_dir, filename)

# Check file exists
if not os.path.exists(filename):
    print("WARNING: Could not find desired file: "+filename)
else :
    print("The",filename,"file was imported for further analysis!")
    
# Open, read in information
not_intensities = []
with open(filename, 'r') as fh:
    not_intensities = fh.read().strip().split("\n")
    # take str, strip whitespace, split on new line character

# Verify size
print("Verifying data read from file is the correct length...\n")
#verify_line_no(filename, len(not_intensities))

# Print to console
print("not_intensities =\n", not_intensities)

The /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_metadata/not_intensities.csv file was imported for further analysis!
Verifying data read from file is the correct length...

not_intensities =
 ['Cytoplasm_Size', 'Nuc_X', 'Primary_chem(1)_vs_surg(0)', 'cluster', 'immune_checkpoint', 'Sample_ID', 'Nucleus_Roundness', 'Unique_ROI_index', 'Nuc_Y', 'Nuc_X_Inv', 'Cell_ID', 'cell_subtype', 'ID', 'Nuc_Y_Inv', 'Patient', 'replicate_ID', 'cell_type', 'ROI_index', 'Cell_Size', 'Nucleus_Size']


### V.3.3. FULL_TO_SHORT_COLUMN_NAMES

In [10]:
filename = "full_to_short_column_names.csv"
filename = os.path.join(metadata_dir, filename)

# Check file exists
if not os.path.exists(filename):
    print("WARNING: Could not find desired file: " + filename)
else :
    print("The",filename,"file was imported for further analysis!")
    
# Open, read in information
df = pd.read_csv(filename, header = 0)

# Verify size
print("Verifying data read from file is the correct length...\n")
#verify_line_no(filename, df.shape[0] + 1)

# Turn into dictionary
full_to_short_names = df.set_index('full_name').T.to_dict('records')[0]

# CD45 instead of CD45b
if project_name == 'Slide_A' :
    full_to_short_names['CD45_Cytoplasm_Intensity_Average'] = full_to_short_names.pop('CD45b_Cytoplasm_Intensity_Average')
    full_to_short_names['CD45_Cytoplasm_Intensity_Average'] = 'CD45_Cytoplasm'

# Print information
print('full_to_short_names =\n',full_to_short_names)

The /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_metadata/full_to_short_column_names.csv file was imported for further analysis!
Verifying data read from file is the correct length...

full_to_short_names =
 {'AF488_Cell_Intensity_Average': 'AF488_Cell', 'AF488_Cytoplasm_Intensity_Average': 'AF488_Cytoplasm', 'AF488_Nucleus_Intensity_Average': 'AF488_Nucleus', 'AF555_Cell_Intensity_Average': 'AF555_Cell', 'AF555_Cytoplasm_Intensity_Average': 'AF555_Cytoplasm', 'AF555_Nucleus_Intensity_Average': 'AF555_Nucleus', 'AF647_Cell_Intensity_Average': 'AF647_Cell', 'AF647_Cytoplasm_Intensity_Average': 'AF647_Cytoplasm', 'AF647_Nucleus_Intensity_Average': 'AF647_Nucleus', 'AF750_Cell_Intensity_Average': 'AF750_Cell', 'AF750_Cytoplasm_Intensity_Average': 'AF750_Cytoplasm', 'AF750_Nucleus_Intensity_Average': 'AF750_Nucleus', 'aSMA_Cell_Intensity_Average': 'aSMA_Cell', 'aSMA_Cytoplasm_Intensity_Average': 'aSMA_Cytoplasm', 'aSMA_Nucleus_Intensity_Average': 'aSMA_Nucleu

### V.3.4. SHORT_TO_FULL_COLUMN_NAMES

In [11]:
filename = "short_to_full_column_names.csv"
filename = os.path.join(metadata_dir, filename)

# Check file exists
if not os.path.exists(filename):
    print("WARNING: Could not find desired file: " + filename)
else :
    print("The",filename,"file was imported for further analysis!")
    
# Open, read in information
df = pd.read_csv(filename, header = 0)

# Verify size
print("Verifying data read from file is the correct length...\n")
#verify_line_no(filename, df.shape[0] + 1)

# Turn into dictionary
short_to_full_names = df.set_index('short_name').T.to_dict('records')[0]

# CD45 instead of CD45b
if project_name == 'Slide_A' :
    short_to_full_names['CD45_Cytoplasm'] = short_to_full_names.pop('CD45b_Cytoplasm')
    short_to_full_names['CD45_Cytoplasm'] = 'CD45_Cytoplasm_Intensity_Average'

# Print information
print('short_to_full_names =\n',short_to_full_names)

The /Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_metadata/short_to_full_column_names.csv file was imported for further analysis!
Verifying data read from file is the correct length...

short_to_full_names =
 {'AF488_Cell': 'AF488_Cell_Intensity_Average', 'AF488_Cytoplasm': 'AF488_Cytoplasm_Intensity_Average', 'AF488_Nucleus': 'AF488_Nucleus_Intensity_Average', 'AF555_Cell': 'AF555_Cell_Intensity_Average', 'AF555_Cytoplasm': 'AF555_Cytoplasm_Intensity_Average', 'AF555_Nucleus': 'AF555_Nucleus_Intensity_Average', 'AF647_Cell': 'AF647_Cell_Intensity_Average', 'AF647_Cytoplasm': 'AF647_Cytoplasm_Intensity_Average', 'AF647_Nucleus': 'AF647_Nucleus_Intensity_Average', 'AF750_Cell': 'AF750_Cell_Intensity_Average', 'AF750_Cytoplasm': 'AF750_Cytoplasm_Intensity_Average', 'AF750_Nucleus': 'AF750_Nucleus_Intensity_Average', 'aSMA_Cell': 'aSMA_Cell_Intensity_Average', 'aSMA_Cytoplasm': 'aSMA_Cytoplasm_Intensity_Average', 'aSMA_Nucleus': 'aSMA_Nucleus_Intensity_Averag

### V.3.5. SAMPLES COLORS

In [12]:
filename = "sample_color_data.csv"
filename = os.path.join(metadata_dir, filename)

# Check file exists
if not os.path.exists(filename):
    print("WARNING: Could not find desired file: " + filename)
else :
    print("The",filename,"file was imported for further analysis!")
    
# Open, read in information
df = pd.read_csv(filename, header = 0)
df = df.drop(columns = ['hex'])

# our tuple of float values for rgb, (r, g, b) was read in 
# as a string '(r, g, b)'. We need to extract the r-, g-, and b-
# substrings and convert them back into floats
df['rgb'] = df.apply(lambda row: rgb_tuple_from_str(row['rgb']), axis = 1)

# Verify size
print("Verifying data read from file is the correct length...\n")
#verify_line_no(filename, df.shape[0] + 1)

# Turn into dictionary
sample_color_dict = df.set_index('Sample_ID').T.to_dict('rgb')[0]

# Print information
print('sample_color_dict =\n',sample_color_dict)

FileNotFoundError: [Errno 2] No such file or directory: '/Users/harshithakolipaka/Downloads/wetransfer_data-zip_2024-05-17_1431/test_metadata/sample_color_data.csv'

### V.3.6. CHANNELS COLORS

In [12]:
filename = "channel_color_data.csv"
filename = os.path.join(metadata_dir, filename)

# Check file exists
if not os.path.exists(filename):
    print("WARNING: Could not find desired file: "+filename)
else :
    print("The",filename,"file was imported for further analysis!")
    
# Open, read in information
df = pd.read_csv(filename, header = 0)
df = df.drop(columns = ['hex'])

# our tuple of float values for rgb, (r, g, b) was read in 
# as a string '(r, g, b)'. We need to extract the r-, g-, and b-
# substrings and convert them back into floats
df['rgb'] = df.apply(lambda row: rgb_tuple_from_str(row['rgb']), axis = 1)

# Verify size
print("Verifying data read from file is the correct length...\n")
#verify_line_no(filename, df.shape[0] + 1)

# Turn into dictionary
channel_color_dict = df.set_index('Channel').T.to_dict('rgb')[0]

# Print information
print('channel_color_dict =\n',channel_color_dict)

The C:\Users\zoege\Documents\Temp\Cyc-IF_pipeline\Set_B\Set_B_metadata\channel_color_data.csv file was imported for further analysis!
Verifying data read from file is the correct length...

channel_color_dict =
 {'c2': (0.00784313725490196, 0.24313725490196078, 1.0), 'c3': (1.0, 0.48627450980392156, 0.0), 'c4': (0.10196078431372549, 0.788235294117647, 0.2196078431372549), 'c5': (0.9098039215686274, 0.0, 0.043137254901960784)}


### V.3.7. ROUNDS COLORS

In [13]:
filename = "round_color_data.csv"
filename = os.path.join(metadata_dir, filename)

# Check file exists
if not os.path.exists(filename):
    print("WARNING: Could not find desired file: "+filename)
else :
    print("The",filename,"file was imported for further analysis!")
    
# Open, read in information
df = pd.read_csv(filename, header = 0)
df = df.drop(columns = ['hex'])

# our tuple of float values for rgb, (r, g, b) was read in 
# as a string '(r, g, b)'. We need to extract the r-, g-, and b-
# substrings and convert them back into floats
df['rgb'] = df.apply(lambda row: rgb_tuple_from_str(row['rgb']), axis = 1)

# Verify size
print("Verifying data read from file is the correct length...\n")
#verify_line_no(filename, df.shape[0] + 1)

# Turn into dictionary
round_color_dict = df.set_index('Round').T.to_dict('rgb')[0]

# Print information
print('round_color_dict =\n',round_color_dict)

The C:\Users\zoege\Documents\Temp\Cyc-IF_pipeline\Set_B\Set_B_metadata\round_color_data.csv file was imported for further analysis!
Verifying data read from file is the correct length...

round_color_dict =
 {'R0': (0.28685356234627135, 0.13009829239513535, 0.23110332132624437), 'R1': (0.36541462435986094, 0.2025447048359916, 0.37693310021636883), 'R2': (0.40867533458903105, 0.2940761173840091, 0.5166711878800253), 'R3': (0.42890613750051265, 0.4082290173220481, 0.6335348887063806), 'R4': (0.4444462906865238, 0.5264664993764805, 0.7056321892616532), 'R5': (0.47707206309601013, 0.6427061780374552, 0.7418477948908153), 'R6': (0.5414454866716836, 0.7466759172596551, 0.7572905778378964), 'R7': (0.6414710091647722, 0.8321551072276492, 0.7746773027952071), 'R8': (0.7684256891219349, 0.8992667116749021, 0.8171383269422353)}


### V.3.8. CELL TYPES COLORS

In [14]:
filename = "celltype_color_data.csv"
filename = os.path.join(metadata_dir, filename)

# Check file exists
if not os.path.exists(filename):
    print("WARNING: Could not find desired file: "+filename)
else :
    print("The",filename,"file was imported for further analysis!")
    
# Open, read in information
df = pd.read_csv(filename, header = 0)
df = df.drop(columns = ['hex'])

# our tuple of float values for rgb, (r, g, b) was read in 
# as a string '(r, g, b)'. We need to extract the r-, g-, and b-
# substrings and convert them back into floats
df['rgb'] = df.apply(lambda row: rgb_tuple_from_str(row['rgb']), axis = 1)

# Verify size
print("Verifying data read from file is the correct length...\n")
#verify_line_no(filename, df.shape[0] + 1)

# Turn into dictionary
cell_type_color_dict = df.set_index('cell_type').T.to_dict('rgb')[0]

# Print information
print('cell_type_color_dict =\n',cell_type_color_dict)

The C:\Users\zoege\Documents\Temp\Cyc-IF_pipeline\Set_B\Set_B_metadata\celltype_color_data.csv file was imported for further analysis!
Verifying data read from file is the correct length...

cell_type_color_dict =
 {'CANCER': (0.1333, 0.5451, 0.1333), 'STROMA': (0.4, 0.4, 0.4), 'IMMUNE': (1.0, 1.0, 0.0), 'ENDOTHELIAL': (0.502, 0.0, 0.502)}


### V.3.9. CELL SUBTYPES COLORS

In [15]:
filename = "cellsubtype_color_data.csv"
filename = os.path.join(metadata_dir, filename)

# Check file exists
if not os.path.exists(filename):
    print("WARNING: Could not find desired file: "+filename)
else :
    print("The",filename,"file was imported for further analysis!")
    
# Open, read in information
df = pd.read_csv(filename, header = 0)
df = df.drop(columns = ['hex'])

# our tuple of float values for rgb, (r, g, b) was read in 
# as a string '(r, g, b)'. We need to extract the r-, g-, and b-
# substrings and convert them back into floats
df['rgb'] = df.apply(lambda row: rgb_tuple_from_str(row['rgb']), axis = 1)

# Verify size
print("Verifying data read from file is the correct length...\n")
#verify_line_no(filename, df.shape[0] + 1)

# Turn into dictionary
cell_subtype_color_dict = df.set_index('cell_subtype').T.to_dict('rgb')[0]

# Print information
print('cell_subtype_color_dict =\n',cell_subtype_color_dict)  

The C:\Users\zoege\Documents\Temp\Cyc-IF_pipeline\Set_B\Set_B_metadata\cellsubtype_color_data.csv file was imported for further analysis!
Verifying data read from file is the correct length...

cell_subtype_color_dict =
 {'DC': (0.6509803921568628, 0.807843137254902, 0.8901960784313725), 'B': (0.12156862745098039, 0.47058823529411764, 0.7058823529411765), 'TCD4': (0.6980392156862745, 0.8745098039215686, 0.5411764705882353), 'TCD8': (0.2, 0.6274509803921569, 0.17254901960784313), 'M1': (0.984313725490196, 0.6039215686274509, 0.6), 'M2': (0.8901960784313725, 0.10196078431372549, 0.10980392156862745), 'Treg': (0.9921568627450981, 0.7490196078431373, 0.43529411764705883), 'IMMUNE_OTHER': (1.0, 0.4980392156862745, 0.0), 'CANCER': (0.792156862745098, 0.6980392156862745, 0.8392156862745098), 'αSMA_myCAF': (0.41568627450980394, 0.23921568627450981, 0.6039215686274509), 'STROMA_OTHER': (1.0, 1.0, 0.6), 'ENDOTHELIAL': (0.6941176470588235, 0.34901960784313724, 0.1568627450980392)}


### V.4.10. IMMUNE CHECKPOINT COLORS

In [16]:
filename = "immunecheckpoint_color_data.csv"
filename = os.path.join(metadata_dir, filename)

# Check file exists
if not os.path.exists(filename):
    print("WARNING: Could not find desired file: "+filename)
else :
    print("The",filename,"file was imported for further analysis!")
    
# Open, read in information
df = pd.read_csv(filename, header = 0)
df = df.drop(columns = ['hex'])

# our tuple of float values for rgb, (r, g, b) was read in 
# as a string '(r, g, b)'. We need to extract the r-, g-, and b-
# substrings and convert them back into floats
df['rgb'] = df.apply(lambda row: rgb_tuple_from_str(row['rgb']), axis = 1)

# Verify size
print("Verifying data read from file is the correct length...\n")
#verify_line_no(filename, df.shape[0] + 1)

# Turn into dictionary
immune_checkpoint_color_dict = df.set_index('immune_checkpoint').T.to_dict('rgb')[0]

# Print information
print('immune_checkpoint_color_dict =\n',immune_checkpoint_color_dict)

The C:\Users\zoege\Documents\Temp\Cyc-IF_pipeline\Set_B\Set_B_metadata\immunecheckpoint_color_data.csv file was imported for further analysis!
Verifying data read from file is the correct length...

immune_checkpoint_color_dict =
 {'B7H4': (0.9677975592919913, 0.44127456009157356, 0.5358103155058701), 'PDL1': (0.3126890019504329, 0.6928754610296064, 0.1923704830330379), 'PD1': (0.23299120924703914, 0.639586552066035, 0.9260706093977744), 'B7H4_PDL1': (0.6402432806212122, 0.56707501056059, 0.36409039926945397), 'B7H4_PD1': (0.6003943842695152, 0.5404305560788043, 0.7309404624518223), 'PDL1_PD1': (0.27284010559873606, 0.6662310065478207, 0.5592205462154062), 'B7H4_PDL1_PD1': (0.5044925901631545, 0.5912455243957383, 0.5514171359788941), 'None': (0.8, 0.8, 0.8)}


### V.3.11. DATA

In [17]:
# DATA
# List files in the directory
# Check if the directory exists
if os.path.exists(input_data_dir):
    # List files in the directory
    ls_samples = [sample for sample in os.listdir(input_data_dir) if sample.endswith("_mt.csv")]
    print("The following CSV files were detected:")
    print([sample for sample in ls_samples])
else:
    print(f"The directory {input_data_dir} does not exist.")

The following CSV files were detected:
['DD3S1_mt.csv', 'DD3S2_mt.csv', 'DD3S3_mt.csv', 'DD4S1_mt.csv', 'DD4S2_mt.csv', 'DD4S3_mt.csv', 'DD5S1_mt.csv', 'DD5S2_mt.csv', 'DD5S3_mt.csv', 'TMA_mt.csv']


In [18]:
# Import all the others files
dfs = {}

# Set variable to hold default header values
# First gather information on expected headers using first file in ls_samples
# Read in the first row of the file corresponding to the first sample (index = 0) in ls_samples
df = pd.read_csv(os.path.join(input_data_dir, ls_samples[0]) , index_col = 0, nrows = 1)
expected_headers = df.columns.values
print(expected_headers)

###############################
# !! This may take a while !! #
###############################
for sample in ls_samples:
    file_path = os.path.join(input_data_dir,sample)
   
    try:
        # Read the CSV file
        df = pd.read_csv(file_path, index_col=0)
        # Check if the DataFrame is empty, if so, don't continue trying to process df and remove it
        
        if not df.empty:
            # Reorder the columns to match the expected headers list
            df = df.reindex(columns=expected_headers)
            print(sample, "file is processed !\n")
            #print(df) 
   
    except pd.errors.EmptyDataError:
        print(f'\nEmpty data error in {sample} file. Removing from analysis...')
        ls_samples.remove(sample)      
    
    # Add df to dfs 
    dfs[sample] = df

#print(dfs)

['PDL1_Cytoplasm_Intensity_Average' 'HLA_Cytoplasm_Intensity_Average'
 'CKs_Cytoplasm_Intensity_Average' 'Ki67_Nucleus_Intensity_Average'
 'CD163_Cytoplasm_Intensity_Average' 'ColVI_Cytoplasm_Intensity_Average'
 'CD20_Cytoplasm_Intensity_Average' 'PD1_Cytoplasm_Intensity_Average'
 'AXL_Cytoplasm_Intensity_Average' 'CD31_Cytoplasm_Intensity_Average'
 'Fibronectin_Cytoplasm_Intensity_Average'
 'CD45_Cytoplasm_Intensity_Average' 'Ecad_Cytoplasm_Intensity_Average'
 'CD8_Cytoplasm_Intensity_Average' 'GATA3_Nucleus_Intensity_Average'
 'Sting_Cytoplasm_Intensity_Average' 'aSMA_Cytoplasm_Intensity_Average'
 'FOXP3_Nucleus_Intensity_Average' 'CD11c_Cytoplasm_Intensity_Average'
 'CD4_Cytoplasm_Intensity_Average' 'Vimentin_Cytoplasm_Intensity_Average'
 'CD44_Cytoplasm_Intensity_Average' 'CD68_Cytoplasm_Intensity_Average'
 'PDGFR_Cytoplasm_Intensity_Average' 'B7H4_Cell_Intensity_Average'
 'MMP9_Cytoplasm_Intensity_Average' 'Desmin_Cytoplasm_Intensity_Average'
 'cell_subtype' 'cell_type' 'Nuc_Y_Inv

In [19]:
# Merge dfs into one df
df = pd.concat(dfs.values(), ignore_index=False , sort = False)
del dfs

print(df.head())

              PDL1_Cytoplasm_Intensity_Average  \
ID                                               
DD3S1_Cell_0                         -0.677863   
DD3S1_Cell_1                         -0.677863   
DD3S1_Cell_2                         -0.677863   
DD3S1_Cell_3                         -0.741282   
DD3S1_Cell_6                         -0.621521   

              HLA_Cytoplasm_Intensity_Average  \
ID                                              
DD3S1_Cell_0                        -0.417494   
DD3S1_Cell_1                        -0.516487   
DD3S1_Cell_2                        -0.141921   
DD3S1_Cell_3                        -0.460472   
DD3S1_Cell_6                        -0.247254   

              CKs_Cytoplasm_Intensity_Average  Ki67_Nucleus_Intensity_Average  \
ID                                                                              
DD3S1_Cell_0                        -0.912537                       -0.817876   
DD3S1_Cell_1                        -0.838037                 

In [20]:
df.shape

(704629, 37)

In [21]:
df.index 

Index(['DD3S1_Cell_0', 'DD3S1_Cell_1', 'DD3S1_Cell_2', 'DD3S1_Cell_3',
       'DD3S1_Cell_6', 'DD3S1_Cell_7', 'DD3S1_Cell_8', 'DD3S1_Cell_10',
       'DD3S1_Cell_11', 'DD3S1_Cell_12',
       ...
       'TMA_Cell_115750', 'TMA_Cell_115751', 'TMA_Cell_115752',
       'TMA_Cell_115753', 'TMA_Cell_115754', 'TMA_Cell_115755',
       'TMA_Cell_115756', 'TMA_Cell_115757', 'TMA_Cell_115758',
       'TMA_Cell_115760'],
      dtype='object', name='ID', length=704629)

In [22]:
df.columns.values

array(['PDL1_Cytoplasm_Intensity_Average',
       'HLA_Cytoplasm_Intensity_Average',
       'CKs_Cytoplasm_Intensity_Average',
       'Ki67_Nucleus_Intensity_Average',
       'CD163_Cytoplasm_Intensity_Average',
       'ColVI_Cytoplasm_Intensity_Average',
       'CD20_Cytoplasm_Intensity_Average',
       'PD1_Cytoplasm_Intensity_Average',
       'AXL_Cytoplasm_Intensity_Average',
       'CD31_Cytoplasm_Intensity_Average',
       'Fibronectin_Cytoplasm_Intensity_Average',
       'CD45_Cytoplasm_Intensity_Average',
       'Ecad_Cytoplasm_Intensity_Average',
       'CD8_Cytoplasm_Intensity_Average',
       'GATA3_Nucleus_Intensity_Average',
       'Sting_Cytoplasm_Intensity_Average',
       'aSMA_Cytoplasm_Intensity_Average',
       'FOXP3_Nucleus_Intensity_Average',
       'CD11c_Cytoplasm_Intensity_Average',
       'CD4_Cytoplasm_Intensity_Average',
       'Vimentin_Cytoplasm_Intensity_Average',
       'CD44_Cytoplasm_Intensity_Average',
       'CD68_Cytoplasm_Intensity_Average',
      

In [23]:
# Check for NaN entries (should not be any unless columns do not align)
# False means no NaN entries 
# True means NaN entries 
df.isnull().any().any()

False

### V.3.12. UNIQUE ROIs

In [24]:
# UNIQUE ROIs
filename = f'{project_name}_unique_ROIs.csv'
filename = os.path.join(metadata_dir, filename)

# Check file exists
if not os.path.exists(filename):
    print("WARNING: Could not find desired file: " + filename)
else :
    print("The",filename,"file was imported for further analysis!")

The C:\Users\zoege\Documents\Temp\Cyc-IF_pipeline\Set_B\Set_B_metadata\Set_B_unique_ROIs.csv file was imported for further analysis!


In [25]:
# Open, read in information
Unique_ROIs = pd.read_csv(filename,delimiter=';')

# Verify headers
exp_cols = ['Sample_ID', 'ROI_index','Patient','Unique_ROI_index']
compare_headers(exp_cols, Unique_ROIs.columns.values, "Unique_ROIs file")

Unique_ROIs = Unique_ROIs.dropna()
Unique_ROIs

Sample_ID  ROI_index Patient Unique_ROI_index
0    DD3S1.csv          0      61              61a
1    DD3S1.csv          1      62              62a
2    DD3S1.csv          2      63              63a
3    DD3S1.csv          3      59              59a
4    DD3S1.csv          4      60              60a
..         ...        ...     ...              ...
462    TMA.csv         55     c55             c55a
463    TMA.csv         56     c56             c56a
464    TMA.csv         57     c57             c57a
465    TMA.csv         58     c58             c58a
466    TMA.csv         59     c59             c59a

[467 rows x 4 columns]

In [26]:
# Jointure des deux dataframes sur la colonne 'Unique_ROI_index'
df1 = df.merge(Unique_ROIs[['Sample_ID', 'ROI_index', 'Patient', 'Unique_ROI_index']], on=['Sample_ID', 'ROI_index'], how='left')

# Set the index of df1 to be the same as the index of df
df1.set_index(df.index, inplace=True)

# Vérification du nouveau dataframe
display(df1)

PDL1_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_0                            -0.677863   
DD3S1_Cell_1                            -0.677863   
DD3S1_Cell_2                            -0.677863   
DD3S1_Cell_3                            -0.741282   
DD3S1_Cell_6                            -0.621521   
...                                           ...   
TMA_Cell_115755                          0.478275   
TMA_Cell_115756                          0.297418   
TMA_Cell_115757                          0.346950   
TMA_Cell_115758                         -0.189415   
TMA_Cell_115760                          0.245777   

                 HLA_Cytoplasm_Intensity_Average  \
ID                                                 
DD3S1_Cell_0                           -0.417494   
DD3S1_Cell_1                           -0.516487   
DD3S1_Cell_2                           -0.141921   
DD3S1_Cell_3                           -0.460472   
DD3S1_Cell_6                           -0.247254   
...                                          ...   
TMA_Cell_115755                         0.558670   
TMA_Cell_115756                         0.420594   
TMA_Cell_115757                         0.453951   
TMA_Cell_115758                         0.508840   
TMA_Cell_115760                         0.460219   

                 CKs_Cytoplasm_Intensity_Average  \
ID                                                 
DD3S1_Cell_0                           -0.912537   
DD3S1_Cell_1                           -0.838037   
DD3S1_Cell_2                           -1.016023   
DD3S1_Cell_3                           -0.491711   
DD3S1_Cell_6                           -0.867127   
...                                          ...   
TMA_Cell_115755                        -0.962840   
TMA_Cell_115756                        -0.971632   
TMA_Cell_115757                        -0.602893   
TMA_Cell_115758                        -0.886041   
TMA_Cell_115760                        -1.003840   

                 Ki67_Nucleus_Intensity_Average  \
ID                                                
DD3S1_Cell_0                          -0.817876   
DD3S1_Cell_1                          -0.869685   
DD3S1_Cell_2                          -0.755879   
DD3S1_Cell_3                          -0.818084   
DD3S1_Cell_6                          -0.742544   
...                                         ...   
TMA_Cell_115755                        1.732291   
TMA_Cell_115756                        1.966955   
TMA_Cell_115757                        1.338956   
TMA_Cell_115758                        0.647980   
TMA_Cell_115760                        0.191158   

                 CD163_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_0                              0.930099   
DD3S1_Cell_1                              1.114924   
DD3S1_Cell_2                              0.834577   
DD3S1_Cell_3                              0.648200   
DD3S1_Cell_6                              0.810579   
...                                            ...   
TMA_Cell_115755                           0.507434   
TMA_Cell_115756                           0.304365   
TMA_Cell_115757                           0.559435   
TMA_Cell_115758                          -0.227224   
TMA_Cell_115760                          -0.313127   

                 ColVI_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_0                              0.232078   
DD3S1_Cell_1                              0.301333   
DD3S1_Cell_2                              0.259216   
DD3S1_Cell_3                              0.107027   
DD3S1_Cell_6                              0.272128   
...                                            ...   
TMA_Cell_115755                          -0.912641   
TMA_Cell_115756                          -1.164112   
TMA_Cell_115757                          -0.801333   
TMA_Cell_115

In [27]:
# Resetting the index temporarily for checking for duplicates
# ID + Unique_ROI_index should not return any duplicate
df_temp = df1.copy()
df_temp.reset_index(inplace=True)
df_temp.rename(columns={'index': 'old_index'}, inplace=True)

# Check for duplicates
duplicates = df_temp[df_temp.duplicated(['ID', 'Unique_ROI_index'], keep=False)]
if not duplicates.empty:
    print("Duplicates found:")
    print(duplicates)
else:
    print("No duplicates found.")

No duplicates found.


### V.3.13. NACT/ACT

In [28]:
filename = "TMA_Clinical_Data_187-OC.csv"
filename = os.path.join(metadata_dir, filename)

# Check file exists
if not os.path.exists(filename):
    print("WARNING: Could not find desired file: " + filename)
else :
    print("The",filename,"file was imported for further analysis!")

The C:\Users\zoege\Documents\Temp\Cyc-IF_pipeline\Set_B\Set_B_metadata\TMA_Clinical_Data_187-OC.csv file was imported for further analysis!


In [29]:
# Open, read in information
clinical_data = pd.read_csv(filename,delimiter=',')

# Renaming columns using the `rename` function
clinical_data = clinical_data.rename(columns={'ID': 'Patient'})
clinical_data['Patient'] = clinical_data['Patient'].astype(str)
df1['Patient'] = df1['Patient'].astype(str)

# Display the first few rows to check the DataFrame
display(clinical_data)

Patient  %_tumor  %_necrosis  Age_Diagnosis   BMI   CA125 Race  \
0         1       80           5           72.0  35.0     NaN    C   
1         2       50           0           36.0  24.0     NaN    C   
2         3       80           5           55.0  45.0   944.0    C   
3         4       80           5           59.0  26.0    50.0    C   
4         5       50           0           70.0  32.0  1426.0    C   
..      ...      ...         ...            ...   ...     ...  ...   
182     183       70           5           72.0  22.0   597.0    C   
183     184       90           0           72.0  26.0  3788.0    C   
184     185       90           0           70.0  29.0  1330.0    C   
185     186       80           0           84.0  17.0   564.0    C   
186     187       80           0           27.0  22.0   922.0    C   

             Other_Cancers BRCAStatus  Primary_chem(1)_vs_surg(0)  ...  \
0                   breast          0                           0  ...   
1                   breast          1                           0  ...   
2                        0        NaN                           0  ...   
3                        0          0                           0  ...   
4                        0        NaN                           1  ...   
..                     ...        ...                         ...  ...   
182                 breast          0                           1  ...   
183                 breast        NaN                           1  ...   
184                      0        NaN                           0  ...   
185  squamouscellcarcinoma        NaN                           0  ...   
186                      0          0                           1  ...   

                                  Histo_Type  Optimal_Debulking  \
0                                      HGSOC                0.0   
1                                      HGSOC                1.0   
2                                      HGSOC                1.0   
3                                    HGtubal                1.0   
4                                        CCC                NaN   
..                                       ...                ...   
182                                    HGSOC                1.0   
183                                    HGSOC                1.0   
184                                    HGSOC                1.0   
185                                    HGSOC                1.0   
186  serousprimarilylowgradewfociofhighgrade                1.0   

    Residual_Disease Platinum_sensitive  Days_surgery_to_recurrence  Avastin  \
0                1.0                1.0                       506.0      1.0   
1                0.0                1.0                       669.0      1.0   
2                0.0                1.0                       596.0      0.0   
3                0.0                NaN                         NaN      NaN   
4                0.0                1.0                       377.0      1.0   
..               ...                ...                         ...      ...   
182              0.0                1.0                         NaN      NaN   
183              0.0                1.0                       282.0      0.0   
184              0.0                NaN                         NaN      NaN   
185              0.0                NaN                         NaN      NaN   
186              1.0                1.0                       540.0      0.0   

     Disease_Stat  Days_from_surgery_to_last_contact_or_death  Recurrence  \
0             DOD                                        1776         1.0   
1             DOD                                        2223         1.0   
2             DOD                                        1355         1.0   
3             NaN                                        1783         NaN   
4             DOD                                         977         1.0   
..            ...                             

In [30]:
print(clinical_data.columns)
print(clinical_data.shape)

Index(['Patient', '%_tumor', '%_necrosis', 'Age_Diagnosis', 'BMI', 'CA125',
       'Race', 'Other_Cancers', 'BRCAStatus', 'Primary_chem(1)_vs_surg(0)',
       'Diagnosis_to_Start_Chemo', 'Diagnosis_to_surgery', 'Stage',
       'Histo_Type', 'Optimal_Debulking', 'Residual_Disease',
       'Platinum_sensitive', 'Days_surgery_to_recurrence', 'Avastin',
       'Disease_Stat', 'Days_from_surgery_to_last_contact_or_death',
       'Recurrence', 'Vital_Status'],
      dtype='object')
(187, 23)


In [31]:
print(df1.columns)
print(df1.shape)

Index(['PDL1_Cytoplasm_Intensity_Average', 'HLA_Cytoplasm_Intensity_Average',
       'CKs_Cytoplasm_Intensity_Average', 'Ki67_Nucleus_Intensity_Average',
       'CD163_Cytoplasm_Intensity_Average',
       'ColVI_Cytoplasm_Intensity_Average', 'CD20_Cytoplasm_Intensity_Average',
       'PD1_Cytoplasm_Intensity_Average', 'AXL_Cytoplasm_Intensity_Average',
       'CD31_Cytoplasm_Intensity_Average',
       'Fibronectin_Cytoplasm_Intensity_Average',
       'CD45_Cytoplasm_Intensity_Average', 'Ecad_Cytoplasm_Intensity_Average',
       'CD8_Cytoplasm_Intensity_Average', 'GATA3_Nucleus_Intensity_Average',
       'Sting_Cytoplasm_Intensity_Average', 'aSMA_Cytoplasm_Intensity_Average',
       'FOXP3_Nucleus_Intensity_Average', 'CD11c_Cytoplasm_Intensity_Average',
       'CD4_Cytoplasm_Intensity_Average',
       'Vimentin_Cytoplasm_Intensity_Average',
       'CD44_Cytoplasm_Intensity_Average', 'CD68_Cytoplasm_Intensity_Average',
       'PDGFR_Cytoplasm_Intensity_Average', 'B7H4_Cell_Intensity_Aver

In [32]:
# Display data types of columns in df1 and NACT
print(df1.dtypes)
print('')
print(clinical_data.dtypes)

PDL1_Cytoplasm_Intensity_Average           float64
HLA_Cytoplasm_Intensity_Average            float64
CKs_Cytoplasm_Intensity_Average            float64
Ki67_Nucleus_Intensity_Average             float64
CD163_Cytoplasm_Intensity_Average          float64
ColVI_Cytoplasm_Intensity_Average          float64
CD20_Cytoplasm_Intensity_Average           float64
PD1_Cytoplasm_Intensity_Average            float64
AXL_Cytoplasm_Intensity_Average            float64
CD31_Cytoplasm_Intensity_Average           float64
Fibronectin_Cytoplasm_Intensity_Average    float64
CD45_Cytoplasm_Intensity_Average           float64
Ecad_Cytoplasm_Intensity_Average           float64
CD8_Cytoplasm_Intensity_Average            float64
GATA3_Nucleus_Intensity_Average            float64
Sting_Cytoplasm_Intensity_Average          float64
aSMA_Cytoplasm_Intensity_Average           float64
FOXP3_Nucleus_Intensity_Average            float64
CD11c_Cytoplasm_Intensity_Average          float64
CD4_Cytoplasm_Intensity_Average

In [33]:
# Liste des valeurs uniques dans la colonne 'Patient' de chaque DataFrame
patients_df1 = set(df1['Patient'].unique())
patients_clinical_data = set(clinical_data['Patient'].unique())

# Patients présents dans df1 mais absents dans clinical_data
patients_unique_to_df1 = patients_df1 - patients_clinical_data

# Patients présents dans NACT mais absents dans df1
patients_unique_to_clinical_data = patients_clinical_data - patients_df1

# Affichage des patients uniques dans chaque DataFrame
print("Patients uniques dans df1 mais absents dans clinical_data:")
print(patients_unique_to_df1)

# no segmented cores?
print("\nPatients uniques dans clinical_data mais absents dans df1:")
print(patients_unique_to_clinical_data)

Patients uniques dans df1 mais absents dans clinical_data:
{'c37', 'c50', 'c38', 'c6', 'c52', 'c55', 'c13', 'c0', 'c25', 'c51', 'c19', 'c42', 'c57', 'c41', 'c56', 'c40', 'c18', 'c21', 'c48', 'c49', 'c1', 'c26', 'c23', 'c39', 'c15', 'c45', 'c34', 'c58', 'c43', 'c32', 'c8', 'c9', 'c4', 'c35', 'c14', 'c27', 'c7', 'c20', 'c2', 'c12', 'c16', 'c46', 'c3', 'c31', 'c28', 'c53', 'c24', 'c59', 'c5', 'c22', 'c11', 'c54', 'c44', 'c17', 'c30', 'c29', 'c10', 'c47', 'c33', 'c36'}

Patients uniques dans clinical_data mais absents dans df1:
{'138', '2', '93', '151', '31', '145', '163', '1', '118', '76'}


In [34]:
# DataFrames fuson based on 'Patient' col
df2 = pd.merge(df1, clinical_data[['Patient', 'Primary_chem(1)_vs_surg(0)']], on='Patient', how='left')

# Set the index of df1 to be the same as the index of df
df2.set_index(df.index, inplace=True)

print(df2.columns)
print(df2.shape)
df2

Index(['PDL1_Cytoplasm_Intensity_Average', 'HLA_Cytoplasm_Intensity_Average',
       'CKs_Cytoplasm_Intensity_Average', 'Ki67_Nucleus_Intensity_Average',
       'CD163_Cytoplasm_Intensity_Average',
       'ColVI_Cytoplasm_Intensity_Average', 'CD20_Cytoplasm_Intensity_Average',
       'PD1_Cytoplasm_Intensity_Average', 'AXL_Cytoplasm_Intensity_Average',
       'CD31_Cytoplasm_Intensity_Average',
       'Fibronectin_Cytoplasm_Intensity_Average',
       'CD45_Cytoplasm_Intensity_Average', 'Ecad_Cytoplasm_Intensity_Average',
       'CD8_Cytoplasm_Intensity_Average', 'GATA3_Nucleus_Intensity_Average',
       'Sting_Cytoplasm_Intensity_Average', 'aSMA_Cytoplasm_Intensity_Average',
       'FOXP3_Nucleus_Intensity_Average', 'CD11c_Cytoplasm_Intensity_Average',
       'CD4_Cytoplasm_Intensity_Average',
       'Vimentin_Cytoplasm_Intensity_Average',
       'CD44_Cytoplasm_Intensity_Average', 'CD68_Cytoplasm_Intensity_Average',
       'PDGFR_Cytoplasm_Intensity_Average', 'B7H4_Cell_Intensity_Aver

PDL1_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_0                            -0.677863   
DD3S1_Cell_1                            -0.677863   
DD3S1_Cell_2                            -0.677863   
DD3S1_Cell_3                            -0.741282   
DD3S1_Cell_6                            -0.621521   
...                                           ...   
TMA_Cell_115755                          0.478275   
TMA_Cell_115756                          0.297418   
TMA_Cell_115757                          0.346950   
TMA_Cell_115758                         -0.189415   
TMA_Cell_115760                          0.245777   

                 HLA_Cytoplasm_Intensity_Average  \
ID                                                 
DD3S1_Cell_0                           -0.417494   
DD3S1_Cell_1                           -0.516487   
DD3S1_Cell_2                           -0.141921   
DD3S1_Cell_3                           -0.460472   
DD3S1_Cell_6                           -0.247254   
...                                          ...   
TMA_Cell_115755                         0.558670   
TMA_Cell_115756                         0.420594   
TMA_Cell_115757                         0.453951   
TMA_Cell_115758                         0.508840   
TMA_Cell_115760                         0.460219   

                 CKs_Cytoplasm_Intensity_Average  \
ID                                                 
DD3S1_Cell_0                           -0.912537   
DD3S1_Cell_1                           -0.838037   
DD3S1_Cell_2                           -1.016023   
DD3S1_Cell_3                           -0.491711   
DD3S1_Cell_6                           -0.867127   
...                                          ...   
TMA_Cell_115755                        -0.962840   
TMA_Cell_115756                        -0.971632   
TMA_Cell_115757                        -0.602893   
TMA_Cell_115758                        -0.886041   
TMA_Cell_115760                        -1.003840   

                 Ki67_Nucleus_Intensity_Average  \
ID                                                
DD3S1_Cell_0                          -0.817876   
DD3S1_Cell_1                          -0.869685   
DD3S1_Cell_2                          -0.755879   
DD3S1_Cell_3                          -0.818084   
DD3S1_Cell_6                          -0.742544   
...                                         ...   
TMA_Cell_115755                        1.732291   
TMA_Cell_115756                        1.966955   
TMA_Cell_115757                        1.338956   
TMA_Cell_115758                        0.647980   
TMA_Cell_115760                        0.191158   

                 CD163_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_0                              0.930099   
DD3S1_Cell_1                              1.114924   
DD3S1_Cell_2                              0.834577   
DD3S1_Cell_3                              0.648200   
DD3S1_Cell_6                              0.810579   
...                                            ...   
TMA_Cell_115755                           0.507434   
TMA_Cell_115756                           0.304365   
TMA_Cell_115757                           0.559435   
TMA_Cell_115758                          -0.227224   
TMA_Cell_115760                          -0.313127   

                 ColVI_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_0                              0.232078   
DD3S1_Cell_1                              0.301333   
DD3S1_Cell_2                              0.259216   
DD3S1_Cell_3                              0.107027   
DD3S1_Cell_6                              0.272128   
...                                            ...   
TMA_Cell_115755                          -0.912641   
TMA_Cell_115756                          -1.164112   
TMA_Cell_115757                          -0.801333   
TMA_Cell_115

In [35]:
#NACT rows
clinical_data[clinical_data['Primary_chem(1)_vs_surg(0)'] == 1]

Patient  %_tumor  %_necrosis  Age_Diagnosis   BMI    CA125      Race  \
4         5       50           0           70.0  32.0   1426.0         C   
6         7       80           5           63.0  29.0  10965.0         C   
10       11       90           0           58.0  20.0     72.0         C   
14       15       60           0           77.0  35.0    183.0         C   
17       18       90           0           75.0  25.0     55.0         C   
25       26       80           0           69.0  29.0   1907.0         C   
30       31       70           0           62.0  26.0  11785.0         C   
31       32       90           5           75.0  41.0   4532.0         C   
39       40       70           5           64.0   NaN   8393.0         C   
50       51       90           0           55.0  33.0   1000.0         C   
60       61       60          10           65.0  23.0    281.0         C   
84       85       90           0           61.0  30.0    116.0  hispanic   
88       89       90           0           64.0  28.0    855.0         C   
94       95       80           5           80.0  24.0   2799.0         C   
97       98       70           0           79.0  26.0   2461.0         C   
103     104       90           0           60.0  29.0     63.0         C   
110     111       90           5           50.0  32.0   1960.0         C   
115     116       80           0           76.0  34.0   7453.0         C   
118     119       90           0           57.0  17.0  16234.0         C   
120     121       90           5           64.0  38.0   2207.0         C   
136     137       90           0           54.0  19.0   2964.0         C   
137     138       70           5           70.0  26.0   1210.0     Asian   
139     140       70           5           71.0  21.0   1046.0         C   
140     141       70           5           31.0  31.0    575.0         C   
145     146       70           0           71.0  21.0  10824.0         C   
148     149       70           0           52.0  26.0   7363.0         C   
152     153       80           5           64.0  23.0    968.0         C   
156     157       80           5           56.0  36.0   1971.0         C   
159     160       90           5           59.0  27.0     89.0         C   
161     162       80           0           75.0  20.0   7482.0         C   
168     169       80           5           75.0  35.0    245.0         C   
170     171       80           5           60.0  34.0    500.0         C   
173     174       50           0           54.0  36.0   8529.0         C   
176     177       90           0           60.0  32.0    919.0         C   
177     178       80           0           67.0  27.0    107.0         C   
178     179       80           0           83.0  25.0      NaN         C   
181     182       80           0           81.0  28.0    990.0         C   
182     183       70           5           72.0  22.0    597.0         C   
183     184       90           0           72.0  26.0   3788.0         C   
186     187       80           0           27.0  22.0    922.0         C   

                              Other_Cancers BRCAStatus  \
4                                         0        NaN   
6                                         0        NaN   
10                                        0        NaN   
14                                        0        NaN   
17                                        0          0   
25                                        0          0   
30                                        0        NaN   
31                                        0        NaN   
39                                      NaN        NaN   
50                                renalcell        NaN   
60                                        0        NaN   
84                                        0        NaN   
88                                        0          0   
94                                        0        NaN   
97               

In [36]:
# Go through 'Primary_chem(1)_vs_surg(0)' col to replace NaN values by 'CONTROL' if 'c' in 'Patient' col
df2.loc[(df2['Primary_chem(1)_vs_surg(0)'].isnull()) & (df2['Patient'].astype(str).str.contains('c|^c')), 'Primary_chem(1)_vs_surg(0)'] = 'CONTROL'

df2

PDL1_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_0                            -0.677863   
DD3S1_Cell_1                            -0.677863   
DD3S1_Cell_2                            -0.677863   
DD3S1_Cell_3                            -0.741282   
DD3S1_Cell_6                            -0.621521   
...                                           ...   
TMA_Cell_115755                          0.478275   
TMA_Cell_115756                          0.297418   
TMA_Cell_115757                          0.346950   
TMA_Cell_115758                         -0.189415   
TMA_Cell_115760                          0.245777   

                 HLA_Cytoplasm_Intensity_Average  \
ID                                                 
DD3S1_Cell_0                           -0.417494   
DD3S1_Cell_1                           -0.516487   
DD3S1_Cell_2                           -0.141921   
DD3S1_Cell_3                           -0.460472   
DD3S1_Cell_6                           -0.247254   
...                                          ...   
TMA_Cell_115755                         0.558670   
TMA_Cell_115756                         0.420594   
TMA_Cell_115757                         0.453951   
TMA_Cell_115758                         0.508840   
TMA_Cell_115760                         0.460219   

                 CKs_Cytoplasm_Intensity_Average  \
ID                                                 
DD3S1_Cell_0                           -0.912537   
DD3S1_Cell_1                           -0.838037   
DD3S1_Cell_2                           -1.016023   
DD3S1_Cell_3                           -0.491711   
DD3S1_Cell_6                           -0.867127   
...                                          ...   
TMA_Cell_115755                        -0.962840   
TMA_Cell_115756                        -0.971632   
TMA_Cell_115757                        -0.602893   
TMA_Cell_115758                        -0.886041   
TMA_Cell_115760                        -1.003840   

                 Ki67_Nucleus_Intensity_Average  \
ID                                                
DD3S1_Cell_0                          -0.817876   
DD3S1_Cell_1                          -0.869685   
DD3S1_Cell_2                          -0.755879   
DD3S1_Cell_3                          -0.818084   
DD3S1_Cell_6                          -0.742544   
...                                         ...   
TMA_Cell_115755                        1.732291   
TMA_Cell_115756                        1.966955   
TMA_Cell_115757                        1.338956   
TMA_Cell_115758                        0.647980   
TMA_Cell_115760                        0.191158   

                 CD163_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_0                              0.930099   
DD3S1_Cell_1                              1.114924   
DD3S1_Cell_2                              0.834577   
DD3S1_Cell_3                              0.648200   
DD3S1_Cell_6                              0.810579   
...                                            ...   
TMA_Cell_115755                           0.507434   
TMA_Cell_115756                           0.304365   
TMA_Cell_115757                           0.559435   
TMA_Cell_115758                          -0.227224   
TMA_Cell_115760                          -0.313127   

                 ColVI_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_0                              0.232078   
DD3S1_Cell_1                              0.301333   
DD3S1_Cell_2                              0.259216   
DD3S1_Cell_3                              0.107027   
DD3S1_Cell_6                              0.272128   
...                                            ...   
TMA_Cell_115755                          -0.912641   
TMA_Cell_115756                          -1.164112   
TMA_Cell_115757                          -0.801333   
TMA_Cell_115

In [37]:
# supposed empty
df2[df2['Primary_chem(1)_vs_surg(0)'].isna()]

Empty DataFrame
Columns: [PDL1_Cytoplasm_Intensity_Average, HLA_Cytoplasm_Intensity_Average, CKs_Cytoplasm_Intensity_Average, Ki67_Nucleus_Intensity_Average, CD163_Cytoplasm_Intensity_Average, ColVI_Cytoplasm_Intensity_Average, CD20_Cytoplasm_Intensity_Average, PD1_Cytoplasm_Intensity_Average, AXL_Cytoplasm_Intensity_Average, CD31_Cytoplasm_Intensity_Average, Fibronectin_Cytoplasm_Intensity_Average, CD45_Cytoplasm_Intensity_Average, Ecad_Cytoplasm_Intensity_Average, CD8_Cytoplasm_Intensity_Average, GATA3_Nucleus_Intensity_Average, Sting_Cytoplasm_Intensity_Average, aSMA_Cytoplasm_Intensity_Average, FOXP3_Nucleus_Intensity_Average, CD11c_Cytoplasm_Intensity_Average, CD4_Cytoplasm_Intensity_Average, Vimentin_Cytoplasm_Intensity_Average, CD44_Cytoplasm_Intensity_Average, CD68_Cytoplasm_Intensity_Average, PDGFR_Cytoplasm_Intensity_Average, B7H4_Cell_Intensity_Average, MMP9_Cytoplasm_Intensity_Average, Desmin_Cytoplasm_Intensity_Average, cell_subtype, cell_type, Nuc_Y_Inv, Nucleus_Roundness, Nuc_X, ROI_index, Nucleus_Size, Sample_ID, immune_checkpoint, Cell_Size, Patient, Unique_ROI_index, Primary_chem(1)_vs_surg(0)]
Index: []

[0 rows x 40 columns]

In [38]:
# Création de trois DataFrames en fonction des valeurs dans 'Primary_chem(1)_vs_surg(0)'
df_NACT = df2[df2['Primary_chem(1)_vs_surg(0)'] == 1]
df_ACT = df2[df2['Primary_chem(1)_vs_surg(0)'] == 0]
df_control = df2[df2['Primary_chem(1)_vs_surg(0)'] == 'CONTROL']

filename_NACT = os.path.join(output_data_dir, 'df_NACT.csv')
filename_ACT = os.path.join(output_data_dir, 'df_ACT.csv')
filename_control = os.path.join(output_data_dir, 'df_control.csv')

# Enregistrement des DataFrames dans des fichiers CSV dans le répertoire output_data_dir
df_NACT.to_csv(filename_NACT, index=False)
df_ACT.to_csv(filename_ACT, index=False)
df_control.to_csv(filename_control, index=False)

In [39]:
df_NACT

PDL1_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_0                             -0.677863   
DD3S1_Cell_1                             -0.677863   
DD3S1_Cell_2                             -0.677863   
DD3S1_Cell_3                             -0.741282   
DD3S1_Cell_6                             -0.621521   
...                                            ...   
DD5S3_Cell_62826                         -0.446025   
DD5S3_Cell_62828                         -0.414440   
DD5S3_Cell_62829                         -0.720569   
DD5S3_Cell_62830                         -0.442500   
DD5S3_Cell_62831                          0.040892   

                  HLA_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_0                            -0.417494   
DD3S1_Cell_1                            -0.516487   
DD3S1_Cell_2                            -0.141921   
DD3S1_Cell_3                            -0.460472   
DD3S1_Cell_6                            -0.247254   
...                                           ...   
DD5S3_Cell_62826                         0.480212   
DD5S3_Cell_62828                         0.416668   
DD5S3_Cell_62829                         0.072144   
DD5S3_Cell_62830                         0.368654   
DD5S3_Cell_62831                         1.166606   

                  CKs_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_0                            -0.912537   
DD3S1_Cell_1                            -0.838037   
DD3S1_Cell_2                            -1.016023   
DD3S1_Cell_3                            -0.491711   
DD3S1_Cell_6                            -0.867127   
...                                           ...   
DD5S3_Cell_62826                         1.195440   
DD5S3_Cell_62828                         1.542926   
DD5S3_Cell_62829                        -0.311962   
DD5S3_Cell_62830                        -1.491754   
DD5S3_Cell_62831                        -1.676753   

                  Ki67_Nucleus_Intensity_Average  \
ID                                                 
DD3S1_Cell_0                           -0.817876   
DD3S1_Cell_1                           -0.869685   
DD3S1_Cell_2                           -0.755879   
DD3S1_Cell_3                           -0.818084   
DD3S1_Cell_6                           -0.742544   
...                                          ...   
DD5S3_Cell_62826                       -0.081463   
DD5S3_Cell_62828                       -0.203248   
DD5S3_Cell_62829                       -0.481442   
DD5S3_Cell_62830                       -0.316270   
DD5S3_Cell_62831                        0.249586   

                  CD163_Cytoplasm_Intensity_Average  \
ID                                                    
DD3S1_Cell_0                               0.930099   
DD3S1_Cell_1                               1.114924   
DD3S1_Cell_2                               0.834577   
DD3S1_Cell_3                               0.648200   
DD3S1_Cell_6                               0.810579   
...                                             ...   
DD5S3_Cell_62826                          -0.634343   
DD5S3_Cell_62828                          -0.076555   
DD5S3_Cell_62829                           1.236053   
DD5S3_Cell_62830                           0.029502   
DD5S3_Cell_62831                          -1.486438   

                  ColVI_Cytoplasm_Intensity_Average  \
ID                                                    
DD3S1_Cell_0                               0.232078   
DD3S1_Cell_1                               0.301333   
DD3S1_Cell_2                               0.259216   
DD3S1_Cell_3                               0.107027   
DD3S1_Cell_6                               0.272128   
...                                             ...   
DD5S3_Cell_62826                          -0.883815   
DD5S3_Cell_62828                          -0.78

In [40]:
df_ACT

PDL1_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_1910                          -1.137775   
DD3S1_Cell_1911                          -1.399789   
DD3S1_Cell_1922                          -1.186023   
DD3S1_Cell_1928                          -0.329397   
DD3S1_Cell_1942                          -0.970875   
...                                            ...   
DD5S3_Cell_64060                         -0.677863   
DD5S3_Cell_64061                          0.479994   
DD5S3_Cell_64062                          0.660736   
DD5S3_Cell_64063                          0.232880   
DD5S3_Cell_64066                         -0.166463   

                  HLA_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_1910                         -0.495306   
DD3S1_Cell_1911                          0.791106   
DD3S1_Cell_1922                         -0.520883   
DD3S1_Cell_1928                          0.396547   
DD3S1_Cell_1942                         -0.126315   
...                                           ...   
DD5S3_Cell_64060                         0.887158   
DD5S3_Cell_64061                         0.415456   
DD5S3_Cell_64062                         0.440965   
DD5S3_Cell_64063                         0.505008   
DD5S3_Cell_64066                         0.896852   

                  CKs_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_1910                         -1.178944   
DD3S1_Cell_1911                          0.567668   
DD3S1_Cell_1922                         -1.104365   
DD3S1_Cell_1928                          1.746212   
DD3S1_Cell_1942                          1.072148   
...                                           ...   
DD5S3_Cell_64060                        -0.528183   
DD5S3_Cell_64061                         0.819658   
DD5S3_Cell_64062                         1.409010   
DD5S3_Cell_64063                         0.798055   
DD5S3_Cell_64066                        -1.903397   

                  Ki67_Nucleus_Intensity_Average  \
ID                                                 
DD3S1_Cell_1910                        -0.832994   
DD3S1_Cell_1911                         0.215155   
DD3S1_Cell_1922                        -0.894190   
DD3S1_Cell_1928                         1.313160   
DD3S1_Cell_1942                         0.178276   
...                                          ...   
DD5S3_Cell_64060                        0.525142   
DD5S3_Cell_64061                        0.623611   
DD5S3_Cell_64062                        0.406828   
DD5S3_Cell_64063                        1.721604   
DD5S3_Cell_64066                        3.436984   

                  CD163_Cytoplasm_Intensity_Average  \
ID                                                    
DD3S1_Cell_1910                            1.067765   
DD3S1_Cell_1911                            0.518692   
DD3S1_Cell_1922                            0.988875   
DD3S1_Cell_1928                            1.139536   
DD3S1_Cell_1942                            1.103388   
...                                             ...   
DD5S3_Cell_64060                           5.217188   
DD5S3_Cell_64061                           2.082444   
DD5S3_Cell_64062                           2.082444   
DD5S3_Cell_64063                           0.625211   
DD5S3_Cell_64066                           1.873290   

                  ColVI_Cytoplasm_Intensity_Average  \
ID                                                    
DD3S1_Cell_1910                            1.432729   
DD3S1_Cell_1911                           -0.627981   
DD3S1_Cell_1922                            1.417141   
DD3S1_Cell_1928                           -0.546020   
DD3S1_Cell_1942                           -0.498249   
...                                             ...   
DD5S3_Cell_64060                          -1.300569   
DD5S3_Cell_64061                          -1.05

In [41]:
df_control

PDL1_Cytoplasm_Intensity_Average  \
ID                                                  
TMA_Cell_4                              -0.367050   
TMA_Cell_300                            -0.738040   
TMA_Cell_1231                           -0.166333   
TMA_Cell_1240                           -0.293766   
TMA_Cell_2107                           -0.677863   
...                                           ...   
TMA_Cell_115755                          0.478275   
TMA_Cell_115756                          0.297418   
TMA_Cell_115757                          0.346950   
TMA_Cell_115758                         -0.189415   
TMA_Cell_115760                          0.245777   

                 HLA_Cytoplasm_Intensity_Average  \
ID                                                 
TMA_Cell_4                              3.386458   
TMA_Cell_300                            2.894731   
TMA_Cell_1231                           3.870697   
TMA_Cell_1240                           2.246166   
TMA_Cell_2107                           2.130819   
...                                          ...   
TMA_Cell_115755                         0.558670   
TMA_Cell_115756                         0.420594   
TMA_Cell_115757                         0.453951   
TMA_Cell_115758                         0.508840   
TMA_Cell_115760                         0.460219   

                 CKs_Cytoplasm_Intensity_Average  \
ID                                                 
TMA_Cell_4                             -2.000166   
TMA_Cell_300                           -2.027276   
TMA_Cell_1231                          -1.953719   
TMA_Cell_1240                          -1.945873   
TMA_Cell_2107                          -2.035940   
...                                          ...   
TMA_Cell_115755                        -0.962840   
TMA_Cell_115756                        -0.971632   
TMA_Cell_115757                        -0.602893   
TMA_Cell_115758                        -0.886041   
TMA_Cell_115760                        -1.003840   

                 Ki67_Nucleus_Intensity_Average  \
ID                                                
TMA_Cell_4                            -0.459972   
TMA_Cell_300                          -0.536334   
TMA_Cell_1231                         -0.289915   
TMA_Cell_1240                         -0.607328   
TMA_Cell_2107                         -0.746582   
...                                         ...   
TMA_Cell_115755                        1.732291   
TMA_Cell_115756                        1.966955   
TMA_Cell_115757                        1.338956   
TMA_Cell_115758                        0.647980   
TMA_Cell_115760                        0.191158   

                 CD163_Cytoplasm_Intensity_Average  \
ID                                                   
TMA_Cell_4                                2.082444   
TMA_Cell_300                              2.463664   
TMA_Cell_1231                             2.276577   
TMA_Cell_1240                             2.082444   
TMA_Cell_2107                             1.538367   
...                                            ...   
TMA_Cell_115755                           0.507434   
TMA_Cell_115756                           0.304365   
TMA_Cell_115757                           0.559435   
TMA_Cell_115758                          -0.227224   
TMA_Cell_115760                          -0.313127   

                 ColVI_Cytoplasm_Intensity_Average  \
ID                                                   
TMA_Cell_4                               -0.331127   
TMA_Cell_300                              0.615413   
TMA_Cell_1231                            -0.760463   
TMA_Cell_1240                            -0.615345   
TMA_Cell_2107                             1.246304   
...                                            ...   
TMA_Cell_115755                          -0.912641   
TMA_Cell_115756                          -1.164112   
TMA_Cell_115757                          -0.801333   
TMA_Cell_115

## V.4. COUNTS

In [42]:
df = df2.copy()

In [43]:
# Get counts for each Sample_ID, sorted by Sample_ID
sample_counts = pd.DataFrame(df.Sample_ID.value_counts()).sort_index()
sample_counts = sample_counts.rename(columns = {'Sample_ID':'counts'})
sample_counts['Sample_ID'] = sample_counts.index
#counts['color'] = counts.apply(lambda row: color_dict[row['Sample_ID']], axis = 1)
sample_counts

counts  Sample_ID
DD3S1.csv   68697  DD3S1.csv
DD3S2.csv   70850  DD3S2.csv
DD3S3.csv  116265  DD3S3.csv
DD4S1.csv   70748  DD4S1.csv
DD4S2.csv   51745  DD4S2.csv
DD4S3.csv   70818  DD4S3.csv
DD5S1.csv   69463  DD5S1.csv
DD5S2.csv   45403  DD5S2.csv
DD5S3.csv   45898  DD5S3.csv
TMA.csv     94742    TMA.csv

### V.4.1. CELL TYPES

In [44]:
# Count by cell type
stroma_counts = pd.DataFrame({'stroma':
    df.loc[
        df['cell_type'] == 'STROMA',:].Sample_ID.value_counts()}).sort_index()

immune_counts = pd.DataFrame({'immune':
    df.loc[
        df['cell_type'] == 'IMMUNE',:].Sample_ID.value_counts()}).sort_index()

cancer_counts = pd.DataFrame({'cancer':
    df.loc[
        df['cell_type'] == 'CANCER',:].Sample_ID.value_counts()}).sort_index()

endothelial_counts = pd.DataFrame({'endothelial':
    df.loc[
        df['cell_type'] == 'ENDOTHELIAL',:].Sample_ID.value_counts()}).sort_index()

counts = pd.concat([sample_counts, stroma_counts,cancer_counts,immune_counts,endothelial_counts], 
                   axis = 1, sort = False)

counts = counts.fillna(0)
print(counts)

filename = os.path.join(output_data_dir , project_name + "_cell_types_number.csv")
counts.to_csv(filename, index = False)

           counts  Sample_ID  stroma  cancer  immune  endothelial
DD3S1.csv   68697  DD3S1.csv   10690   48981    7360         1666
DD3S2.csv   70850  DD3S2.csv   12064   51059    5977         1750
DD3S3.csv  116265  DD3S3.csv   23412   77000   13075         2778
DD4S1.csv   70748  DD4S1.csv    7249   54013    7433         2053
DD4S2.csv   51745  DD4S2.csv    6193   39470    4850         1232
DD4S3.csv   70818  DD4S3.csv    8516   50598   10331         1373
DD5S1.csv   69463  DD5S1.csv   17067   43723    5878         2795
DD5S2.csv   45403  DD5S2.csv   11098   30839    2131         1335
DD5S3.csv   45898  DD5S3.csv    9018   30060    5656         1164
TMA.csv     94742    TMA.csv   23121   59978    9356         2287


In [45]:
# Compute %
# get_perc() function in my_modules.py

counts['stroma_perc'] = counts.apply(lambda row: get_perc(row, 'stroma'), axis = 1)
counts['immune_perc'] = counts.apply(lambda row: get_perc(row, 'immune'), axis = 1)
counts['cancer_perc'] = counts.apply(lambda row: get_perc(row, 'cancer'), axis = 1)
counts['endothelial_perc'] = counts.apply(lambda row: get_perc(row, 'endothelial'), axis = 1)

counts

counts  Sample_ID  stroma  cancer  immune  endothelial  \
DD3S1.csv   68697  DD3S1.csv   10690   48981    7360         1666   
DD3S2.csv   70850  DD3S2.csv   12064   51059    5977         1750   
DD3S3.csv  116265  DD3S3.csv   23412   77000   13075         2778   
DD4S1.csv   70748  DD4S1.csv    7249   54013    7433         2053   
DD4S2.csv   51745  DD4S2.csv    6193   39470    4850         1232   
DD4S3.csv   70818  DD4S3.csv    8516   50598   10331         1373   
DD5S1.csv   69463  DD5S1.csv   17067   43723    5878         2795   
DD5S2.csv   45403  DD5S2.csv   11098   30839    2131         1335   
DD5S3.csv   45898  DD5S3.csv    9018   30060    5656         1164   
TMA.csv     94742    TMA.csv   23121   59978    9356         2287   

           stroma_perc  immune_perc  cancer_perc  endothelial_perc  
DD3S1.csv         15.6         10.7         71.3               2.4  
DD3S2.csv         17.0          8.4         72.1               2.5  
DD3S3.csv         20.1         11.2         66.2               2.4  
DD4S1.csv         10.2         10.5         76.3               2.9  
DD4S2.csv         12.0          9.4         76.3               2.4  
DD4S3.csv         12.0         14.6         71.4               1.9  
DD5S1.csv         24.6          8.5         62.9               4.0  
DD5S2.csv         24.4          4.7         67.9               2.9  
DD5S3.csv         19.6         12.3         65.5               2.5  
TMA.csv           24.4          9.9         63.3               2.4

In [46]:
fig = go.Figure()
title = 'Cell proportions by Sample ID and tissue type'

fig = go.Figure(data=[
    go.Bar(name='Stroma', x=counts['Sample_ID'], y=counts['stroma_perc'], 
           text = counts['stroma_perc'], textposition='auto',
           marker_color = 'rgb' + str(cell_type_color_dict['STROMA'])),
    go.Bar(name='Immune', x=counts['Sample_ID'], y=counts['immune_perc'], 
           text = counts['immune_perc'], textposition='auto',
           marker_color = 'rgb' + str(cell_type_color_dict['IMMUNE'])),
    go.Bar(name='Cancer',x=counts['Sample_ID'], y=counts['cancer_perc'], 
           text = counts['cancer_perc'], textposition='auto', 
           marker_color = 'rgb' + str(cell_type_color_dict['CANCER'])),
    go.Bar(name='Endothelial',x=counts['Sample_ID'], y=counts['endothelial_perc'], 
           text = counts['endothelial_perc'], textposition='auto', 
           marker_color = 'rgb' + str(cell_type_color_dict['ENDOTHELIAL']))
])
    
fig.update_layout( plot_bgcolor = 'white',barmode ='stack')#title = title,
fig.update_xaxes( linecolor = 'black')#title = "Sample",
fig.update_yaxes(title = "Cell count (%)", linecolor = 'black')
plot(fig)
#fig.write_image(output_images_dir + "/" + title.replace(" ","_") + ".png")

'temp-plot.html'

### V.4.2. CELL SUBTYPES

#### V.4.2.1 BY SCENES

In [47]:
# Count by cell SUBtype
cell_subtypes = ['DC', 'B', 'TCD4', 'TCD8', 'M1', 'M2', 'Treg', \
                 'IMMUNE_OTHER', 'CANCER', 'αSMA_myCAF', 'STROMA_OTHER', 'ENDOTHELIAL']
# Initialisation d'un dictionnaire pour stocker les counts des sous-types de cellules
subtype_counts = {}

# Boucle sur les sous-types de cellules pour compter les échantillons correspondants
for subtype in cell_subtypes:
    subtype_counts[subtype.lower()] = pd.DataFrame({subtype.lower():
        df.loc[
            df['cell_subtype'] == subtype, 'Sample_ID'].value_counts()
    }).sort_index()

# Concaténation des counts des sous-types de cellules en un seul DataFrame
counts_subtypes = pd.concat([pd.DataFrame(v) for v in subtype_counts.values()], axis=1, sort=False)
counts_subtypes = counts_subtypes.fillna(0)

# Ajouter une colonne pour le compte total de cellules par ligne
counts_subtypes['total_cells'] = counts_subtypes.sum(axis=1)

# Enregistrement des counts des sous-types de cellules dans un fichier CSV
filename_subtypes = os.path.join(output_data_dir, project_name + "_cell_subtypes_number_by_scenes.csv")
counts_subtypes.to_csv(filename_subtypes, index=False)
counts_subtypes

dc       b  tcd4  tcd8   m1   m2  treg  immune_other  cancer  \
DD3S1.csv    81     0.0  2991  2849  310  129     6           994   48981   
DD3S2.csv   294     0.0  1915  2350   94   25    38          1261   51059   
DD3S3.csv   280   138.0  6857  3550  252   96    28          1874   77000   
DD4S1.csv   272    29.0  2667  1950   76   38    12          2389   54013   
DD4S2.csv   130    14.0  1938  1694  112  102    19           841   39470   
DD4S3.csv  1150    31.0  2353  2940  155  328    38          3336   50598   
DD5S1.csv   583   139.0  2840   536  504   28    28          1220   43723   
DD5S2.csv   160    16.0  1135   145  131   63    14           467   30839   
DD5S3.csv  1467    35.0  2000   687  479  110    13           865   30060   
TMA.csv     132  2309.0  5027   952  109   11   209           607   59978   

           αsma_mycaf  stroma_other  endothelial  total_cells  
DD3S1.csv        3967          6723         1666      68697.0  
DD3S2.csv        4789          7275         1750      70850.0  
DD3S3.csv        7424         15988         2778     116265.0  
DD4S1.csv        3106          4143         2053      70748.0  
DD4S2.csv        1664          4529         1232      51745.0  
DD4S3.csv        3686          4830         1373      70818.0  
DD5S1.csv        6976         10091         2795      69463.0  
DD5S2.csv        3876          7222         1335      45403.0  
DD5S3.csv        4831          4187         1164      45898.0  
TMA.csv          4875         18246         2287      94742.0

In [48]:
# Ajout des colonnes de pourcentages pour chaque sous-type de cellules
counts_perc = counts_subtypes.copy()

# Calcul des pourcentages pour chaque sous-type de cellules, en excluant la colonne 'total_cells'
for col in counts_subtypes.columns:
    if col != 'total_cells':
        counts_perc[col + '_perc'] = (counts_perc[col] / counts_perc['total_cells']) * 100

# Affichage des pourcentages des sous-types de cellules

counts_perc['Sample_ID'] = counts_perc.index
counts_perc.columns.values
display(counts_perc)


dc       b  tcd4  tcd8   m1   m2  treg  immune_other  cancer  \
DD3S1.csv    81     0.0  2991  2849  310  129     6           994   48981   
DD3S2.csv   294     0.0  1915  2350   94   25    38          1261   51059   
DD3S3.csv   280   138.0  6857  3550  252   96    28          1874   77000   
DD4S1.csv   272    29.0  2667  1950   76   38    12          2389   54013   
DD4S2.csv   130    14.0  1938  1694  112  102    19           841   39470   
DD4S3.csv  1150    31.0  2353  2940  155  328    38          3336   50598   
DD5S1.csv   583   139.0  2840   536  504   28    28          1220   43723   
DD5S2.csv   160    16.0  1135   145  131   63    14           467   30839   
DD5S3.csv  1467    35.0  2000   687  479  110    13           865   30060   
TMA.csv     132  2309.0  5027   952  109   11   209           607   59978   

           αsma_mycaf  ...  tcd8_perc   m1_perc   m2_perc  treg_perc  \
DD3S1.csv        3967  ...   4.147197  0.451257  0.187781   0.008734   
DD3S2.csv        4789  ...   3.316867  0.132675  0.035286   0.053634   
DD3S3.csv        7424  ...   3.053369  0.216746  0.082570   0.024083   
DD4S1.csv        3106  ...   2.756262  0.107424  0.053712   0.016962   
DD4S2.csv        1664  ...   3.273746  0.216446  0.197120   0.036719   
DD4S3.csv        3686  ...   4.151487  0.218871  0.463159   0.053659   
DD5S1.csv        6976  ...   0.771634  0.725566  0.040309   0.040309   
DD5S2.csv        3876  ...   0.319362  0.288527  0.138757   0.030835   
DD5S3.csv        4831  ...   1.496797  1.043618  0.239662   0.028324   
TMA.csv          4875  ...   1.004834  0.115049  0.011610   0.220599   

           immune_other_perc  cancer_perc  αsma_mycaf_perc  stroma_other_perc  \
DD3S1.csv           1.446934    71.300057         5.774634           9.786454   
DD3S2.csv           1.779817    72.066337         6.759351          10.268172   
DD3S3.csv           1.611835    66.228014         6.385413          13.751344   
DD4S1.csv           3.376774    76.345621         4.390230           5.855996   
DD4S2.csv           1.625278    76.277901         3.215770           8.752536   
DD4S3.csv           4.710667    71.447937         5.204891           6.820300   
DD5S1.csv           1.756331    62.944301        10.042757          14.527158   
DD5S2.csv           1.028566    67.922824         8.536881          15.906438   
DD5S3.csv           1.884614    65.493050        10.525513           9.122402   
TMA.csv             0.640687    63.306664         5.145553          19.258618   

           endothelial_perc  Sample_ID  
DD3S1.csv          2.425142  DD3S1.csv  
DD3S2.csv          2.470007  DD3S2.csv  
DD3S3.csv          2.389369  DD3S3.csv  
DD4S1.csv          2.901849  DD4S1.csv  
DD4S2.csv          2.380906  DD4S2.csv  
DD4S3.csv          1.938773  DD4S3.csv  
DD5S1.csv          4.023725  DD5S1.csv  
DD5S2.csv          2.940334  DD5S2.csv  
DD5S3.csv          2.536058  DD5S3.csv  
TMA.csv            2.413924    TMA.csv  

[10 rows x 26 columns]

In [49]:
fig = go.Figure()
title = 'Cell subtypes proportions by Sample ID and tissue type'

for cell_subtype in cell_subtypes:
    fig.add_trace(
        go.Bar(
            name=cell_subtype,
            x=counts_perc['Sample_ID'],
            y=counts_perc[f'{cell_subtype.lower()}_perc'],
            text=counts_perc[f'{cell_subtype.lower()}_perc'],
            textposition='auto',
            marker_color='rgb' + str(cell_subtype_color_dict[cell_subtype])))

fig.update_layout(
    plot_bgcolor='white',
    barmode='stack',
    title=title,
    xaxis=dict(linecolor='black'),
    yaxis=dict(title='Cell count (%)', linecolor='black')
)

# Enregistrer l'image
output_filename = title.replace(" ", "_") + ".png"
#fig.write_image(output_images_dir + "/" + output_filename, scale=1000)

# Afficher le graphique
fig.show()
plot(fig)

'temp-plot.html'

#### V.4.2.2 BY PATIENTS

In [50]:
df

PDL1_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_0                            -0.677863   
DD3S1_Cell_1                            -0.677863   
DD3S1_Cell_2                            -0.677863   
DD3S1_Cell_3                            -0.741282   
DD3S1_Cell_6                            -0.621521   
...                                           ...   
TMA_Cell_115755                          0.478275   
TMA_Cell_115756                          0.297418   
TMA_Cell_115757                          0.346950   
TMA_Cell_115758                         -0.189415   
TMA_Cell_115760                          0.245777   

                 HLA_Cytoplasm_Intensity_Average  \
ID                                                 
DD3S1_Cell_0                           -0.417494   
DD3S1_Cell_1                           -0.516487   
DD3S1_Cell_2                           -0.141921   
DD3S1_Cell_3                           -0.460472   
DD3S1_Cell_6                           -0.247254   
...                                          ...   
TMA_Cell_115755                         0.558670   
TMA_Cell_115756                         0.420594   
TMA_Cell_115757                         0.453951   
TMA_Cell_115758                         0.508840   
TMA_Cell_115760                         0.460219   

                 CKs_Cytoplasm_Intensity_Average  \
ID                                                 
DD3S1_Cell_0                           -0.912537   
DD3S1_Cell_1                           -0.838037   
DD3S1_Cell_2                           -1.016023   
DD3S1_Cell_3                           -0.491711   
DD3S1_Cell_6                           -0.867127   
...                                          ...   
TMA_Cell_115755                        -0.962840   
TMA_Cell_115756                        -0.971632   
TMA_Cell_115757                        -0.602893   
TMA_Cell_115758                        -0.886041   
TMA_Cell_115760                        -1.003840   

                 Ki67_Nucleus_Intensity_Average  \
ID                                                
DD3S1_Cell_0                          -0.817876   
DD3S1_Cell_1                          -0.869685   
DD3S1_Cell_2                          -0.755879   
DD3S1_Cell_3                          -0.818084   
DD3S1_Cell_6                          -0.742544   
...                                         ...   
TMA_Cell_115755                        1.732291   
TMA_Cell_115756                        1.966955   
TMA_Cell_115757                        1.338956   
TMA_Cell_115758                        0.647980   
TMA_Cell_115760                        0.191158   

                 CD163_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_0                              0.930099   
DD3S1_Cell_1                              1.114924   
DD3S1_Cell_2                              0.834577   
DD3S1_Cell_3                              0.648200   
DD3S1_Cell_6                              0.810579   
...                                            ...   
TMA_Cell_115755                           0.507434   
TMA_Cell_115756                           0.304365   
TMA_Cell_115757                           0.559435   
TMA_Cell_115758                          -0.227224   
TMA_Cell_115760                          -0.313127   

                 ColVI_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_0                              0.232078   
DD3S1_Cell_1                              0.301333   
DD3S1_Cell_2                              0.259216   
DD3S1_Cell_3                              0.107027   
DD3S1_Cell_6                              0.272128   
...                                            ...   
TMA_Cell_115755                          -0.912641   
TMA_Cell_115756                          -1.164112   
TMA_Cell_115757                          -0.801333   
TMA_Cell_115

In [51]:
# Compter par numéro de patiente
patient_counts = {}

# Boucle sur les sous-types de cellules pour compter les échantillons correspondants par patient
for subtype in cell_subtypes:
    patient_counts[subtype.lower()] = pd.DataFrame({subtype.lower():
        df.loc[
            df['cell_subtype'] == subtype, 'Patient'].value_counts()
    }).sort_index()

# Concaténation des counts des sous-types de cellules en un seul DataFrame
counts_patients = pd.concat([pd.DataFrame(v) for v in patient_counts.values()], axis=1, sort=False)
counts_patients = counts_patients.fillna(0)

# Ajout de la colonne de total de cellules comptées par patientes
counts_patients['Total_cells'] = counts_patients.sum(axis=1)
counts_patients = counts_patients[~counts_patients.index.str.startswith('c')]

# Enregistrement des counts des sous-types de cellules par patient dans un fichier CSV
filename_patients = os.path.join(output_data_dir, project_name + "_cell_subtypes_number_by_patient.csv")
counts_patients.to_csv(filename_patients, index=False)
counts_patients

dc    b   tcd4   tcd8     m1     m2  treg  immune_other  cancer  \
10    2.0  0.0  900.0   24.0  167.0  100.0   5.0          28.0  3981.0   
100  21.0  0.0   92.0   46.0    0.0    3.0   1.0          30.0  1449.0   
101   2.0  0.0   20.0   15.0    3.0    1.0   0.0          24.0  1896.0   
102   1.0  2.0   45.0   24.0    5.0    1.0   0.0          38.0  3564.0   
103  57.0  0.0   72.0  555.0    7.0    0.0   1.0          78.0  2157.0   
..    ...  ...    ...    ...    ...    ...   ...           ...     ...   
92    0.0  0.0   11.0  990.0    3.0   25.0   1.0         184.0   424.0   
96    0.0  0.0   76.0    2.0    2.0    1.0   0.0           4.0  1854.0   
97    0.0  0.0  174.0   38.0    0.0    0.0   1.0          56.0  2193.0   
60    0.0  0.0    0.0  107.0    9.0   16.0   1.0          57.0  1979.0   
62    0.0  0.0    0.0   23.0    3.0   15.0   0.0           4.0   151.0   

     αsma_mycaf  stroma_other  endothelial  Total_cells  
10        388.0         530.0        335.0       6460.0  
100        30.0          73.0        131.0       1876.0  
101        81.0         173.0         60.0       2275.0  
102        18.0          91.0         16.0       3805.0  
103        17.0         131.0        117.0       3192.0  
..          ...           ...          ...          ...  
92        140.0          22.0         15.0       1815.0  
96          1.0          16.0          3.0       1959.0  
97         28.0         163.0        102.0       2755.0  
60        107.0           1.0         32.0       2309.0  
62         91.0          20.0          3.0        310.0  

[177 rows x 13 columns]

In [52]:
# Ajout des colonnes de pourcentages pour chaque sous-type de cellules par patient
counts_perc_patients = counts_patients.copy()

# Calcul des pourcentages pour chaque sous-type de cellules, en excluant la colonne 'total_cells'
for col in counts_perc_patients.columns:
    if col != 'Total_cells':
        counts_perc_patients[col + '_perc'] = (counts_perc_patients[col] / counts_perc_patients['Total_cells']) * 100


# Affichage des pourcentages des sous-types de cellules par patient
counts_perc_patients['Patient'] = counts_perc_patients.index
counts_perc_patients.columns.values
counts_perc_patients = counts_perc_patients[~counts_perc_patients.index.str.startswith('c')]
counts_perc_patients

dc    b   tcd4   tcd8     m1     m2  treg  immune_other  cancer  \
10    2.0  0.0  900.0   24.0  167.0  100.0   5.0          28.0  3981.0   
100  21.0  0.0   92.0   46.0    0.0    3.0   1.0          30.0  1449.0   
101   2.0  0.0   20.0   15.0    3.0    1.0   0.0          24.0  1896.0   
102   1.0  2.0   45.0   24.0    5.0    1.0   0.0          38.0  3564.0   
103  57.0  0.0   72.0  555.0    7.0    0.0   1.0          78.0  2157.0   
..    ...  ...    ...    ...    ...    ...   ...           ...     ...   
92    0.0  0.0   11.0  990.0    3.0   25.0   1.0         184.0   424.0   
96    0.0  0.0   76.0    2.0    2.0    1.0   0.0           4.0  1854.0   
97    0.0  0.0  174.0   38.0    0.0    0.0   1.0          56.0  2193.0   
60    0.0  0.0    0.0  107.0    9.0   16.0   1.0          57.0  1979.0   
62    0.0  0.0    0.0   23.0    3.0   15.0   0.0           4.0   151.0   

     αsma_mycaf  ...  tcd8_perc   m1_perc   m2_perc  treg_perc  \
10        388.0  ...   0.371517  2.585139  1.547988   0.077399   
100        30.0  ...   2.452026  0.000000  0.159915   0.053305   
101        81.0  ...   0.659341  0.131868  0.043956   0.000000   
102        18.0  ...   0.630749  0.131406  0.026281   0.000000   
103        17.0  ...  17.387218  0.219298  0.000000   0.031328   
..          ...  ...        ...       ...       ...        ...   
92        140.0  ...  54.545455  0.165289  1.377410   0.055096   
96          1.0  ...   0.102093  0.102093  0.051046   0.000000   
97         28.0  ...   1.379310  0.000000  0.000000   0.036298   
60        107.0  ...   4.634041  0.389779  0.692941   0.043309   
62         91.0  ...   7.419355  0.967742  4.838710   0.000000   

     immune_other_perc  cancer_perc  αsma_mycaf_perc  stroma_other_perc  \
10            0.433437    61.625387         6.006192           8.204334   
100           1.599147    77.238806         1.599147           3.891258   
101           1.054945    83.340659         3.560440           7.604396   
102           0.998686    93.666229         0.473062           2.391590   
103           2.443609    67.575188         0.532581           4.104010   
..                 ...          ...              ...                ...   
92           10.137741    23.360882         7.713499           1.212121   
96            0.204186    94.640123         0.051046           0.816743   
97            2.032668    79.600726         1.016334           5.916515   
60            2.468601    85.708099         4.634041           0.043309   
62            1.290323    48.709677        29.354839           6.451613   

     endothelial_perc  Patient  
10           5.185759       10  
100          6.982942      100  
101          2.637363      101  
102          0.420499      102  
103          3.665414      103  
..                ...      ...  
92           0.826446       92  
96           0.153139       96  
97           3.702359       97  
60           1.385881       60  
62           0.967742       62  

[177 rows x 26 columns]

In [53]:
fig = go.Figure()
title = 'Cell subtypes proportions by Patient and tissue type'

for cell_subtype in cell_subtypes:
    fig.add_trace(
        go.Bar(
            name=cell_subtype,
            x=counts_perc_patients['Patient'],
            y=counts_perc_patients[f'{cell_subtype.lower()}_perc'],
            text=counts_perc_patients[f'{cell_subtype.lower()}_perc'],
            textposition='auto',
            marker_color='rgb' + str(cell_subtype_color_dict[cell_subtype])))

fig.update_layout(
    plot_bgcolor='white',
    barmode='stack',
    title=title,
    xaxis=dict(linecolor='black'),
    yaxis=dict(title='Cell count (%)', linecolor='black'))

output_filename = title.replace(" ", "_") + ".png"
#fig.write_image(output_images_dir + "/" + output_filename, scale=1000)

fig.show()
plot(fig)

'temp-plot.html'

#### V.4.2.3 BY SCENES AND PATIENTS

In [54]:
# Sélectionner les valeurs de 'Sample_ID' spécifiées
allowed_sample_ids = ['DD3S1.csv', 'DD3S2.csv', 'DD3S3.csv']

df_filtered = df[df['Sample_ID'].isin(allowed_sample_ids)]
df_filtered

# Compter par numéro de patiente
patient_counts = {}

# Boucle sur les sous-types de cellules pour compter les échantillons correspondants par patient
for subtype in cell_subtypes:
    patient_counts[subtype.lower()] = pd.DataFrame({subtype.lower():
        df_filtered.loc[
            df_filtered['cell_subtype'] == subtype, 'Patient'].value_counts()
    }).sort_index()

# Concaténation des counts des sous-types de cellules en un seul DataFrame
counts_patients = pd.concat([pd.DataFrame(v) for v in patient_counts.values()], axis=1, sort=False)
counts_patients = counts_patients.fillna(0)

# Ajout de la colonne de total de cellules comptées par patientes
counts_patients['Total_cells'] = counts_patients.sum(axis=1)


counts_patients

dc     b    tcd4    tcd8     m1     m2  treg  immune_other  cancer  \
10    2.0   0.0   900.0    24.0  167.0  100.0   5.0          28.0    3981   
11    1.0   0.0     7.0     5.0    0.0    0.0   0.0          26.0     556   
14    1.0   0.0   190.0     6.0    2.0    1.0   0.0          53.0    7142   
15    4.0   0.0    32.0     7.0    7.0    1.0   0.0          19.0    1823   
19   38.0   0.0   983.0   258.0    3.0    0.0   4.0          64.0    2322   
20    1.0   0.0    26.0    23.0    0.0    0.0   0.0         152.0    4317   
22    1.0  84.0     5.0   416.0   70.0    1.0   0.0          57.0    2447   
23   67.0   1.0   239.0   750.0    0.0    3.0   1.0         155.0    3370   
26    1.0   0.0   159.0    17.0    0.0    0.0   1.0          15.0    2950   
27    5.0   0.0    45.0     0.0    3.0    2.0   0.0          10.0    4522   
28    1.0   0.0    26.0    23.0    1.0    0.0   0.0          90.0     983   
30    7.0   0.0   986.0   148.0    3.0    0.0   5.0          74.0    1404   
32   30.0  16.0  1137.0   628.0   52.0   15.0   0.0         122.0    6327   
33   14.0   0.0    64.0    33.0    0.0    1.0   1.0          26.0    1187   
34   19.0   0.0    34.0   435.0    0.0    2.0   0.0         219.0    1426   
35   13.0   0.0     2.0   861.0   26.0   13.0   1.0          71.0     189   
36  107.0   0.0    68.0  1299.0    1.0    0.0   0.0         403.0    2805   
37    2.0   0.0     1.0    60.0    0.0    0.0   0.0          83.0    4356   
38    4.0   1.0    20.0    21.0    4.0    4.0   2.0          41.0    4806   
39   11.0   0.0   241.0    35.0    0.0    0.0   0.0          45.0    3889   
4    31.0   2.0  1730.0     1.0    1.0    4.0   1.0          23.0    1457   
41    2.0   0.0   153.0     6.0    0.0    0.0   2.0           2.0      71   
42   50.0   0.0   746.0   481.0   50.0   12.0  32.0         209.0    2968   
43    9.0   0.0    44.0    10.0    0.0    0.0   1.0           7.0     983   
44   12.0   0.0    48.0    14.0    0.0    0.0   0.0           4.0    3623   
45    9.0   0.0   277.0    24.0    0.0    3.0   0.0          80.0    4357   
46    9.0   0.0    37.0    22.0    3.0    0.0   0.0           9.0    2281   
5     1.0   1.0    66.0    40.0   78.0    6.0   0.0          55.0     393   
50    2.0   0.0   130.0    91.0    5.0    0.0   1.0          66.0    3155   
52   37.0   0.0    91.0     7.0   25.0    1.0   0.0         175.0    3656   
53  144.0   0.0    18.0    65.0    0.0    0.0   0.0          75.0    3079   
54    3.0   0.0     2.0  1133.0    3.0    2.0   0.0         340.0    4714   
57    6.0   0.0    69.0    62.0    0.0    0.0   0.0          43.0    5765   
58    1.0   0.0    17.0    39.0    0.0    0.0   1.0           6.0     134   
6     2.0   0.0   235.0     5.0    1.0    5.0   0.0          71.0    3275   
63    5.0   0.0   117.0    99.0    3.0    1.0   0.0          58.0    4629   
7     1.0   0.0   184.0    31.0    0.0    0.0   0.0          11.0     771   
8     2.0   0.0   704.0    18.0    0.0    0.0   4.0          28.0    4514   
18    0.0  27.0   328.0   395.0    1.0    0.0   2.0          83.0    8371   
25    0.0   1.0     5.0    53.0    0.0    2.0   0.0          42.0    1844   
29    0.0   2.0   105.0    27.0  101.0    3.0   1.0          59.0    2448   
3     0.0   3.0     6.0     7.0    0.0    0.0   0.0          17.0    1037   
12    0.0   0.0   318.0     6.0    2.0    0.0   2.0         153.0    7448   
13    0.0   0.0    39.0    28.0    0.0    1.0   0.0          21.0    1864   
16    0.0   0.0    45.0    41.0    0.0    3.0   0.0         119.0    5667   
17    0.0   0.0   220.0    35.0    2.0    0.0   1.0          28.0    4129   
21    0.0   0.0   234.0    91.0    0.0    0.0   0.0         177.0    7353   
24    0.0   0.0     3.0    45.0    1.0    0.0   0.0          27.0     463   
40    0.0   0.0    11.0     6.0    1.0    0.0   0.0          17.0    2274   
47    0.0   0.0    14.0    10.0    1.0    0.0   1.0          12.0    2740   
48    0.0   0.0    22.0    51.0    0.0    0.0   0.0          14.0    1252   
49 

In [55]:
# Filtrer counts_patients pour ne conserver que les lignes avec 'Sample_ID' égal à 'DD3S1.csv', 'DD3S2.csv' ou 'DD3S3.csv'
counts_patients_filtered = counts_patients[counts_patients.index.isin(df_filtered['Patient'])]

# Ajout des colonnes de pourcentages pour chaque sous-type de cellules par patient
counts_perc_patients = counts_patients_filtered.copy()

# Calcul des pourcentages pour chaque sous-type de cellules, en excluant la colonne 'total_cells'
for col in counts_perc_patients.columns:
    if col != 'Total_cells':
        counts_perc_patients[col + '_perc'] = (counts_perc_patients[col] / counts_perc_patients['Total_cells']) * 100


# Affichage des pourcentages des sous-types de cellules par patient
counts_perc_patients['Patient'] = counts_perc_patients.index
counts_perc_patients.columns.values
counts_perc_patients

dc     b    tcd4    tcd8     m1     m2  treg  immune_other  cancer  \
10    2.0   0.0   900.0    24.0  167.0  100.0   5.0          28.0    3981   
11    1.0   0.0     7.0     5.0    0.0    0.0   0.0          26.0     556   
14    1.0   0.0   190.0     6.0    2.0    1.0   0.0          53.0    7142   
15    4.0   0.0    32.0     7.0    7.0    1.0   0.0          19.0    1823   
19   38.0   0.0   983.0   258.0    3.0    0.0   4.0          64.0    2322   
20    1.0   0.0    26.0    23.0    0.0    0.0   0.0         152.0    4317   
22    1.0  84.0     5.0   416.0   70.0    1.0   0.0          57.0    2447   
23   67.0   1.0   239.0   750.0    0.0    3.0   1.0         155.0    3370   
26    1.0   0.0   159.0    17.0    0.0    0.0   1.0          15.0    2950   
27    5.0   0.0    45.0     0.0    3.0    2.0   0.0          10.0    4522   
28    1.0   0.0    26.0    23.0    1.0    0.0   0.0          90.0     983   
30    7.0   0.0   986.0   148.0    3.0    0.0   5.0          74.0    1404   
32   30.0  16.0  1137.0   628.0   52.0   15.0   0.0         122.0    6327   
33   14.0   0.0    64.0    33.0    0.0    1.0   1.0          26.0    1187   
34   19.0   0.0    34.0   435.0    0.0    2.0   0.0         219.0    1426   
35   13.0   0.0     2.0   861.0   26.0   13.0   1.0          71.0     189   
36  107.0   0.0    68.0  1299.0    1.0    0.0   0.0         403.0    2805   
37    2.0   0.0     1.0    60.0    0.0    0.0   0.0          83.0    4356   
38    4.0   1.0    20.0    21.0    4.0    4.0   2.0          41.0    4806   
39   11.0   0.0   241.0    35.0    0.0    0.0   0.0          45.0    3889   
4    31.0   2.0  1730.0     1.0    1.0    4.0   1.0          23.0    1457   
41    2.0   0.0   153.0     6.0    0.0    0.0   2.0           2.0      71   
42   50.0   0.0   746.0   481.0   50.0   12.0  32.0         209.0    2968   
43    9.0   0.0    44.0    10.0    0.0    0.0   1.0           7.0     983   
44   12.0   0.0    48.0    14.0    0.0    0.0   0.0           4.0    3623   
45    9.0   0.0   277.0    24.0    0.0    3.0   0.0          80.0    4357   
46    9.0   0.0    37.0    22.0    3.0    0.0   0.0           9.0    2281   
5     1.0   1.0    66.0    40.0   78.0    6.0   0.0          55.0     393   
50    2.0   0.0   130.0    91.0    5.0    0.0   1.0          66.0    3155   
52   37.0   0.0    91.0     7.0   25.0    1.0   0.0         175.0    3656   
53  144.0   0.0    18.0    65.0    0.0    0.0   0.0          75.0    3079   
54    3.0   0.0     2.0  1133.0    3.0    2.0   0.0         340.0    4714   
57    6.0   0.0    69.0    62.0    0.0    0.0   0.0          43.0    5765   
58    1.0   0.0    17.0    39.0    0.0    0.0   1.0           6.0     134   
6     2.0   0.0   235.0     5.0    1.0    5.0   0.0          71.0    3275   
63    5.0   0.0   117.0    99.0    3.0    1.0   0.0          58.0    4629   
7     1.0   0.0   184.0    31.0    0.0    0.0   0.0          11.0     771   
8     2.0   0.0   704.0    18.0    0.0    0.0   4.0          28.0    4514   
18    0.0  27.0   328.0   395.0    1.0    0.0   2.0          83.0    8371   
25    0.0   1.0     5.0    53.0    0.0    2.0   0.0          42.0    1844   
29    0.0   2.0   105.0    27.0  101.0    3.0   1.0          59.0    2448   
3     0.0   3.0     6.0     7.0    0.0    0.0   0.0          17.0    1037   
12    0.0   0.0   318.0     6.0    2.0    0.0   2.0         153.0    7448   
13    0.0   0.0    39.0    28.0    0.0    1.0   0.0          21.0    1864   
16    0.0   0.0    45.0    41.0    0.0    3.0   0.0         119.0    5667   
17    0.0   0.0   220.0    35.0    2.0    0.0   1.0          28.0    4129   
21    0.0   0.0   234.0    91.0    0.0    0.0   0.0         177.0    7353   
24    0.0   0.0     3.0    45.0    1.0    0.0   0.0          27.0     463   
40    0.0   0.0    11.0     6.0    1.0    0.0   0.0          17.0    2274   
47    0.0   0.0    14.0    10.0    1.0    0.0   1.0          12.0    2740   
48    0.0   0.0    22.0    51.0    0.0    0.0   0.0          14.0    1252   
49 

In [56]:
fig = go.Figure()
title = 'Cell subtypes proportions by Patient and tissue type DD3'

for cell_subtype in cell_subtypes:
    fig.add_trace(
        go.Bar(
            name=cell_subtype,
            x=counts_perc_patients['Patient'],
            y=counts_perc_patients[f'{cell_subtype.lower()}_perc'],
            text=counts_perc_patients[f'{cell_subtype.lower()}_perc'],
            textposition='auto',
            marker_color='rgb' + str(cell_subtype_color_dict[cell_subtype])))

fig.update_layout(
    plot_bgcolor='white',
    barmode='stack',
    title=title,
    xaxis=dict(linecolor='black'),
    yaxis=dict(title='Cell count (%)', linecolor='black'))

output_filename = title.replace(" ", "_") + ".png"
#fig.write_image(output_images_dir + "/" + output_filename, scale=1000)

fig.show()
plot(fig)

'temp-plot.html'

#### V.4.3.4 BY TREATMENT

In [57]:
df_NACT

PDL1_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_0                             -0.677863   
DD3S1_Cell_1                             -0.677863   
DD3S1_Cell_2                             -0.677863   
DD3S1_Cell_3                             -0.741282   
DD3S1_Cell_6                             -0.621521   
...                                            ...   
DD5S3_Cell_62826                         -0.446025   
DD5S3_Cell_62828                         -0.414440   
DD5S3_Cell_62829                         -0.720569   
DD5S3_Cell_62830                         -0.442500   
DD5S3_Cell_62831                          0.040892   

                  HLA_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_0                            -0.417494   
DD3S1_Cell_1                            -0.516487   
DD3S1_Cell_2                            -0.141921   
DD3S1_Cell_3                            -0.460472   
DD3S1_Cell_6                            -0.247254   
...                                           ...   
DD5S3_Cell_62826                         0.480212   
DD5S3_Cell_62828                         0.416668   
DD5S3_Cell_62829                         0.072144   
DD5S3_Cell_62830                         0.368654   
DD5S3_Cell_62831                         1.166606   

                  CKs_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_0                            -0.912537   
DD3S1_Cell_1                            -0.838037   
DD3S1_Cell_2                            -1.016023   
DD3S1_Cell_3                            -0.491711   
DD3S1_Cell_6                            -0.867127   
...                                           ...   
DD5S3_Cell_62826                         1.195440   
DD5S3_Cell_62828                         1.542926   
DD5S3_Cell_62829                        -0.311962   
DD5S3_Cell_62830                        -1.491754   
DD5S3_Cell_62831                        -1.676753   

                  Ki67_Nucleus_Intensity_Average  \
ID                                                 
DD3S1_Cell_0                           -0.817876   
DD3S1_Cell_1                           -0.869685   
DD3S1_Cell_2                           -0.755879   
DD3S1_Cell_3                           -0.818084   
DD3S1_Cell_6                           -0.742544   
...                                          ...   
DD5S3_Cell_62826                       -0.081463   
DD5S3_Cell_62828                       -0.203248   
DD5S3_Cell_62829                       -0.481442   
DD5S3_Cell_62830                       -0.316270   
DD5S3_Cell_62831                        0.249586   

                  CD163_Cytoplasm_Intensity_Average  \
ID                                                    
DD3S1_Cell_0                               0.930099   
DD3S1_Cell_1                               1.114924   
DD3S1_Cell_2                               0.834577   
DD3S1_Cell_3                               0.648200   
DD3S1_Cell_6                               0.810579   
...                                             ...   
DD5S3_Cell_62826                          -0.634343   
DD5S3_Cell_62828                          -0.076555   
DD5S3_Cell_62829                           1.236053   
DD5S3_Cell_62830                           0.029502   
DD5S3_Cell_62831                          -1.486438   

                  ColVI_Cytoplasm_Intensity_Average  \
ID                                                    
DD3S1_Cell_0                               0.232078   
DD3S1_Cell_1                               0.301333   
DD3S1_Cell_2                               0.259216   
DD3S1_Cell_3                               0.107027   
DD3S1_Cell_6                               0.272128   
...                                             ...   
DD5S3_Cell_62826                          -0.883815   
DD5S3_Cell_62828                          -0.78

In [58]:
# Extraire les valeurs uniques de la colonne 'Patient'
num_NACT_patients = df_NACT['Patient'].unique()
num_ACT_patients = df_ACT['Patient'].unique()

# Numéros des patientes qui ont reçu le traitement
print(num_NACT_patients)
print(num_ACT_patients)

['61' '32' '26' '15' '18' '11' '5' '51' '40' '7' '95' '121' '85' '111'
 '116' '98' '119' '104' '89' '140' '137' '153' '149' '146' '162' '160'
 '157' '171' '169' '183' '182' '179' '177' '174' '178' '187' '184' '141']
['62' '63' '59' '60' '33' '35' '36' '37' '38' '30' '25' '27' '29' '20'
 '21' '22' '23' '24' '14' '16' '17' '19' '12' '8' '9' '10' '4' '52' '53'
 '54' '55' '56' '57' '50' '42' '43' '44' '45' '47' '39' '41' '49' '46'
 '48' '58' '28' '13' '6' '34' '3' '122' '125' '124' '94' '101' '86' '84'
 '83' '91' '88' '87' '75' '74' '82' '81' '80' '79' '67' '66' '65' '64'
 '73' '71' '69' '68' '123' '115' '114' '113' '120' '117' '126' '105' '103'
 '102' '110' '109' '106' '166' '112' '108' '107' '97' '96' '100' '78' '77'
 '70' '72' '99' '92' '90' '136' '135' '134' '133' '132' '131' '130' '129'
 '144' '143' '155' '154' '150' '148' '147' '164' '161' '159' '128' '127'
 '142' '139' '152' '158' '156' '172' '170' '168' '167' '165' '181' '180'
 '176' '173' '175' '185' '186']


##### V.4.3.4.1 NACT

In [59]:
# Compter par numéro de patiente pour les patientes NACT uniquement
patient_counts = {}

# Boucle sur les sous-types de cellules pour compter les échantillons correspondants par patient
for subtype in cell_subtypes:
    patient_counts[subtype.lower()] = pd.DataFrame({subtype.lower():
        df.loc[
            (df['cell_subtype'] == subtype) & (df['Patient'].isin(num_NACT_patients)), 'Patient'].value_counts()
    }).sort_index()

# Concaténation des counts des sous-types de cellules en un seul DataFrame
counts_patients = pd.concat([pd.DataFrame(v) for v in patient_counts.values()], axis=1, sort=False)
counts_patients = counts_patients.fillna(0)

# Ajout de la colonne de total de cellules comptées par patientes
counts_patients['Total_cells'] = counts_patients.sum(axis=1)

# Enregistrement des counts des sous-types de cellules par patient dans un fichier CSV
filename_patients = os.path.join(output_data_dir, project_name + "_cell_subtypes_number_by_patient_NACT.csv")
counts_patients.to_csv(filename_patients, index=False)
counts_patients


dc     b  tcd4   tcd8     m1    m2  treg  immune_other  cancer  \
11     1.0   0.0     7    5.0    0.0   0.0   0.0          26.0     556   
111   27.0   1.0     2   30.0   10.0   3.0   1.0          39.0     899   
116    3.0   0.0     4    2.0    0.0   0.0   0.0           1.0     125   
119    1.0   0.0    60    9.0    3.0   0.0   0.0          17.0    4289   
121   15.0   2.0   704   54.0    4.0   0.0   2.0         350.0    3652   
137    2.0   0.0    21   22.0    1.0   1.0   2.0          28.0    1302   
140  402.0   0.0   385    6.0  307.0  38.0   3.0           6.0      35   
141   42.0   0.0   158   21.0   10.0   1.0   0.0          25.0      71   
146    6.0   0.0    80    3.0    1.0   2.0   0.0          52.0     916   
149   20.0   0.0   270   25.0  275.0   3.0   0.0         265.0     735   
15     4.0   0.0    32    7.0    7.0   1.0   0.0          19.0    1823   
153    2.0   1.0   567   24.0   61.0  14.0   3.0         283.0    1580   
157   12.0   1.0    16  173.0    2.0   7.0   0.0          89.0    2463   
162    6.0   1.0    76    3.0    1.0   0.0   1.0          31.0    2321   
169   68.0   0.0   202   21.0    1.0   0.0   1.0          17.0    1564   
174    1.0   0.0    24    4.0    1.0   0.0   0.0          46.0     295   
177    1.0   0.0   131    0.0    1.0   0.0   0.0          28.0     259   
182    5.0   1.0    15    4.0    0.0   3.0   0.0          80.0     610   
183    6.0   0.0    46    3.0    0.0   1.0   4.0           8.0     557   
184   39.0   0.0    46    1.0   13.0  11.0   1.0           1.0    1708   
187    4.0   0.0    27   21.0    2.0   8.0   2.0          45.0    2599   
26     1.0   0.0   159   17.0    0.0   0.0   1.0          15.0    2950   
32    30.0  16.0  1137  628.0   52.0  15.0   0.0         122.0    6327   
5      1.0   1.0    66   40.0   78.0   6.0   0.0          55.0     393   
7      1.0   0.0   184   31.0    0.0   0.0   0.0          11.0     771   
85    32.0   0.0   216   22.0   41.0  16.0   0.0         309.0    4273   
89    18.0   0.0   253   17.0   22.0   8.0   5.0         194.0    2490   
95    37.0   1.0    69  166.0    5.0  44.0   1.0         549.0    1851   
98    25.0   0.0   790   72.0   73.0  70.0   2.0          81.0    2156   
104    0.0   1.0   169   30.0    1.0   2.0   3.0          69.0    1600   
18     0.0  27.0   328  395.0    1.0   0.0   2.0          83.0    8371   
160    0.0   0.0     5    2.0    0.0   0.0   0.0          30.0    1121   
171    0.0   0.0    95   28.0   25.0   1.0   0.0          67.0     523   
178    0.0   0.0     1    0.0    0.0   0.0   0.0           3.0    1613   
179    0.0   0.0    13    1.0    0.0   0.0   2.0           3.0     312   
40     0.0   0.0    11    6.0    1.0   0.0   0.0          17.0    2274   
51     0.0   0.0     4    1.0    1.0   0.0   1.0           0.0      11   
61     0.0   0.0    79  144.0    4.0  19.0   0.0          37.0     958   

     αsma_mycaf  stroma_other  endothelial  Total_cells  
11          409          5103           87       6194.0  
111           1             3           10       1026.0  
116           4            56            3        198.0  
119          16           104           34       4533.0  
121         183           236          587       5789.0  
137         409           202          101       2091.0  
140          66           293           51       1592.0  
141         565           154           73       1120.0  
146          89           331           98       1578.0  
149        1250           425          111       3379.0  
15          747           232           86       2958.0  
153         415           823          348       4121.0  
157         132            45           29       2969.0  
162         609           998          313       4360.0  
169         222           594          221       2911.0  
174        1203           224           22       1820.0  
177         768           275          457       1920.0  
182           2           102           37        859.0  
183          12    

In [60]:
# Ajout des colonnes de pourcentages pour chaque sous-type de cellules par patient
counts_perc_patients = counts_patients.copy()

# Calcul des pourcentages pour chaque sous-type de cellules, en excluant la colonne 'total_cells'
for col in counts_perc_patients.columns:
    if col != 'Total_cells':
        counts_perc_patients[col + '_perc'] = (counts_perc_patients[col] / counts_perc_patients['Total_cells']) * 100


# Affichage des pourcentages des sous-types de cellules par patient
counts_perc_patients['Patient'] = counts_perc_patients.index
counts_perc_patients.columns.values
counts_perc_patients



dc     b  tcd4   tcd8     m1    m2  treg  immune_other  cancer  \
11     1.0   0.0     7    5.0    0.0   0.0   0.0          26.0     556   
111   27.0   1.0     2   30.0   10.0   3.0   1.0          39.0     899   
116    3.0   0.0     4    2.0    0.0   0.0   0.0           1.0     125   
119    1.0   0.0    60    9.0    3.0   0.0   0.0          17.0    4289   
121   15.0   2.0   704   54.0    4.0   0.0   2.0         350.0    3652   
137    2.0   0.0    21   22.0    1.0   1.0   2.0          28.0    1302   
140  402.0   0.0   385    6.0  307.0  38.0   3.0           6.0      35   
141   42.0   0.0   158   21.0   10.0   1.0   0.0          25.0      71   
146    6.0   0.0    80    3.0    1.0   2.0   0.0          52.0     916   
149   20.0   0.0   270   25.0  275.0   3.0   0.0         265.0     735   
15     4.0   0.0    32    7.0    7.0   1.0   0.0          19.0    1823   
153    2.0   1.0   567   24.0   61.0  14.0   3.0         283.0    1580   
157   12.0   1.0    16  173.0    2.0   7.0   0.0          89.0    2463   
162    6.0   1.0    76    3.0    1.0   0.0   1.0          31.0    2321   
169   68.0   0.0   202   21.0    1.0   0.0   1.0          17.0    1564   
174    1.0   0.0    24    4.0    1.0   0.0   0.0          46.0     295   
177    1.0   0.0   131    0.0    1.0   0.0   0.0          28.0     259   
182    5.0   1.0    15    4.0    0.0   3.0   0.0          80.0     610   
183    6.0   0.0    46    3.0    0.0   1.0   4.0           8.0     557   
184   39.0   0.0    46    1.0   13.0  11.0   1.0           1.0    1708   
187    4.0   0.0    27   21.0    2.0   8.0   2.0          45.0    2599   
26     1.0   0.0   159   17.0    0.0   0.0   1.0          15.0    2950   
32    30.0  16.0  1137  628.0   52.0  15.0   0.0         122.0    6327   
5      1.0   1.0    66   40.0   78.0   6.0   0.0          55.0     393   
7      1.0   0.0   184   31.0    0.0   0.0   0.0          11.0     771   
85    32.0   0.0   216   22.0   41.0  16.0   0.0         309.0    4273   
89    18.0   0.0   253   17.0   22.0   8.0   5.0         194.0    2490   
95    37.0   1.0    69  166.0    5.0  44.0   1.0         549.0    1851   
98    25.0   0.0   790   72.0   73.0  70.0   2.0          81.0    2156   
104    0.0   1.0   169   30.0    1.0   2.0   3.0          69.0    1600   
18     0.0  27.0   328  395.0    1.0   0.0   2.0          83.0    8371   
160    0.0   0.0     5    2.0    0.0   0.0   0.0          30.0    1121   
171    0.0   0.0    95   28.0   25.0   1.0   0.0          67.0     523   
178    0.0   0.0     1    0.0    0.0   0.0   0.0           3.0    1613   
179    0.0   0.0    13    1.0    0.0   0.0   2.0           3.0     312   
40     0.0   0.0    11    6.0    1.0   0.0   0.0          17.0    2274   
51     0.0   0.0     4    1.0    1.0   0.0   1.0           0.0      11   
61     0.0   0.0    79  144.0    4.0  19.0   0.0          37.0     958   

     αsma_mycaf  ...  tcd8_perc    m1_perc   m2_perc  treg_perc  \
11          409  ...   0.080723   0.000000  0.000000   0.000000   
111           1  ...   2.923977   0.974659  0.292398   0.097466   
116           4  ...   1.010101   0.000000  0.000000   0.000000   
119          16  ...   0.198544   0.066181  0.000000   0.000000   
121         183  ...   0.932804   0.069097  0.000000   0.034548   
137         409  ...   1.052128   0.047824  0.047824   0.095648   
140          66  ...   0.376884  19.283920  2.386935   0.188442   
141         565  ...   1.875000   0.892857  0.089286   0.000000   
146          89  ...   0.190114   0.063371  0.126743   0.000000   
149        1250  ...   0.739864   8.138503  0.088784   0.000000   
15          747  ...   0.236646   0.236646  0.033807   0.000000   
153         415  ...   0.582383   1.480223  0.339723   0.072798   
157         132  ...   5.826878   0.067363  0.235770   0.000000   
162         609  ...   0.068807   0.022936  0.000000   0.022936   
169         222  ...   0.721402   0.034352  0.000000   0.034352   
174        1203  ...   0.219780   0.054945  0.000

In [61]:
counts_perc_patients_NACT = counts_perc_patients

In [62]:
fig = go.Figure()
title = 'Cell subtypes proportions by Patient and tissue type - NACT group'

for cell_subtype in cell_subtypes:
    fig.add_trace(
        go.Bar(
            name=cell_subtype,
            x=counts_perc_patients['Patient'],
            y=counts_perc_patients[f'{cell_subtype.lower()}_perc'],
            text=counts_perc_patients[f'{cell_subtype.lower()}_perc'],
            textposition='auto',
            marker_color='rgb' + str(cell_subtype_color_dict[cell_subtype])))

fig.update_layout(
    plot_bgcolor='white',
    barmode='stack',
    title=title,
    xaxis=dict(linecolor='black'),
    yaxis=dict(title='Cell count (%)', linecolor='black'))

output_filename = title.replace(" ", "_") + ".png"
#fig.write_image(output_images_dir + "/" + output_filename, scale=1000)

fig.show()
plot(fig)

'temp-plot.html'

##### V.4.3.4.1 ACT

In [63]:
# Compter par numéro de patiente pour les patientes ACT uniquement
patient_counts = {}

# Boucle sur les sous-types de cellules pour compter les échantillons correspondants par patient
for subtype in cell_subtypes:
    patient_counts[subtype.lower()] = pd.DataFrame({subtype.lower():
        df.loc[
            (df['cell_subtype'] == subtype) & (df['Patient'].isin(num_ACT_patients)), 'Patient'].value_counts()
    }).sort_index()

# Concaténation des counts des sous-types de cellules en un seul DataFrame
counts_patients = pd.concat([pd.DataFrame(v) for v in patient_counts.values()], axis=1, sort=False)
counts_patients = counts_patients.fillna(0)

# Ajout de la colonne de total de cellules comptées par patientes
counts_patients['Total_cells'] = counts_patients.sum(axis=1)

# Enregistrement des counts des sous-types de cellules par patient dans un fichier CSV
filename_patients = os.path.join(output_data_dir, project_name + "_cell_subtypes_number_by_patient_ACT.csv")
counts_patients.to_csv(filename_patients, index=False)
counts_patients

dc    b   tcd4   tcd8     m1     m2  treg  immune_other  cancer  \
10    2.0  0.0  900.0   24.0  167.0  100.0   5.0          28.0    3981   
100  21.0  0.0   92.0   46.0    0.0    3.0   1.0          30.0    1449   
101   2.0  0.0   20.0   15.0    3.0    1.0   0.0          24.0    1896   
102   1.0  2.0   45.0   24.0    5.0    1.0   0.0          38.0    3564   
103  57.0  0.0   72.0  555.0    7.0    0.0   1.0          78.0    2157   
..    ...  ...    ...    ...    ...    ...   ...           ...     ...   
92    0.0  0.0   11.0  990.0    3.0   25.0   1.0         184.0     424   
96    0.0  0.0   76.0    2.0    2.0    1.0   0.0           4.0    1854   
97    0.0  0.0  174.0   38.0    0.0    0.0   1.0          56.0    2193   
60    0.0  0.0    0.0  107.0    9.0   16.0   1.0          57.0    1979   
62    0.0  0.0    0.0   23.0    3.0   15.0   0.0           4.0     151   

     αsma_mycaf  stroma_other  endothelial  Total_cells  
10        388.0           530        335.0       6460.0  
100        30.0            73        131.0       1876.0  
101        81.0           173         60.0       2275.0  
102        18.0            91         16.0       3805.0  
103        17.0           131        117.0       3192.0  
..          ...           ...          ...          ...  
92        140.0            22         15.0       1815.0  
96          1.0            16          3.0       1959.0  
97         28.0           163        102.0       2755.0  
60        107.0             1         32.0       2309.0  
62         91.0            20          3.0        310.0  

[139 rows x 13 columns]

In [64]:
# Ajout des colonnes de pourcentages pour chaque sous-type de cellules par patient
counts_perc_patients = counts_patients.copy()

# Calcul des pourcentages pour chaque sous-type de cellules, en excluant la colonne 'total_cells'
for col in counts_perc_patients.columns:
    if col != 'Total_cells':
        counts_perc_patients[col + '_perc'] = (counts_perc_patients[col] / counts_perc_patients['Total_cells']) * 100


# Affichage des pourcentages des sous-types de cellules par patient
counts_perc_patients['Patient'] = counts_perc_patients.index
counts_perc_patients.columns.values
counts_perc_patients



dc    b   tcd4   tcd8     m1     m2  treg  immune_other  cancer  \
10    2.0  0.0  900.0   24.0  167.0  100.0   5.0          28.0    3981   
100  21.0  0.0   92.0   46.0    0.0    3.0   1.0          30.0    1449   
101   2.0  0.0   20.0   15.0    3.0    1.0   0.0          24.0    1896   
102   1.0  2.0   45.0   24.0    5.0    1.0   0.0          38.0    3564   
103  57.0  0.0   72.0  555.0    7.0    0.0   1.0          78.0    2157   
..    ...  ...    ...    ...    ...    ...   ...           ...     ...   
92    0.0  0.0   11.0  990.0    3.0   25.0   1.0         184.0     424   
96    0.0  0.0   76.0    2.0    2.0    1.0   0.0           4.0    1854   
97    0.0  0.0  174.0   38.0    0.0    0.0   1.0          56.0    2193   
60    0.0  0.0    0.0  107.0    9.0   16.0   1.0          57.0    1979   
62    0.0  0.0    0.0   23.0    3.0   15.0   0.0           4.0     151   

     αsma_mycaf  ...  tcd8_perc   m1_perc   m2_perc  treg_perc  \
10        388.0  ...   0.371517  2.585139  1.547988   0.077399   
100        30.0  ...   2.452026  0.000000  0.159915   0.053305   
101        81.0  ...   0.659341  0.131868  0.043956   0.000000   
102        18.0  ...   0.630749  0.131406  0.026281   0.000000   
103        17.0  ...  17.387218  0.219298  0.000000   0.031328   
..          ...  ...        ...       ...       ...        ...   
92        140.0  ...  54.545455  0.165289  1.377410   0.055096   
96          1.0  ...   0.102093  0.102093  0.051046   0.000000   
97         28.0  ...   1.379310  0.000000  0.000000   0.036298   
60        107.0  ...   4.634041  0.389779  0.692941   0.043309   
62         91.0  ...   7.419355  0.967742  4.838710   0.000000   

     immune_other_perc  cancer_perc  αsma_mycaf_perc  stroma_other_perc  \
10            0.433437    61.625387         6.006192           8.204334   
100           1.599147    77.238806         1.599147           3.891258   
101           1.054945    83.340659         3.560440           7.604396   
102           0.998686    93.666229         0.473062           2.391590   
103           2.443609    67.575188         0.532581           4.104010   
..                 ...          ...              ...                ...   
92           10.137741    23.360882         7.713499           1.212121   
96            0.204186    94.640123         0.051046           0.816743   
97            2.032668    79.600726         1.016334           5.916515   
60            2.468601    85.708099         4.634041           0.043309   
62            1.290323    48.709677        29.354839           6.451613   

     endothelial_perc  Patient  
10           5.185759       10  
100          6.982942      100  
101          2.637363      101  
102          0.420499      102  
103          3.665414      103  
..                ...      ...  
92           0.826446       92  
96           0.153139       96  
97           3.702359       97  
60           1.385881       60  
62           0.967742       62  

[139 rows x 26 columns]

In [65]:
counts_perc_patients_ACT = counts_perc_patients

In [66]:
fig = go.Figure()
title = 'Cell subtypes proportions by Patient and tissue type - ACT group'

for cell_subtype in cell_subtypes:
    fig.add_trace(
        go.Bar(
            name=cell_subtype,
            x=counts_perc_patients['Patient'],
            y=counts_perc_patients[f'{cell_subtype.lower()}_perc'],
            text=counts_perc_patients[f'{cell_subtype.lower()}_perc'],
            textposition='auto',
            marker_color='rgb' + str(cell_subtype_color_dict[cell_subtype])))

fig.update_layout(
    plot_bgcolor='white',
    barmode='stack',
    title=title,
    xaxis=dict(linecolor='black'),
    yaxis=dict(title='Cell count (%)', linecolor='black'))

output_filename = title.replace(" ", "_") + ".png"
#fig.write_image(output_images_dir + "/" + output_filename, scale=1000)

fig.show()
plot(fig)

'temp-plot.html'

In [67]:
from scipy.stats import mannwhitneyu


# Choisissez la colonne sur laquelle vous voulez effectuer la comparaison
column_to_compare = 'm2'

# Effectuez le test de Mann-Whitney
statistic, p_value = mannwhitneyu(counts_perc_patients_NACT[column_to_compare], counts_perc_patients_ACT[column_to_compare])

# Affichez les résultats
print("Statistique de test de Mann-Whitney :", statistic)
print("P-value associée :", p_value)

# Interprétez les résultats
alpha = 0.05
if p_value < alpha:
    print("La différence entre les groupes est statistiquement significative.")
else:
    print("Il n'y a pas de différence statistiquement significative entre les groupes.")

Statistique de test de Mann-Whitney : 2845.0
P-value associée : 0.44739619874878456
Il n'y a pas de différence statistiquement significative entre les groupes.


In [68]:
import plotly.graph_objs as go

# Données à comparer
data1 = counts_perc_patients_NACT[column_to_compare]
data2 = counts_perc_patients_ACT[column_to_compare]

# Créer un graphique boxplot
fig = go.Figure()

# Ajouter les données de chaque groupe au graphique
fig.add_trace(go.Violin(y=data1, name='NACT', box_visible=True, meanline_visible=True))
fig.add_trace(go.Violin(y=data2, name='ACT', box_visible=True, meanline_visible=True))

# Mettre en forme le titre et les axes
fig.update_layout(
    title="Comparaison de la distribution de '{}' entre les groupes NACT et ACT".format(column_to_compare),
    xaxis_title="Groupe",
    yaxis_title="Valeurs de '{}'".format(column_to_compare)
)

# Afficher le graphique
fig.show()

plot(fig)

'temp-plot.html'

In [69]:
# Compter le nombre d'occurrences des checkpoints immunitaires par patiente
occurrences_checkpoint_NACT = df_NACT.groupby('Patient')['immune_checkpoint'].value_counts()
occurrences_checkpoint_ACT = df_ACT.groupby('Patient')['immune_checkpoint'].value_counts()

# Afficher le résultat
print(occurrences_checkpoint_NACT)
print(occurrences_checkpoint_ACT)

Patient  immune_checkpoint
104      None                 2461
         PDL1                   20
         PD1                    10
11       None                 6138
         PDL1                   50
                              ... 
95       B7H4_PDL1               1
98       None                 2901
         B7H4                  487
         PDL1                  321
         PD1                     1
Name: immune_checkpoint, Length: 155, dtype: int64
Patient  immune_checkpoint
10       None                 6427
         B7H4                   23
         PD1                     5
         PDL1                    4
         B7H4_PD1                1
                              ... 
97       B7H4                    2
99       None                 1064
         B7H4                  182
         PD1                    13
         PDL1                    6
Name: immune_checkpoint, Length: 583, dtype: int64


In [70]:
from scipy.stats import chi2_contingency

# Créer un tableau de contingence à partir des occurrences de checkpoints immunitaires dans chaque tableau
contingency_table = pd.concat([occurrences_checkpoint_NACT, occurrences_checkpoint_ACT], axis=1, keys=['NACT', 'ACT'], sort=False).fillna(0)

# Effectuer le test de chi-deux
chi2_stat, p_val, _, _ = chi2_contingency(contingency_table)

# Afficher les résultats
print("Statistique de test de chi-deux :", chi2_stat)
print("P-valeur associée :", p_val)

# Interpréter les résultats
alpha = 0.05
if p_val < alpha:
    print("Il y a une différence statistiquement significative entre les distributions des checkpoints immunitaires dans les deux groupes.")
else:
    print("Il n'y a pas de différence statistiquement significative entre les distributions des checkpoints immunitaires dans les deux groupes.")


Statistique de test de chi-deux : 609887.0
P-valeur associée : 0.0
Il y a une différence statistiquement significative entre les distributions des checkpoints immunitaires dans les deux groupes.


In [71]:
import plotly.graph_objs as go

# Concaténer les occurrences des checkpoints immunitaires dans les deux tableaux
all_occurrences = pd.concat([occurrences_checkpoint_NACT, occurrences_checkpoint_ACT], axis=1, keys=['NACT', 'ACT'], sort=False).fillna(0)

# Calculer le nombre total de patientes dans chaque groupe
total_patients_NACT = len(df_NACT['Patient'].unique())
total_patients_ACT = len(df_ACT['Patient'].unique())

# Diviser le nombre d'occurrences de chaque checkpoint immunitaire par le nombre total de patientes dans le groupe correspondant
all_occurrences_normalized = all_occurrences.copy()
all_occurrences_normalized['NACT'] /= total_patients_NACT
all_occurrences_normalized['ACT'] /= total_patients_ACT

all_occurrences_normalized

NACT       ACT
Patient immune_checkpoint                      
104     None                64.763158  0.000000
        PDL1                 0.526316  0.000000
        PD1                  0.263158  0.000000
11      None               161.526316  0.000000
        PDL1                 1.315789  0.000000
...                               ...       ...
97      B7H4                 0.000000  0.014388
99      None                 0.000000  7.654676
        B7H4                 0.000000  1.309353
        PD1                  0.000000  0.093525
        PDL1                 0.000000  0.043165

[738 rows x 2 columns]

In [72]:
df_ACT['Patient'].unique()

array(['62', '63', '59', '60', '33', '35', '36', '37', '38', '30', '25',
       '27', '29', '20', '21', '22', '23', '24', '14', '16', '17', '19',
       '12', '8', '9', '10', '4', '52', '53', '54', '55', '56', '57',
       '50', '42', '43', '44', '45', '47', '39', '41', '49', '46', '48',
       '58', '28', '13', '6', '34', '3', '122', '125', '124', '94', '101',
       '86', '84', '83', '91', '88', '87', '75', '74', '82', '81', '80',
       '79', '67', '66', '65', '64', '73', '71', '69', '68', '123', '115',
       '114', '113', '120', '117', '126', '105', '103', '102', '110',
       '109', '106', '166', '112', '108', '107', '97', '96', '100', '78',
       '77', '70', '72', '99', '92', '90', '136', '135', '134', '133',
       '132', '131', '130', '129', '144', '143', '155', '154', '150',
       '148', '147', '164', '161', '159', '128', '127', '142', '139',
       '152', '158', '156', '172', '170', '168', '167', '165', '181',
       '180', '176', '173', '175', '185', '186'], dtype=object)

In [73]:
import plotly.graph_objs as go

# Calculer le nombre total de patientes dans chaque groupe
total_patients_NACT = len(df_NACT['Patient'].unique())
total_patients_ACT = len(df_ACT['Patient'].unique())

# Diviser le nombre d'occurrences de chaque checkpoint immunitaire par le nombre total de patientes dans le groupe correspondant
all_occurrences_normalized = all_occurrences.copy()
all_occurrences_normalized['NACT'] /= total_patients_NACT
all_occurrences_normalized['ACT'] /= total_patients_ACT

# Créer un objet Figure de Plotly
fig = go.Figure()

# Ajouter les barres pour les proportions normalisées de chaque checkpoint immunitaire dans les deux groupes
for col in all_occurrences_normalized.columns:
    fig.add_trace(go.Bar(x=all_occurrences_normalized.index.get_level_values('immune_checkpoint'), y=all_occurrences_normalized[col], name=col))

# Mettre en forme le titre et les axes
fig.update_layout(
    title="Comparaison des proportions de checkpoints immunitaires entre les groupes NACT et ACT",
    xaxis_title="Checkpoint Immunitaire",
    yaxis_title="Proportion d'Occurrences",
    xaxis_tickangle=-45,
    legend_title="Groupe"
)

# Afficher le graphique
fig.show()
plot(fig)

'temp-plot.html'

### V.4.3. IMMUNE CHECKPOINT

#### V.4.3.1. NACT

In [74]:
# Count of each immune_checkpoint type by cell_subtype
counts_NACT = df_NACT.groupby(['cell_type', 'cell_subtype', 'immune_checkpoint']).size().reset_index(name='count')

# % for each cell_subtype
counts_NACT['percentage'] = counts_NACT.groupby('cell_subtype')['count'].apply(lambda x: (x / x.sum()) * 100)

display(counts_NACT)

cell_type cell_subtype immune_checkpoint  count  percentage
0     CANCER       CANCER              B7H4  10827   16.317273
1     CANCER       CANCER          B7H4_PD1    140    0.210993
2     CANCER       CANCER         B7H4_PDL1     19    0.028635
3     CANCER       CANCER              None  52778   79.541242
4     CANCER       CANCER               PD1   1553    2.340512
..       ...          ...               ...    ...         ...
59    STROMA   αSMA_myCAF              B7H4     13    0.101634
60    STROMA   αSMA_myCAF          B7H4_PD1      1    0.007818
61    STROMA   αSMA_myCAF              None  12746   99.648190
62    STROMA   αSMA_myCAF               PD1     15    0.117270
63    STROMA   αSMA_myCAF              PDL1     16    0.125088

[64 rows x 5 columns]

In [75]:
fig = px.bar(counts_NACT, x='immune_checkpoint', y='percentage', color='cell_type', 
             title='Percentage of Each Immune Checkpoint Type by Cell Subtype in NACT',
             labels={'immune_checkpoint': 'Immune Checkpoint', 'percentage': 'Percentage', 'cell_subtype': 'Cell Subtype'})

fig.show()
plot(fig)

'temp-plot.html'

#### V.4.3.2. ACT

In [76]:
# Count of each immune_checkpoint type by cell_subtype
counts_ACT = df_ACT.groupby(['cell_type', 'cell_subtype', 'immune_checkpoint']).size().reset_index(name='count')

# % for each cell_subtype
counts_ACT['percentage'] = counts_ACT.groupby('cell_subtype')['count'].apply(lambda x: (x / x.sum()) * 100)

print(counts_ACT)

   cell_type  cell_subtype immune_checkpoint   count  percentage
0     CANCER        CANCER              B7H4   32646    9.083725
1     CANCER        CANCER          B7H4_PD1     425    0.118256
2     CANCER        CANCER         B7H4_PDL1      84    0.023373
3     CANCER        CANCER              None  314226   87.433151
4     CANCER        CANCER               PD1    7532    2.095773
..       ...           ...               ...     ...         ...
66    STROMA  STROMA_OTHER              PDL1     160    0.332226
67    STROMA    αSMA_myCAF              B7H4      51    0.185266
68    STROMA    αSMA_myCAF              None   27200   98.808486
69    STROMA    αSMA_myCAF               PD1     256    0.929962
70    STROMA    αSMA_myCAF              PDL1      21    0.076286

[71 rows x 5 columns]


In [77]:
# Créer le graphique à barres avec Plotly Express
fig = px.bar(counts_ACT, x='immune_checkpoint', y='percentage', color='cell_type', 
             title='Percentage of Each Immune Checkpoint Type by Cell Subtype in ACT',
             labels={'immune_checkpoint': 'Immune Checkpoint', 'percentage': 'Percentage', 'cell_subtype': 'Cell Subtype'})

# Afficher le graphique
fig.show()
plot(fig)

'temp-plot.html'

In [78]:
# Concaténer les deux DataFrames
combined_counts = pd.concat([counts_NACT, counts_ACT])

# Ajouter une colonne pour distinguer les deux ensembles de données
combined_counts['dataset'] = ['NACT'] * len(counts_NACT) + ['ACT'] * len(counts_ACT)

# Créer le graphique à barres avec Plotly Express
fig = px.bar(combined_counts, x='immune_checkpoint', y='percentage', color='cell_subtype', 
             facet_col='dataset', facet_col_wrap=1,
             title='Percentage of Each Immune Checkpoint Type by Cell Subtype',
             labels={'immune_checkpoint': 'Immune Checkpoint', 'percentage': 'Percentage', 'cell_subtype': 'Cell Subtype', 'dataset': 'Dataset'})

# Afficher le graphique
fig.show()
plot(fig)

'temp-plot.html'

In [79]:
# Concaténer les deux DataFrames
combined_counts = pd.concat([counts_NACT, counts_ACT])

# Ajouter une colonne pour distinguer les deux ensembles de données
combined_counts['dataset'] = ['NACT'] * len(counts_NACT) + ['ACT'] * len(counts_ACT)

# Créer le graphique à barres groupées avec Plotly Express
fig = px.bar(combined_counts, x='immune_checkpoint', y='percentage', color='cell_subtype', 
             facet_col='dataset', facet_col_wrap=1,
             barmode='group',
             title='Percentage of Each Immune Checkpoint Type by Cell Subtype',
             labels={'immune_checkpoint': 'Immune Checkpoint', 'percentage': 'Percentage', 'cell_subtype': 'Cell Subtype', 'dataset': 'Dataset'})

# Afficher le graphique
fig.show()
plot(fig)

'temp-plot.html'

In [80]:
combined_counts

cell_type  cell_subtype immune_checkpoint  count  percentage dataset
0     CANCER        CANCER              B7H4  10827   16.317273    NACT
1     CANCER        CANCER          B7H4_PD1    140    0.210993    NACT
2     CANCER        CANCER         B7H4_PDL1     19    0.028635    NACT
3     CANCER        CANCER              None  52778   79.541242    NACT
4     CANCER        CANCER               PD1   1553    2.340512    NACT
..       ...           ...               ...    ...         ...     ...
66    STROMA  STROMA_OTHER              PDL1    160    0.332226     ACT
67    STROMA    αSMA_myCAF              B7H4     51    0.185266     ACT
68    STROMA    αSMA_myCAF              None  27200   98.808486     ACT
69    STROMA    αSMA_myCAF               PD1    256    0.929962     ACT
70    STROMA    αSMA_myCAF              PDL1     21    0.076286     ACT

[135 rows x 6 columns]

### V.4.4. NACT VS ACT

In [81]:
#######
####### Count by cell SUBtype !! IN NACT !!
#######
cell_subtypes = ['DC', 'B', 'TCD4', 'TCD8', 'M1', 'M2', 'Treg', \
                 'IMMUNE_OTHER', 'CANCER', 'αSMA_myCAF', 'STROMA_OTHER', 'ENDOTHELIAL']
# Initialisation d'un dictionnaire pour stocker les counts des sous-types de cellules
subtype_counts = {}

# Boucle sur les sous-types de cellules pour compter les échantillons correspondants
for subtype in cell_subtypes:
    subtype_counts[subtype.lower()] = pd.DataFrame({subtype.lower():
        df_NACT.loc[
            df_NACT['cell_subtype'] == subtype, 'Sample_ID'].value_counts()
    }).sort_index()

# Concaténation des counts des sous-types de cellules en un seul DataFrame
counts_subtypes = pd.concat([pd.DataFrame(v) for v in subtype_counts.values()], axis=1, sort=False)
counts_subtypes = counts_subtypes.fillna(0)

# Enregistrement des counts des sous-types de cellules dans un fichier CSV
filename_subtypes = os.path.join(output_data_dir, project_name + "_cell_subtypes_number.csv")
counts_subtypes.to_csv(filename_subtypes, index=False)
counts_subtypes

dc     b  tcd4  tcd8   m1    m2  treg  immune_other  cancer  \
DD3S1.csv   11.0   0.0   551   539   73  22.0     1           110    8186   
DD3S3.csv   27.0  44.0  1441   728   69  19.0     2           258   13963   
DD4S1.csv   48.0   3.0  1087   211   26   5.0     5           531    8862   
DD4S2.csv   28.0   1.0   807    47   78  74.0     4           161    6999   
DD4S3.csv   82.0   1.0   373   144   55  64.0     5           917    5474   
DD5S1.csv   55.0   1.0   861    69  342  17.0     7           548    6529   
DD5S2.csv   71.0   0.0   413    63   27   4.0     5           247    5963   
DD5S3.csv  490.0   3.0   904   230  332  69.0     7           312    8092   
DD3S2.csv    0.0   0.0    15     7    2   0.0     1            17    2285   

           αsma_mycaf  stroma_other  endothelial  
DD3S1.csv        1143          2380          283  
DD3S3.csv        2334          5066          321  
DD4S1.csv         274           843          778  
DD4S2.csv         334           619          268  
DD4S3.csv          37           708          178  
DD5S1.csv        1776          2269          758  
DD5S2.csv        2673          3198          930  
DD5S3.csv        2657          1428          581  
DD3S2.csv        1563           317          119

In [82]:
# Ajout des colonnes de pourcentages pour chaque sous-type de cellules
counts_perc = counts_subtypes.copy()

# Calcul des pourcentages pour chaque sous-type de cellules
for col in counts_perc.columns:
    counts_perc[col + '_perc'] = (counts_perc[col] / counts_perc.sum(axis=1)) * 100

# Affichage des pourcentages des sous-types de cellules

counts_perc['Sample_ID'] = counts_perc.index
counts_perc.columns.values
display(counts_perc)

dc     b  tcd4  tcd8   m1    m2  treg  immune_other  cancer  \
DD3S1.csv   11.0   0.0   551   539   73  22.0     1           110    8186   
DD3S3.csv   27.0  44.0  1441   728   69  19.0     2           258   13963   
DD4S1.csv   48.0   3.0  1087   211   26   5.0     5           531    8862   
DD4S2.csv   28.0   1.0   807    47   78  74.0     4           161    6999   
DD4S3.csv   82.0   1.0   373   144   55  64.0     5           917    5474   
DD5S1.csv   55.0   1.0   861    69  342  17.0     7           548    6529   
DD5S2.csv   71.0   0.0   413    63   27   4.0     5           247    5963   
DD5S3.csv  490.0   3.0   904   230  332  69.0     7           312    8092   
DD3S2.csv    0.0   0.0    15     7    2   0.0     1            17    2285   

           αsma_mycaf  ...  tcd8_perc   m1_perc   m2_perc  treg_perc  \
DD3S1.csv        1143  ...   4.051649  0.548572  0.165316   0.007514   
DD3S3.csv        2334  ...   2.998571  0.284170  0.078249   0.008237   
DD4S1.csv         274  ...   1.663778  0.204988  0.039420   0.039420   
DD4S2.csv         334  ...   0.498469  0.827202  0.784713   0.042413   
DD4S3.csv          37  ...   1.790227  0.683615  0.795412   0.062135   
DD5S1.csv        1776  ...   0.521190  2.583189  0.128379   0.052861   
DD5S2.csv        2673  ...   0.463318  0.198558  0.029416   0.036769   
DD5S3.csv        2657  ...   1.521743  2.196382  0.456411   0.046301   
DD3S2.csv        1563  ...   0.161799  0.046227  0.000000   0.023113   

           immune_other_perc  cancer_perc  αsma_mycaf_perc  stroma_other_perc  \
DD3S1.csv           0.826571    61.508057         8.548777          17.789229   
DD3S3.csv           1.062533    57.501935         9.589089          20.805140   
DD4S1.csv           4.186401    69.844899         2.147679           6.606528   
DD4S2.csv           1.707131    74.199057         3.513225           6.508632   
DD4S3.csv          11.395546    67.929123         0.455310           8.711933   
DD5S1.csv           4.138280    49.289035        13.357759          17.048613   
DD5S2.csv           1.816405    43.845251        19.591101          23.405353   
DD5S3.csv           2.063701    53.516636        17.510159           9.399957   
DD3S2.csv           0.392920    52.808306        35.686731           7.179310   

           endothelial_perc  Sample_ID  
DD3S1.csv          2.112465  DD3S1.csv  
DD3S3.csv          1.317163  DD3S3.csv  
DD4S1.csv          6.093973  DD4S1.csv  
DD4S2.csv          2.816027  DD4S2.csv  
DD4S3.csv          2.187943  DD4S3.csv  
DD5S1.csv          5.688107  DD5S1.csv  
DD5S2.csv          6.794795  DD5S2.csv  
DD5S3.csv          3.822127  DD5S3.csv  
DD3S2.csv          2.690697  DD3S2.csv  

[9 rows x 25 columns]

In [83]:
fig = go.Figure()
title = 'NACT_patients_Cell subtypes proportions by Sample ID and tissue type'

for cell_subtype in cell_subtypes:
    fig.add_trace(
        go.Bar(
            name=cell_subtype,
            x=counts_perc['Sample_ID'],
            y=counts_perc[f'{cell_subtype.lower()}_perc'],
            text=counts_perc[f'{cell_subtype.lower()}_perc'],
            textposition='auto',
            marker_color='rgb' + str(cell_subtype_color_dict[cell_subtype])))

fig.update_layout(
    plot_bgcolor='white',
    barmode='stack',
    xaxis=dict(linecolor='black'),
    title=title,
    yaxis=dict(title='Cell count (%)', linecolor='black')
)

# Enregistrer l'image
output_filename = title.replace(" ", "_") + ".png"
#fig.write_image(output_images_dir + "/" + output_filename, scale=1000)

# Afficher le graphique
fig.show()
plot(fig)

'temp-plot.html'

In [84]:
#######
####### Count by cell SUBtype !! IN ACT !!
#######
cell_subtypes = ['DC', 'B', 'TCD4', 'TCD8', 'M1', 'M2', 'Treg', \
                 'IMMUNE_OTHER', 'CANCER', 'αSMA_myCAF', 'STROMA_OTHER', 'ENDOTHELIAL']
# Initialisation d'un dictionnaire pour stocker les counts des sous-types de cellules
subtype_counts = {}

# Boucle sur les sous-types de cellules pour compter les échantillons correspondants
for subtype in cell_subtypes:
    subtype_counts[subtype.lower()] = pd.DataFrame({subtype.lower():
        df_ACT.loc[
            df_ACT['cell_subtype'] == subtype, 'Sample_ID'].value_counts()
    }).sort_index()

# Concaténation des counts des sous-types de cellules en un seul DataFrame
counts_subtypes = pd.concat([pd.DataFrame(v) for v in subtype_counts.values()], axis=1, sort=False)
counts_subtypes = counts_subtypes.fillna(0)

# Enregistrement des counts des sous-types de cellules dans un fichier CSV
filename_subtypes = os.path.join(output_data_dir, project_name + "_cell_subtypes_number.csv")
counts_subtypes.to_csv(filename_subtypes, index=False)
counts_subtypes

dc      b  tcd4  tcd8   m1   m2  treg  immune_other  cancer  \
DD3S1.csv    70    0.0  2440  2310  237  107     5           884   40795   
DD3S2.csv   294    0.0  1900  2343   92   25    37          1244   48774   
DD3S3.csv   253   94.0  5416  2822  183   77    26          1616   63037   
DD4S1.csv   224   26.0  1580  1739   50   33     7          1858   45151   
DD4S2.csv   102   13.0  1131  1647   34   28    15           680   32471   
DD4S3.csv  1068   30.0  1980  2796  100  264    33          2419   45124   
DD5S1.csv   528  138.0  1979   467  162   11    21           672   37194   
DD5S2.csv    89   16.0   722    82  104   59     9           220   24876   
DD5S3.csv   977   32.0  1096   457  147   41     6           553   21968   

           αsma_mycaf  stroma_other  endothelial  
DD3S1.csv        2824          4343         1383  
DD3S2.csv        3226          6958         1631  
DD3S3.csv        5090         10922         2457  
DD4S1.csv        2832          3300         1275  
DD4S2.csv        1330          3910          964  
DD4S3.csv        3649          4122         1195  
DD5S1.csv        5200          7822         2037  
DD5S2.csv        1203          4024          405  
DD5S3.csv        2174          2759          583

In [85]:
# Ajout des colonnes de pourcentages pour chaque sous-type de cellules
counts_perc = counts_subtypes.copy()

# Calcul des pourcentages pour chaque sous-type de cellules
for col in counts_perc.columns:
    counts_perc[col + '_perc'] = (counts_perc[col] / counts_perc.sum(axis=1)) * 100

# Affichage des pourcentages des sous-types de cellules

counts_perc['Sample_ID'] = counts_perc.index
counts_perc.columns.values
display(counts_perc)

dc      b  tcd4  tcd8   m1   m2  treg  immune_other  cancer  \
DD3S1.csv    70    0.0  2440  2310  237  107     5           884   40795   
DD3S2.csv   294    0.0  1900  2343   92   25    37          1244   48774   
DD3S3.csv   253   94.0  5416  2822  183   77    26          1616   63037   
DD4S1.csv   224   26.0  1580  1739   50   33     7          1858   45151   
DD4S2.csv   102   13.0  1131  1647   34   28    15           680   32471   
DD4S3.csv  1068   30.0  1980  2796  100  264    33          2419   45124   
DD5S1.csv   528  138.0  1979   467  162   11    21           672   37194   
DD5S2.csv    89   16.0   722    82  104   59     9           220   24876   
DD5S3.csv   977   32.0  1096   457  147   41     6           553   21968   

           αsma_mycaf  ...  tcd8_perc   m1_perc   m2_perc  treg_perc  \
DD3S1.csv        2824  ...   4.169485  0.427746  0.193116   0.009024   
DD3S2.csv        3226  ...   3.521863  0.138282  0.037576   0.055613   
DD3S3.csv        5090  ...   3.067416  0.198908  0.083693   0.028260   
DD4S1.csv        2832  ...   2.994241  0.086086  0.056817   0.012052   
DD4S2.csv        1330  ...   3.891047  0.080318  0.066144   0.035434   
DD4S3.csv        3649  ...   4.453300  0.159263  0.420452   0.052556   
DD5S1.csv        5200  ...   0.830433  0.288069  0.019560   0.037342   
DD5S2.csv        1203  ...   0.257768  0.326922  0.185464   0.028291   
DD5S3.csv        2174  ...   1.483774  0.477252  0.133109   0.019479   

           immune_other_perc  cancer_perc  αsma_mycaf_perc  stroma_other_perc  \
DD3S1.csv           1.595457    73.625322         5.089889           7.826968   
DD3S2.csv           1.869804    73.308069         4.843391          10.445711   
DD3S3.csv           1.756471    68.515202         5.528227          11.861625   
DD4S1.csv           3.198964    77.733303         4.869139           5.673310   
DD4S2.csv           1.606349    76.702624         3.136029           9.218771   
DD4S3.csv           3.852525    71.860551         5.804437           6.556229   
DD5S1.csv           1.194945    66.136689         9.235544          13.890111   
DD5S2.csv           0.691554    78.194228         3.772191          12.616375   
DD5S3.csv           1.795341    71.316005         7.041282           8.933977   

           endothelial_perc  Sample_ID  
DD3S1.csv          2.492095  DD3S1.csv  
DD3S2.csv          2.448158  DD3S2.csv  
DD3S3.csv          2.668033  DD3S3.csv  
DD4S1.csv          2.191747  DD4S1.csv  
DD4S2.csv          2.272369  DD4S2.csv  
DD4S3.csv          1.900504  DD4S3.csv  
DD5S1.csv          3.616361  DD5S1.csv  
DD5S2.csv          1.269287  DD5S2.csv  
DD5S3.csv          1.887279  DD5S3.csv  

[9 rows x 25 columns]

In [86]:
fig = go.Figure()
title = 'ACT_patients_Cell subtypes proportions by Sample ID and tissue type'

for cell_subtype in cell_subtypes:
    fig.add_trace(
        go.Bar(
            name=cell_subtype,
            x=counts_perc['Sample_ID'],
            y=counts_perc[f'{cell_subtype.lower()}_perc'],
            text=counts_perc[f'{cell_subtype.lower()}_perc'],
            textposition='auto',
            marker_color='rgb' + str(cell_subtype_color_dict[cell_subtype])))

fig.update_layout(
    plot_bgcolor='white',
    barmode='stack',
    xaxis=dict(linecolor='black'),
    title=title,
    yaxis=dict(title='Cell count (%)', linecolor='black')
)

# Enregistrer l'image
output_filename = title.replace(" ", "_") + ".png"
#fig.write_image(output_images_dir + "/" + output_filename, scale=1000)

# Afficher le graphique
fig.show()
plot(fig)

'temp-plot.html'

In [87]:
df1

PDL1_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_0                            -0.677863   
DD3S1_Cell_1                            -0.677863   
DD3S1_Cell_2                            -0.677863   
DD3S1_Cell_3                            -0.741282   
DD3S1_Cell_6                            -0.621521   
...                                           ...   
TMA_Cell_115755                          0.478275   
TMA_Cell_115756                          0.297418   
TMA_Cell_115757                          0.346950   
TMA_Cell_115758                         -0.189415   
TMA_Cell_115760                          0.245777   

                 HLA_Cytoplasm_Intensity_Average  \
ID                                                 
DD3S1_Cell_0                           -0.417494   
DD3S1_Cell_1                           -0.516487   
DD3S1_Cell_2                           -0.141921   
DD3S1_Cell_3                           -0.460472   
DD3S1_Cell_6                           -0.247254   
...                                          ...   
TMA_Cell_115755                         0.558670   
TMA_Cell_115756                         0.420594   
TMA_Cell_115757                         0.453951   
TMA_Cell_115758                         0.508840   
TMA_Cell_115760                         0.460219   

                 CKs_Cytoplasm_Intensity_Average  \
ID                                                 
DD3S1_Cell_0                           -0.912537   
DD3S1_Cell_1                           -0.838037   
DD3S1_Cell_2                           -1.016023   
DD3S1_Cell_3                           -0.491711   
DD3S1_Cell_6                           -0.867127   
...                                          ...   
TMA_Cell_115755                        -0.962840   
TMA_Cell_115756                        -0.971632   
TMA_Cell_115757                        -0.602893   
TMA_Cell_115758                        -0.886041   
TMA_Cell_115760                        -1.003840   

                 Ki67_Nucleus_Intensity_Average  \
ID                                                
DD3S1_Cell_0                          -0.817876   
DD3S1_Cell_1                          -0.869685   
DD3S1_Cell_2                          -0.755879   
DD3S1_Cell_3                          -0.818084   
DD3S1_Cell_6                          -0.742544   
...                                         ...   
TMA_Cell_115755                        1.732291   
TMA_Cell_115756                        1.966955   
TMA_Cell_115757                        1.338956   
TMA_Cell_115758                        0.647980   
TMA_Cell_115760                        0.191158   

                 CD163_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_0                              0.930099   
DD3S1_Cell_1                              1.114924   
DD3S1_Cell_2                              0.834577   
DD3S1_Cell_3                              0.648200   
DD3S1_Cell_6                              0.810579   
...                                            ...   
TMA_Cell_115755                           0.507434   
TMA_Cell_115756                           0.304365   
TMA_Cell_115757                           0.559435   
TMA_Cell_115758                          -0.227224   
TMA_Cell_115760                          -0.313127   

                 ColVI_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_0                              0.232078   
DD3S1_Cell_1                              0.301333   
DD3S1_Cell_2                              0.259216   
DD3S1_Cell_3                              0.107027   
DD3S1_Cell_6                              0.272128   
...                                            ...   
TMA_Cell_115755                          -0.912641   
TMA_Cell_115756                          -1.164112   
TMA_Cell_115757                          -0.801333   
TMA_Cell_115

## RATIO M2/M1

In [88]:
# Filtrer les lignes correspondant aux cellules M1 et M2 pour les patients NACT
df_M1_NACT = df[(df['cell_subtype'] == 'M1') & df['Patient'].isin(num_NACT_patients)]
df_M2_NACT = df[(df['cell_subtype'] == 'M2') & df['Patient'].isin(num_NACT_patients)]

# Filtrer les lignes correspondant aux cellules M1 et M2 pour les patients ACT
df_M1_ACT = df[(df['cell_subtype'] == 'M1') & df['Patient'].isin(num_ACT_patients)]
df_M2_ACT = df[(df['cell_subtype'] == 'M2') & df['Patient'].isin(num_ACT_patients)]

In [89]:
# Regrouper les données par patient et calculer le total de cellules M1 et M2 pour les patients NACT
result_M1_NACT = df_M1_NACT.groupby('Patient').size().rename('total_M1_cells')
result_M2_NACT = df_M2_NACT.groupby('Patient').size().rename('total_M2_cells')

# Regrouper les données par patient et calculer le total de cellules M1 et M2 pour les patients ACT
result_M1_ACT = df_M1_ACT.groupby('Patient').size().rename('total_M1_cells')
result_M2_ACT = df_M2_ACT.groupby('Patient').size().rename('total_M2_cells')

In [90]:
# Créer le DataFrame résultant avec Patient comme index pour les patients NACT
result_NACT = pd.concat([result_M1_NACT, result_M2_NACT], axis=1, sort=False).fillna(0)

# Créer le DataFrame résultant avec Patient comme index pour les patients ACT
result_ACT = pd.concat([result_M1_ACT, result_M2_ACT], axis=1, sort=False).fillna(0)

In [91]:
# Ajouter une colonne pour le ratio de M2/M1 pour les patients NACT
result_NACT['M2_M1_ratio'] = result_NACT['total_M2_cells'] / result_NACT['total_M1_cells']
result_NACT['Treatment_Type'] = 'NACT'  # Ajouter une colonne pour indiquer le traitement

# Ajouter une colonne pour le ratio de M2/M1 pour les patients ACT
result_ACT['M2_M1_ratio'] = result_ACT['total_M2_cells'] / result_ACT['total_M1_cells']
result_ACT['Treatment_Type'] = 'ACT'  # Ajouter une colonne pour indiquer le traitement

In [92]:
# Regrouper les données par patient et calculer le total de cellules M1 et M2 pour les patients NACT
result_M1_NACT = df_M1_NACT.groupby('Patient').size().rename('total_M1_cells')
result_M2_NACT = df_M2_NACT.groupby('Patient').size().rename('total_M2_cells')

# Regrouper les données par patient et calculer le total de cellules M1 et M2 pour les patients ACT
result_M1_ACT = df_M1_ACT.groupby('Patient').size().rename('total_M1_cells')
result_M2_ACT = df_M2_ACT.groupby('Patient').size().rename('total_M2_cells')

In [93]:
result_ACT

total_M1_cells  total_M2_cells  M2_M1_ratio Treatment_Type
Patient                                                            
10                167.0           100.0     0.598802            ACT
101                 3.0             1.0     0.333333            ACT
102                 5.0             1.0     0.200000            ACT
103                 7.0             0.0     0.000000            ACT
105                 3.0             3.0     1.000000            ACT
...                 ...             ...          ...            ...
34                  0.0             2.0          inf            ACT
45                  0.0             3.0          inf            ACT
71                  0.0            16.0          inf            ACT
72                  0.0             1.0          inf            ACT
9                   0.0             1.0          inf            ACT

[103 rows x 4 columns]

In [94]:
result_NACT

total_M1_cells  total_M2_cells  M2_M1_ratio Treatment_Type
Patient                                                            
104                 1.0             2.0     2.000000           NACT
111                10.0             3.0     0.300000           NACT
119                 3.0             0.0     0.000000           NACT
121                 4.0             0.0     0.000000           NACT
137                 1.0             1.0     1.000000           NACT
140               307.0            38.0     0.123779           NACT
141                10.0             1.0     0.100000           NACT
146                 1.0             2.0     2.000000           NACT
149               275.0             3.0     0.010909           NACT
15                  7.0             1.0     0.142857           NACT
153                61.0            14.0     0.229508           NACT
157                 2.0             7.0     3.500000           NACT
162                 1.0             0.0     0.000000           NACT
169                 1.0             0.0     0.000000           NACT
171                25.0             1.0     0.040000           NACT
174                 1.0             0.0     0.000000           NACT
177                 1.0             0.0     0.000000           NACT
18                  1.0             0.0     0.000000           NACT
184                13.0            11.0     0.846154           NACT
187                 2.0             8.0     4.000000           NACT
32                 52.0            15.0     0.288462           NACT
40                  1.0             0.0     0.000000           NACT
5                  78.0             6.0     0.076923           NACT
51                  1.0             0.0     0.000000           NACT
61                  4.0            19.0     4.750000           NACT
85                 41.0            16.0     0.390244           NACT
89                 22.0             8.0     0.363636           NACT
95                  5.0            44.0     8.800000           NACT
98                 73.0            70.0     0.958904           NACT
182                 0.0             3.0          inf           NACT
183                 0.0             1.0          inf           NACT

In [95]:
# Concaténer les résultats pour obtenir le DataFrame final
result_final = pd.concat([result_NACT, result_ACT])

# Trier le DataFrame par index
result_sorted = result_final.sort_index()

# Définir l'option pour afficher toutes les lignes du DataFrame
#pd.set_option('display.max_rows', None)

display(result_sorted)

total_M1_cells  total_M2_cells  M2_M1_ratio Treatment_Type
Patient                                                            
10                167.0           100.0     0.598802            ACT
100                 0.0             3.0          inf            ACT
101                 3.0             1.0     0.333333            ACT
102                 5.0             1.0     0.200000            ACT
103                 7.0             0.0     0.000000            ACT
...                 ...             ...          ...            ...
92                  3.0            25.0     8.333333            ACT
95                  5.0            44.0     8.800000           NACT
96                  2.0             1.0     0.500000            ACT
98                 73.0            70.0     0.958904           NACT
99                  5.0             5.0     1.000000            ACT

[134 rows x 4 columns]

In [96]:
# Remplacer les valeurs négatives du ratio M2/M1 par 0
#result_sorted['M2_M1_ratio'] = result_sorted['M2_M1_ratio'].clip(lower=0)

#result_sorted['M2_M1_ratio'] = result_sorted['M2_M1_ratio'].replace([-float('inf'), float('inf')], 0)
#result_sorted['M2_M1_ratio'] = result_sorted['M2_M1_ratio'].apply(lambda x: 0 if x < 0 else x)

# Définir l'option pour afficher toutes les lignes du DataFrame
#pd.set_option('display.max_rows', None)

display(result_sorted)

total_M1_cells  total_M2_cells  M2_M1_ratio Treatment_Type
Patient                                                            
10                167.0           100.0     0.598802            ACT
100                 0.0             3.0          inf            ACT
101                 3.0             1.0     0.333333            ACT
102                 5.0             1.0     0.200000            ACT
103                 7.0             0.0     0.000000            ACT
...                 ...             ...          ...            ...
92                  3.0            25.0     8.333333            ACT
95                  5.0            44.0     8.800000           NACT
96                  2.0             1.0     0.500000            ACT
98                 73.0            70.0     0.958904           NACT
99                  5.0             5.0     1.000000            ACT

[134 rows x 4 columns]

In [97]:
# Créer le violin plot avec des points individuels
fig = px.violin(result_sorted, x='Treatment_Type', y='M2_M1_ratio', 
                box=True, hover_data=result_sorted.columns)

# Afficher le violin plot
fig.update_layout(title=f'Violin Plot du Ratio M2/M1 en fonction du Traitement',
                  xaxis_title='Traitement', yaxis_title='Ratio M2/M1')


fig.show()
plot(fig)
import plotly.io as pio
#pio.write_image(fig, 'Violinplot_ratio_M2_M1.png')

In [98]:
# Filtrer les lignes correspondant aux cellules CANCER B7H4/PDL1 pour les patients NACT
df_B7H4_NACT = df[(df['immune_checkpoint'] == 'B7H4') & df['Patient'].isin(num_NACT_patients) & (df['cell_type'] == 'CANCER')]
df_PDL1_NACT = df[(df['immune_checkpoint'] == 'PDL1') & df['Patient'].isin(num_NACT_patients) & ((df['cell_type'] == 'CANCER') | (df['cell_type'] == 'IMMUNE'))]

# Filtrer les lignes correspondant aux cellules CANCER B7H4/PDL1 pour les patients ACT
df_B7H4_ACT = df[(df['immune_checkpoint'] == 'B7H4') & df['Patient'].isin(num_ACT_patients) & (df['cell_type'] == 'CANCER')]
df_PDL1_ACT = df[(df['immune_checkpoint'] == 'PDL1') & df['Patient'].isin(num_ACT_patients) & ((df['cell_type'] == 'CANCER') | (df['cell_type'] == 'IMMUNE'))]


In [99]:
#pd.set_option('display.max_rows', None)
print(df_B7H4_NACT.shape)
print(df_PDL1_NACT.shape)

print(df_B7H4_ACT.shape)
print(df_PDL1_ACT.shape)

(10827, 40)
(1229, 40)
(32646, 40)
(5434, 40)


In [100]:
df_PDL1_NACT.head()

PDL1_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_21828                          1.609792   
DD3S1_Cell_21831                          1.590608   
DD3S1_Cell_21937                          1.611230   
DD3S1_Cell_21939                          1.630944   
DD3S1_Cell_21959                          1.517887   

                  HLA_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_21828                         2.521615   
DD3S1_Cell_21831                         2.493721   
DD3S1_Cell_21937                         2.189588   
DD3S1_Cell_21939                         2.690321   
DD3S1_Cell_21959                         2.719076   

                  CKs_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_21828                         0.223023   
DD3S1_Cell_21831                         0.231741   
DD3S1_Cell_21937                         0.558693   
DD3S1_Cell_21939                        -0.185765   
DD3S1_Cell_21959                         0.000214   

                  Ki67_Nucleus_Intensity_Average  \
ID                                                 
DD3S1_Cell_21828                        1.084166   
DD3S1_Cell_21831                        0.251524   
DD3S1_Cell_21937                        0.249337   
DD3S1_Cell_21939                        1.258937   
DD3S1_Cell_21959                       -0.039537   

                  CD163_Cytoplasm_Intensity_Average  \
ID                                                    
DD3S1_Cell_21828                           0.338872   
DD3S1_Cell_21831                           1.185084   
DD3S1_Cell_21937                           0.313269   
DD3S1_Cell_21939                           0.552631   
DD3S1_Cell_21959                           0.431631   

                  ColVI_Cytoplasm_Intensity_Average  \
ID                                                    
DD3S1_Cell_21828                          -1.112327   
DD3S1_Cell_21831                          -1.203795   
DD3S1_Cell_21937                          -1.248514   
DD3S1_Cell_21939                          -1.223585   
DD3S1_Cell_21959                          -1.257583   

                  CD20_Cytoplasm_Intensity_Average  \
ID                                                   
DD3S1_Cell_21828                          1.374637   
DD3S1_Cell_21831                          1.610041   
DD3S1_Cell_21937                          1.501920   
DD3S1_Cell_21939                          1.519502   
DD3S1_Cell_21959                          1.471392   

                  PD1_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_21828                         0.236768   
DD3S1_Cell_21831                        -0.700345   
DD3S1_Cell_21937                        -0.669547   
DD3S1_Cell_21939                        -0.700822   
DD3S1_Cell_21959                        -0.863404   

                  AXL_Cytoplasm_Intensity_Average  \
ID                                                  
DD3S1_Cell_21828                        -0.450948   
DD3S1_Cell_21831                        -0.673078   
DD3S1_Cell_21937                        -0.781676   
DD3S1_Cell_21939                        -0.721136   
DD3S1_Cell_21959                        -0.803700   

                  CD31_Cytoplasm_Intensity_Average  ...  Nucleus_Roundness  \
ID                                                  ...                      
DD3S1_Cell_21828                         -0.132787  ...           0.868000   
DD3S1_Cell_21831                         -0.641906  ...           0.580756   
DD3S1_Cell_21937                         -0.848153  ...           0.829105   
DD3S1_Cell_21939                         -0.785331  ...           0.925649   
DD3S1_Cell_21959                         -0.732914  ...           0.777269   

                        Nuc_X  ROI_index  Nucleus_Size  Sample_ID  \
ID                 

In [101]:
# Regrouper les données par patient et calculer le total de cellules B7H4 et PDL1 pour les patients NACT
result_B7H4_NACT = df_B7H4_NACT.groupby('Patient').size().rename('B7H4_cells')
result_PDL1_NACT = df_PDL1_NACT.groupby('Patient').size().rename('PDL1_cells')

# Regrouper les données par patient et calculer le total de cellules B7H4 et PDL1 pour les patients ACT
result_B7H4_ACT = df_B7H4_ACT.groupby('Patient').size().rename('B7H4_cells')
result_PDL1_ACT = df_PDL1_ACT.groupby('Patient').size().rename('PDL1_cells')

In [102]:
result_PDL1_NACT

Patient
104     20
111      1
116      3
119     18
121      4
137      4
140      3
141      2
149      1
15       6
153     30
157      7
160    198
162      5
169     12
171      1
178      6
18     307
182     46
183      2
184      3
187      7
26      19
32     126
5       34
61      18
7        6
85       9
89       5
95      23
98     303
Name: PDL1_cells, dtype: int64

In [103]:
# Créer le DataFrame résultant avec Patient comme index pour les patients NACT
result_NACT = pd.concat([result_B7H4_NACT, result_PDL1_NACT], axis=1, sort=False).fillna(0)

# Créer le DataFrame résultant avec Patient comme index pour les patients ACT
result_ACT = pd.concat([result_B7H4_ACT, result_PDL1_ACT], axis=1, sort=False).fillna(0)

In [104]:
result_NACT.head()


B7H4_cells  PDL1_cells
Patient                        
111            35.0         1.0
116            24.0         3.0
119          2151.0        18.0
121          2361.0         4.0
137            25.0         4.0

In [105]:
len(df_NACT[df_NACT['cell_type'] == 'CANCER'])


66353

In [106]:
#  pour les patients NACT
result_NACT['%_B7H4'] = result_NACT['B7H4_cells'] / len(df_NACT[df_NACT['cell_type'] == 'CANCER'])
result_NACT['%_PDL1'] = result_NACT['PDL1_cells'] / len(df_NACT[(df_NACT['cell_type'] == 'CANCER') | (df_NACT['cell_type'] == 'IMMUNE')])
result_NACT['Treatment_Type'] = 'NACT'  # Ajouter une colonne pour indiquer le traitement

#  pour le ratio de M2/M1 pour les patients ACT
result_ACT['%_B7H4'] = result_ACT['B7H4_cells'] / len(df_ACT[df_ACT['cell_type'] == 'CANCER'])
result_ACT['%_PDL1'] = result_ACT['PDL1_cells'] / len(df_ACT[(df_ACT['cell_type'] == 'CANCER') | (df_ACT['cell_type'] == 'IMMUNE')])
result_ACT['Treatment_Type'] = 'ACT'  # Ajouter une colonne pour indiquer le traitement

In [107]:
len(df_NACT[(df_NACT['cell_type'] == 'CANCER') | (df_NACT['cell_type'] == 'IMMUNE')])

80124

In [108]:
result_NACT

B7H4_cells  PDL1_cells    %_B7H4    %_PDL1 Treatment_Type
Patient                                                           
111            35.0         1.0  0.000527  0.000012           NACT
116            24.0         3.0  0.000362  0.000037           NACT
119          2151.0        18.0  0.032418  0.000225           NACT
121          2361.0         4.0  0.035582  0.000050           NACT
137            25.0         4.0  0.000377  0.000050           NACT
146            71.0         0.0  0.001070  0.000000           NACT
149           281.0         1.0  0.004235  0.000012           NACT
15           1008.0         6.0  0.015191  0.000075           NACT
153             9.0        30.0  0.000136  0.000374           NACT
157             2.0         7.0  0.000030  0.000087           NACT
160             1.0       198.0  0.000015  0.002471           NACT
162            40.0         5.0  0.000603  0.000062           NACT
169           140.0        12.0  0.002110  0.000150           NACT
171            28.0         1.0  0.000422  0.000012           NACT
174            47.0         0.0  0.000708  0.000000           NACT
177           124.0         0.0  0.001869  0.000000           NACT
178             2.0         6.0  0.000030  0.000075           NACT
179             6.0         0.0  0.000090  0.000000           NACT
18            285.0       307.0  0.004295  0.003832           NACT
182            39.0        46.0  0.000588  0.000574           NACT
183           152.0         2.0  0.002291  0.000025           NACT
184          1260.0         3.0  0.018989  0.000037           NACT
187            14.0         7.0  0.000211  0.000087           NACT
26              3.0        19.0  0.000045  0.000237           NACT
32            215.0       126.0  0.003240  0.001573           NACT
40             90.0         0.0  0.001356  0.000000           NACT
5               1.0        34.0  0.000015  0.000424           NACT
61              2.0        18.0  0.000030  0.000225           NACT
7              15.0         6.0  0.000226  0.000075           NACT
85           1563.0         9.0  0.023556  0.000112           NACT
89            154.0         5.0  0.002321  0.000062           NACT
95            207.0        23.0  0.003120  0.000287           NACT
98            472.0       303.0  0.007113  0.003782           NACT
104             0.0        20.0  0.000000  0.000250           NACT
140             0.0         3.0  0.000000  0.000037           NACT
141             0.0         2.0  0.000000  0.000025           NACT

In [109]:
# Concaténer les résultats pour obtenir le DataFrame final
result_final = pd.concat([result_NACT, result_ACT])

# Trier le DataFrame par index
result_sorted = result_final.sort_index()

# Définir l'option pour afficher toutes les lignes du DataFrame
#pd.set_option('display.max_rows', None)

display(result_sorted)

B7H4_cells  PDL1_cells    %_B7H4    %_PDL1 Treatment_Type
Patient                                                           
10             18.0         4.0  0.000050  0.000010            ACT
100           663.0         0.0  0.001845  0.000000            ACT
101            61.0        41.0  0.000170  0.000100            ACT
102           135.0        31.0  0.000376  0.000076            ACT
103            12.0       120.0  0.000033  0.000294            ACT
...             ...         ...       ...       ...            ...
95            207.0        23.0  0.003120  0.000287           NACT
96            812.0         0.0  0.002259  0.000000            ACT
97              2.0        46.0  0.000006  0.000113            ACT
98            472.0       303.0  0.007113  0.003782           NACT
99            161.0         2.0  0.000448  0.000005            ACT

[172 rows x 5 columns]

In [120]:
import plotly.express as px

fig = px.box(result_sorted, x='Treatment_Type', y='%_B7H4', 
                hover_data=result_sorted.columns,
                color='Treatment_Type',  # This can be set to a single color if preferred
                template='plotly_white',  # Starting with a clean white template
                )

fig.update_layout(
    title_text='Distribution of % B7H4 in Cancer Cells by Treatment',
    title_x=0.5,  # Center the title
    title_font=dict(size=18, family='Arial, sans-serif'),
    xaxis_title='Treatment Type',
    yaxis_title='% B7H4',
    xaxis=dict(tickangle=-45, title_font=dict(size=14, family='Arial, sans-serif')),
    yaxis=dict(title_font=dict(size=14, family='Arial, sans-serif')),
    legend_title_text='Treatment',
    legend_title_font=dict(size=12, family='Arial, sans-serif'),
)

# Adjusting gridlines to mimic R's ggplot2 style
fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='white')
fig.update_xaxes(showline=True, linewidth=2, linecolor='black', mirror=True)
fig.update_yaxes(showline=True, linewidth=2, linecolor='black', mirror=True)

fig.show()
plot(fig)

import plotly.io as pio
#pio.write_image(fig, 'Violinplot_%B7H4.png')

AssertionError: 

In [178]:
fig = px.box(result_sorted, x='Treatment_Type', y='%_PDL1', 
                hover_data=result_sorted.columns,
                color='Treatment_Type',  # This can be set to a single color if preferred
                template='plotly_white',  # Starting with a clean white template
                )

fig.update_layout(
    title_text='Distribution of % PDL1 in Cancer Cells by Treatment',
    title_x=0.5,  # Center the title
    title_font=dict(size=18, family='Arial, sans-serif'),
    xaxis_title='Treatment Type',
    yaxis_title='% PDL1',
    xaxis=dict(tickangle=-45, title_font=dict(size=14, family='Arial, sans-serif')),
    yaxis=dict(title_font=dict(size=14, family='Arial, sans-serif')),
    legend_title_text='Treatment',
    legend_title_font=dict(size=12, family='Arial, sans-serif'),
)

# Adjusting gridlines to mimic R's ggplot2 style
fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='white')
fig.update_xaxes(showline=True, linewidth=2, linecolor='black', mirror=True)
fig.update_yaxes(showline=True, linewidth=2, linecolor='black', mirror=True)


fig.show()
plot(fig)


import plotly.io as pio
#pio.write_image(fig, 'Violinplot_%PDL1.png')

In [194]:
# both on the same plot
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px

# Assuming 'result_sorted' is your DataFrame

# Create subplots with a shared y-axis
fig = make_subplots(rows=1, cols=2,
                    shared_yaxes=True, 
                    horizontal_spacing=0.01,
                    subplot_titles=('Distribution of % B7H4', 'Distribution of % PDL1'))

# Define a color map for the treatment types
color_map = {'ACT': "#327EBA", 'NACT': "#E06663"}

# Add first plot for % B7H4
fig1 = px.box(result_sorted, x='Treatment_Type', y='%_B7H4', template='plotly_white',
              color='Treatment_Type', color_discrete_map=color_map)
for trace in fig1.data:
    fig.add_trace(trace, row=1, col=1)

# Add second plot for % PDL1
fig2 = px.box(result_sorted, x='Treatment_Type', y='%_PDL1', template='plotly_white',
              color='Treatment_Type', color_discrete_map=color_map)
for trace in fig2.data:
    fig.add_trace(trace, row=1, col=2)

# Update layout to match the style and adjust gridlines
fig.update_layout(
    title_text='Distribution of % B7H4 and % PDL1 in Cancer Cells by Treatment',
    title_x=0.5,
    title_font=dict(size=18, family='Arial, sans-serif'),
    xaxis_title='Treatment Type',
    yaxis_title='Percentage',
    xaxis=dict(tickangle=-45, title_font=dict(size=14, family='Arial, sans-serif')),
    yaxis=dict(title_font=dict(size=14, family='Arial, sans-serif')),
    legend_title_text='Treatment',
    legend_title_font=dict(size=12, family='Arial, sans-serif'),
    template='plotly_white',
    width=950,  # Increase the width of the figure
    height=700,  # Increase the height of the figure
)

# Set y-axis range to enhance visibility
fig.update_yaxes(range=[-0.001, 0.036])  # Adjust this range based on your data
 
# Adjust grid and lines
fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='white')
fig.update_xaxes(showline=True, linewidth=2, linecolor='black', mirror=True)
fig.update_yaxes(showline=True, linewidth=2, linecolor='black', mirror=True)

fig.show()


plot(fig)

'temp-plot.html'

In [ ]:
f=

## V.5. XY MAPS

#### V.5.1. CELL SUBTYPES

In [ ]:
#Create a x, y map and visualize the tissues architecture
for sample in ls_samples:
    sample_id = sample.split('_')[0] + '.csv'
    sample_id2 = sample.split('_')[0]
    location_colors = df.loc[df['Sample_ID'] == sample_id,['Nuc_X','Nuc_Y_Inv','cell_type']]

    #print('nb c endo',len(location_colors.loc[location_colors['cell_type']=='ENDOTHELIAL']))
    #print('nb c immune',len(location_colors.loc[location_colors['cell_type']=='IMMUNE']))
    #print('nb c cancer',len(location_colors.loc[location_colors['cell_type']=='CANCER']))

    fig = go.Figure()
    title = sample_id2 + " Background Subtracted XY Map cell types"

    for celltype in df.loc[df['Sample_ID'] == sample_id,'cell_type'].unique():
        fig.add_scatter(
            mode = 'markers',
            marker=dict(size=3, opacity=0.5, color='rgb' + str(cell_type_color_dict[celltype])),
         x = location_colors.loc[location_colors['cell_type']==celltype,'Nuc_X'],
         y = location_colors.loc[location_colors['cell_type']==celltype,'Nuc_Y_Inv'],
         name = celltype)

    fig.update_layout(title = title, plot_bgcolor = 'white')
    fig.update_xaxes(title_text = 'Nuc_X', linecolor = 'black')
    fig.update_yaxes(title_text = 'Nuc_Y_Inv', linecolor = 'black')
    
    # Adjust the size of the points
    for trace in fig.data:
        trace.marker.size = 2  
        # Adjust the size of the points
    for trace in fig.data:
        trace.marker.size = 2  
    fig.update_layout(
        title=title,
        plot_bgcolor='white',
        legend=dict(
            title='Cell Types',  # Titre de la légende
            font=dict(
                family='Arial',
                size=12,
                color='black'
            ),
            bgcolor='white',
            bordercolor='black',
            borderwidth=0.4,
            itemsizing='constant'
        )
    )
    

    #fig.write_image(output_images_dir + "/" + title.replace(" ", "_") + ".png", width=1200, height=800, scale=4)
    print(sample_id,  "processed!")

    fig.show(renderer='png')  # Display the figure as png
    plot(fig)

In [ ]:
#Create a  x,y  map and visualize the tissues architecture
for sample in ls_samples:
    sample_id = sample.split('_')[0] + '.csv'
    sample_id2 = sample.split('_')[0]
    location_colors = df.loc[df['Sample_ID'] == sample_id,['Nuc_X','Nuc_Y_Inv','cell_subtype']]

    fig = go.Figure()
    title = sample_id2 + " Background Subtracted XY Map cell subtypes"

    for cellsubtype in df.loc[df['Sample_ID'] == sample_id,'cell_subtype'].unique():
        fig.add_scatter(
            mode = 'markers',
            marker = dict(size=3, 
                          opacity=0.5, 
                          color='rgb' + str(cell_subtype_color_dict[cellsubtype])),
            x = location_colors.loc[location_colors['cell_subtype']==cellsubtype,'Nuc_X'],
            y = location_colors.loc[location_colors['cell_subtype']==cellsubtype,'Nuc_Y_Inv'],
            name = cellsubtype)

    fig.update_layout(title = title, plot_bgcolor = 'white')
    fig.update_xaxes(title_text = 'Nuc_X', linecolor = 'black')
    fig.update_yaxes(title_text = 'Nuc_Y_Inv', linecolor = 'black')
    
    # Adjust the size of the points
    for trace in fig.data:
        trace.marker.size = 2  
    fig.update_layout(
        title=title,
        plot_bgcolor='white',
        legend=dict(
            title='Cell Subtypes',  #Legende title
            font=dict(
                family='Arial',
                size=12,
                color='black'
            ),
            bgcolor='white',
            bordercolor='black',
            borderwidth=0.4,
            itemsizing='constant'
        )
    )
    

    fig.write_image(output_images_dir + "/" + title.replace(" ", "_") + ".png", width=1200, height=800, scale=4)
    print(sample_id,  "processed!")

    plot(fig)
    fig.show(renderer='png')  # Display the figure as png

#### V.5.1. IMMUNE CHECKPOINTS

In [ ]:
immune_checkpoint_color_dict

In [ ]:
# !!!! test for B7H4 !!!!


for sample in ls_samples:
    sample_id = sample.split('_')[0] + '.csv'
    sample_id2 = sample.split('_')[0]
    location_colors = df.loc[df['Sample_ID'] == sample_id,['Nuc_X','Nuc_Y_Inv','immune_checkpoint']]


    fig = go.Figure()
    title = sample_id2 + " Background Subtracted XY Map immune checkpoint"

    for immunecheckpoint in df.loc[df['Sample_ID'] == sample_id,'immune_checkpoint'].unique():
        fig.add_scatter(
            mode = 'markers',
            marker=dict(size=3, opacity=0.5, color='rgb' + str(immune_checkpoint_color_dict[immunecheckpoint])),
         x = location_colors.loc[location_colors['immune_checkpoint']==immunecheckpoint,'Nuc_X'],
         y = location_colors.loc[location_colors['immune_checkpoint']==immunecheckpoint,'Nuc_Y_Inv'],
         name = immunecheckpoint)

    fig.update_layout(title = title, plot_bgcolor = 'white')
    fig.update_xaxes(title_text = 'Nuc_X', linecolor = 'black')
    fig.update_yaxes(title_text = 'Nuc_Y_Inv', linecolor = 'black')
    
    # Adjust the size of the points
    for trace in fig.data:
        trace.marker.size = 2  
        # Adjust the size of the points
    for trace in fig.data:
        trace.marker.size = 2  
    fig.update_layout(
        title=title,
        plot_bgcolor='white',
        legend=dict(
            title='Immune checkpoint',  # Titre de la légende
            font=dict(
                family='Arial',
                size=12,
                color='black'
            ),
            bgcolor='white',
            bordercolor='black',
            borderwidth=0.4,
            itemsizing='constant'
        )
    )
    

    fig.write_image(output_images_dir + "/" + title.replace(" ", "_") + ".png", width=1200, height=800, scale=4)
    print(sample_id,  "processed!")

    fig.show(renderer='png')  # Display the figure as png
    plot(fig)

In [ ]:
for sample in ls_samples:
    sample_id = sample.split('_')[0] + '.csv'
    sample_id2 = sample.split('_')[0]
    location_colors = df.loc[df['Sample_ID'] == sample_id, ['Nuc_X', 'Nuc_Y_Inv', 'immune_checkpoint']]

    fig = go.Figure()
    title = sample_id2 + " Background Subtracted XY Map immune checkpoint"

    for immunecheckpoint in df.loc[df['Sample_ID'] == sample_id, 'immune_checkpoint'].unique():
        # Vérifier si la combinaison est dans le dictionnaire avant d'ajouter la trace
        if immunecheckpoint in immune_checkpoint_color_dict:
            color = 'rgb' + str(immune_checkpoint_color_dict[immunecheckpoint])
            
            fig.add_scatter(
                mode='markers',
                marker=dict(size=3, opacity=0.5, color=color),
                x=location_colors.loc[location_colors['immune_checkpoint'] == immunecheckpoint, 'Nuc_X'],
                y=location_colors.loc[location_colors['immune_checkpoint'] == immunecheckpoint, 'Nuc_Y_Inv'],
                name=immunecheckpoint
            )
    
    fig.update_layout(
        title=title,
        plot_bgcolor='white',
        xaxis_title='Nuc_X',
        yaxis_title='Nuc_Y_Inv',
        legend_title='Immune checkpoint',
        legend=dict(
            font=dict(
                family='Arial',
                size=12,
                color='black'
            ),
            bgcolor='white',
            bordercolor='black',
            borderwidth=0.4,
            itemsizing='constant'
        )
    )
    
    fig.write_image(output_images_dir + "/" + title.replace(" ", "_") + ".png", width=1200, height=800, scale=4)
    print(sample_id,  "processed!")

    fig.show(renderer='png')  # Display the figure as png
    plot(fig)


### V.5.2. CELL SUBTYPE DENSITY

In [ ]:
from shapely.geometry import MultiPoint

 

# Convert pixel to mm

df['x_mm'] = df['Nuc_X'] * 0.650 / 1000

df['y_mm'] = df['Nuc_Y_Inv'] * 0.650 / 1000

 

# Group by Sample_ID and ROI_Index and calculate the convex hull for each group

df_grouped = df.groupby(['Sample_ID', 'ROI_index']).apply(lambda group: MultiPoint(group[['x_mm', 'y_mm']].values).convex_hull)

 

# Calculate the area of each convex hull

df_area = df_grouped.apply(lambda hull: hull.area if hull.geom_type == 'Polygon' else 0)

 

# Convert to DataFrame

df_area = pd.DataFrame(df_area, columns=['Area_mm2'])

 

print(df_area)

## V.6. CORRELATION PLOTS

In [ ]:
# Get Pearson correlations and P values for all marker values
# First, get we need to determine how many columns we will be evaluating. 
# And prepare empty Numpy arrays to hold our data.

In [ ]:
#This is a work in progress section, need to run this on individual cell types instead of all cell types together

keep_sample_Set_A = [ 'TMA.csv', 'D3S1.csv', 'D3S2.csv','D3S3.csv','D4S1.csv','D4S2.csv','D4S3.csv','D5S1.csv','D5S2.csv','D5S3.csv']
keep_sample_Set_B = [ 'TMA.csv', 'DD3S1.csv','DD3S2.csv','DD3S3.csv','DD4S1.csv','DD4S2.csv','DD4S3.csv','DD5S1.csv','DD5S2.csv','DD5S3.csv']
keep_cell_type = [ 'CANCER', 'STROMA', 'ENDOTHELIAL', 'IMMUNE' ]

# Check project name and execute corresponding operations
if project_name == 'Set_A':
    keep_sample = keep_sample_Set_A
elif project_name == 'Set_B':
    keep_sample = keep_sample_Set_B
else:
    raise ValueError("Unknown project name.")

df_keep_sample = df.loc[(df['Sample_ID'].isin(keep_sample))
                      & (df['Sample_ID'].isin(keep_sample)), :].copy()

# df_keep_sample will change regarding which sample you decided to keep in the kee_sample_proj list
df_keep_sample

In [ ]:
# n_corr_cols is the number of colums you will compute the correlations with
# (columns in df_keep_sample that are not in the list not_intensities)
n_corr_cols = len(df_keep_sample.columns[~df_keep_sample.columns.isin(not_intensities)])
print(n_corr_cols)

In [ ]:
# An empty 2D NumPy array is created with dimensions n_corr_cols by n_corr_cols and assigned to the variable pvalues 
# This array is intended to store p-values.
pvalues = np.empty((n_corr_cols, n_corr_cols))

# Similarly, another empty 2D NumPy array with dimensions n_corr_cols by n_corr_cols is created and assigned to the variable corrvalues. 
# This array is intended to store correlation values.
corrvalues = np.empty((n_corr_cols,n_corr_cols))

#print(pvalues)
#print(corrvalues)

In [ ]:
# Columns of the DataFrame for_corr are renamed using the dictionary full_to_short_names
for_corr = df_keep_sample.loc[:,~df_keep_sample.columns.isin(not_intensities)].copy()
for_corr = for_corr.rename(columns = full_to_short_names)
for_corr.shape

In [ ]:
# Compute Pearson correlation coefficient and the corresponding p-value for each pair of columns in dataframe
for i in range(for_corr.shape[1]):
    for j in range(0,for_corr.shape[1]):
        col1 = for_corr[for_corr.columns.values[i]]
        col2 = for_corr[for_corr.columns.values[j]]
        corrvalues[i,j] = pearsonr(col1,col2)[0]
        pvalues[i,j] = pearsonr(col1,col2)[1]

In [ ]:
# Correlation and p-value calculations are being organized and formatted into dataframes
corrvalues = pd.DataFrame(corrvalues).round(3)
corrvalues.columns = for_corr.columns.values
corrvalues.index = for_corr.columns.values

pvalues = pd.DataFrame(pvalues)
pvalues.columns = for_corr.columns.values
pvalues.index = for_corr.columns.values

### V.6.1. OPTION 1

In [ ]:
# Visualizing and marking statistically significant p-values with an asterisk (*) 
# for ease of interpretation
# p-values that are less than or equal to 0.05

# p_add_star() in my_modules.py
p_w_star = pvalues.copy()
p_w_star = p_w_star.apply(lambda row: p_add_star(row), axis = 1)
p_w_star.columns = for_corr.columns.values
p_w_star.head()

In [ ]:
# Check if there is non-significant values
for index, row in p_w_star.iterrows():
    for col in p_w_star.columns:
        value = p_w_star.loc[index, col]
        if "*" not in value:
            print(f"Value without asterisk found at index: {index}, column: {col}, value: {value}")

In [ ]:
# Correlation visualization
sb.set()

x_axis_labels = for_corr.columns.values.tolist()
y_axis_labels = for_corr.columns.values.tolist()

ax = sb.heatmap(corrvalues, 
                annot = p_w_star, 
                annot_kws = {"size": 1.25},
                fmt = 's',
                xticklabels = x_axis_labels, 
                yticklabels = y_axis_labels,
                cbar_kws = {'label':'Pearson correlation'},
                linecolor = 'black', 
                linewidth = 0.5,
                cmap = 'coolwarm')

plt.yticks(rotation=0, size = 5)
ax.xaxis.tick_top() # x axis on top
ax.xaxis.set_label_position('top')
ax.tick_params(length=0)
plt.xticks(rotation=45, size = 5)
plt.setp(ax.xaxis.get_majorticklabels(), ha='left')

ax.set_title(label = "Correlations option 1", fontsize = 20)
plt.tight_layout()

filename = "correlations_option1.png"
filename = os.path.join(output_images_dir, filename)
plt.savefig(filename,dpi=500)

### V.6.2. OPTION 2

In [ ]:
# If the item is less than or equal to 0.001, it assigns 3 asterisks, 
# if less than or equal to 0.01, it assigns 2 asterisks, 
# if less than or equal to 0.05, it assigns 1 asterisk, 
# and if greater than 0.05, it assigns 0 asterisks. 

# p_to_star() in my_modules.py
p_as_stars = pvalues.copy()
p_as_stars = p_as_stars.apply(lambda row: p_to_star(row), axis = 1)
p_as_stars.columns = for_corr.columns.values
p_as_stars.head()

In [ ]:
corr_w_star = corrvalues.round(2).astype(str) + p_as_stars
corr_w_star.head()

In [ ]:
# Check if there is non-significant values
for index, row in corr_w_star.iterrows():
    for col in corr_w_star.columns:
        value = corr_w_star.loc[index, col]
        if "*" not in value:
            print(f"Value without asterisk found at index: {index}, column: {col}, value: {value}")

In [ ]:
corrvalues.shape

In [ ]:
corr_w_star.shape

In [ ]:
# Correlation visualization
sb.set()

x_axis_labels = for_corr.columns.values.tolist()
y_axis_labels = for_corr.columns.values.tolist()

ax = sb.heatmap(corrvalues, 
                annot = corr_w_star, 
                annot_kws = {"size": 1.25},
                fmt = 's',
                xticklabels = x_axis_labels, 
                yticklabels=y_axis_labels,
                cbar_kws = {'label':'Pearson correlation'},
                linecolor = 'black', linewidth = 0.5,
                cmap = 'coolwarm')

plt.yticks(rotation=0, size = 5)
ax.xaxis.tick_top() # x axis on top
ax.xaxis.set_label_position('top')
ax.tick_params(length=0)
plt.xticks(rotation=45, size = 5)
plt.setp(ax.xaxis.get_majorticklabels(), ha='left')

ax.set_title(label = "Correlations option 2", fontsize = 20)
plt.tight_layout()

filename = "correlations_option2.png"
filename = os.path.join(output_images_dir, filename)
plt.savefig(filename,dpi=500)

In [ ]:
filename = "zscore_pearson_correlations.csv"
filename = os.path.join(output_data_dir, filename)
corrvalues.to_csv(filename, index = True)

filename = "zscore_pearson_p-values.csv"
filename = os.path.join(output_data_dir, filename)
pvalues.to_csv(filename, index = True)

## V.7. PCA

In [ ]:
def demo_PCA(data, c):
    reduced_data = PCA(n_components=2).fit_transform(data)
    kmeans = KMeans(init="k-means++", n_clusters=c, n_init=4)
    kmeans.fit(reduced_data)

    # Step size of the mesh. Decrease to increase the quality of the VQ.
    h = 0.02  # point in the mesh [x_min, x_max]x[y_min, y_max].

    # Plot the decision boundary. For that, we will assign a color to each
    x_min, x_max = reduced_data[:, 0].min() - 1, reduced_data[:, 0].max() + 1
    y_min, y_max = reduced_data[:, 1].min() - 1, reduced_data[:, 1].max() + 1
    xx, yy = np.meshgrid(np.arange(x_min, x_max, h), np.arange(y_min, y_max, h))

    # Obtain labels for each point in mesh. Use last trained model.
    Z = kmeans.predict(np.c_[xx.ravel(), yy.ravel()])

    # Put the result into a color plot
    Z = Z.reshape(xx.shape)
    plt.figure(1)
    plt.clf()
    plt.imshow(
        Z,
        interpolation="nearest",
        extent=(xx.min(), xx.max(), yy.min(), yy.max()),
        cmap=plt.cm.Paired,
        aspect="auto",
        origin="lower",
    )

    plt.plot(reduced_data[:, 0], reduced_data[:, 1], "k.", markersize=2)
    # Plot the centroids as a white X
    centroids = kmeans.cluster_centers_
    plt.scatter(
        centroids[:, 0],
        centroids[:, 1],
        marker="x",
        s=169,
        linewidths=3,
        color="w",
        zorder=10,
    )
    plt.title(
        "K-means clustering on the dataset (PCA-reduced data)\n"
        "Centroids are marked with white cross"
    )
    plt.xlim(x_min, x_max)
    plt.ylim(y_min, y_max)
    plt.xticks(())
    plt.yticks(())
    plt.show()
    
    return None


def other_PCA(data, c):
    reduced_data = PCA(n_components=2).fit_transform(data)
    ###kmeans = KMeans(init="k-means++", n_clusters=c, n_init=4)
    ###kmeans.fit(reduced_data)
    
    plt.scatter(reduced_data[:,0], reduced_data[:,1], cmap = 'plasma')
    plt.xlabel('1st Principal Component')
    plt.ylabel('2nd Principal Component')
    plt.title('Scatter Plot of the 2 Principal Component')
    plt.show()
    
    return None

In [ ]:
df_test=df.loc[:,~df.columns.isin(not_intensities)]
demo_PCA(df_test, 100)

In [ ]:
other_PCA(df_test, 100)

## V.8. KMEANS

In [ ]:
# Define number of clusters - according to set & cell type

def kmeans_analysis(df, c):
    analyzed_df = df.loc[:,~df.columns.isin(not_intensities)]
    ###kM = KMeans(n_clusters=c).fit_predict(analyzed_df)
    kM = KMeans(n_clusters=c).fit(analyzed_df)
    ###centroids = kmeans.cluster_centers_ #list of clusters. Each cluster is a matrix of means for each parameter (protein) analyzed
    labels = kM.labels_
    clusterCount = np.bincount(labels) #holds information for how many points are in each cluster
    ###plt.scatter(normed_V1, normed_V2, s=10, c=labels, cmap='coolwarm') # instead of c=bn_class
    return None

def scale_data(df):
    pca = PCA(n_components=2) #We are doing a 2D data visualisation, so we need to select 2 principal components for PCA
    sc = StandardScaler()
    df_scaled = sc.fit_transform(df.loc[:,~df.columns.isin(not_intensities)])
    PCs = pca.fit_transform(df_scaled)
    return PCs, df_scaled

def plot_kmeans(df, nb_cl):
    pc, scaled_df = scale_data(df)
    ###kmeans = KMeans(n_clusters= nb_cl).fit(scaled_df)
    ###df_predict = kmeans.predict(scaled_df)
    test = KMeans(n_clusters= nb_cl).fit_predict(scaled_df)
    sb.scatterplot(x=pc[:,0],y=pc[:,1],hue=test)
    return None

def kmeans_plotting(df, c):
    analyzed_df = df.loc[:,~df.columns.isin(not_intensities)]
    #Initialize the class object
    kmeans = KMeans(n_clusters= c)
    #Predict the labels of clusters.
    l = kmeans.fit_predict(analyzed_df) #returns the array of cluster labels each data point belongs to
    plot_results(l)
    return l

def plot_results(label): #https://www.askpython.com/python/examples/plot-k-means-clusters-python
    #Getting unique labels
    u_labels = np.unique(label)
    #Plotting the results
    for i in u_labels:
        plt.scatter(df.iloc[label == i , 0] , df.iloc[label == i , 1] , label = i)
    plt.title("K-means clustering")
    plt.legend(loc='center left', title = "Clusters", bbox_to_anchor=(1, 0.5))
    plt.show()
    return None

In [ ]:
# Define number of clusters - according to set & cell type

clusterList = kmeans_analysis(df, 20)
plot_kmeans(df, 20)

In [ ]:
clusterLabels_array = kmeans_plotting(df, 20)

## pca + kmean

In [ ]:
def standardization(df):
    df = df.loc[:,~df.columns.isin(not_intensities)]
    scaler = StandardScaler()
    data_std = scaler.fit_transform(df)
    return data_std

def determine_features_kept(x, y):
    real_componentValue = np.interp(0.8, y, x)
    rounded_componentValue = round(real_componentValue)
    print("Number of features/components kept : {}".format(rounded_componentValue))
    return rounded_componentValue

def explained_variance(pCA):
    y = pCA.explained_variance_ratio_
    max_range = len(y) + 1
    x = range(1,max_range)
    plt.figure(figsize = (10,8))
    plt.plot(x, y.cumsum(), marker = 'o', linestyle = '--')
    plt.title("Explained Variance by Components")
    plt.xlabel("Number of components")
    plt.ylabel("Cumulative Explained Variance")
    plt.show()
    nb_features = determine_features_kept(x, y.cumsum())
    return nb_features

def pca_analysis(nb_feat, df):
    pca = PCA(n_components = nb_feat)
    pca.fit(df)
    scores_pca = pca.transform(df)
    return scores_pca

def dimensionality_reduction(df): #using PCA
    standard_df = standardization(df)
    pca = PCA()
    pca.fit(standard_df)
    nb_components = explained_variance(pca)
    pca_scores = pca_analysis(nb_components, standard_df)
    return pca_scores

In [ ]:
scoresPCA = dimensionality_reduction(df)

In [ ]:
def determine_slope(a, b):
    return abs((b[1] - a[1]) / (b[0] - a[0]))

def record_slopes(X, Y):
    slope_list = []
    if len(X) == len(Y):
        for i in range(len(X)-1):
            A = (X[i], Y[i])
            B = (X[i+1], Y[i+1])
            slope = determine_slope(A, B)
            slope_list.append(slope)
    else:
        print("Error! length of X and Y coordinates do not match!")
        slope_list.append(0)
    return slope_list

def elbow_coordinates(diff_ls, x_coord):
    max_diff = max(diff_ls) #the slopes with the highest difference correspond to the "sharpest" elbow
    index_max = diff_ls.index(max_diff)   
    s_coord = x_coord[index_max+1] #we determine the X position of the elbow
    return s_coord

def highest_slope_diff(ls_slopes, coord_x):
    ls_diffs = [] #list of slope differences
    for i in range(len(ls_slopes)-1):
        diff = abs(ls_slopes[i] - ls_slopes[i+1]) #compare differences between each slope
        ls_diffs.append(diff)
    elbow = elbow_coordinates(ls_diffs, coord_x) #returns the X coordinates where the elbow is
    return elbow

In [ ]:
liste = [46405799.34079681, 38240577.23298195, 35026058.95518527, 32185738.815936424, 30500185.571518555, 28678764.340087377, 27418667.363556623, 26234063.97845333, 25405258.778627113, 24454635.699228957]
x = list(range(1, 11))

highest_slope_diff(liste, x)

## V.9. T-SNE

In [ ]:
# Implémente notre dataset
## A partir df_tsne, ajoute colonne(s) d'intérêt
cols = list(df.columns)
df['Patient']= df['Patient']
df['cell_type']= df['cell_type']
print('Size of the dataframe: {}'.format(df.shape))

## Selectionner nb random de valeurs (temp, pr performance)
np.random.seed(50)
rndperm = np.random.permutation(df.shape[0])

In [ ]:
#Remove index values (unneeded & handicapping for T-SNE analysis)
df = df.reset_index(drop=True)
df.head()

In [ ]:
#Keep only the numbers in the patient ID column
df['Patient'] = df['Patient'].map(lambda x: x.lstrip('Pt'))
df.head()

In [ ]:
#t-sne
N = 20000

df_subset = df.loc[rndperm[:N],:].copy() #remove later for full subset? (since it is already a subset)

data_subset = df_subset[cols].values

pca = PCA(n_components=3)
data_subset

In [ ]:

pca_result = pca.fit_transform(data_subset)

df_subset['pca-one'] = pca_result[:,0]
df_subset['pca-two'] = pca_result[:,1] 
df_subset['pca-three'] = pca_result[:,2]

print('Explained variation per principal component: {}'.format(pca.explained_variance_ratio_))

## V.10. SAVE

In [ ]:
# Save the data by Sample_ID
# Check for the existence of the output file first
for sample in ls_samples:
    sample_id = sample.split('_')[0]
    filename = os.path.join(output_data_dir,  sample_id + "_" + step_suffix + ".csv")
    if os.path.exists(filename):
        print("File by name "+filename+" already exists.")
    else:
        sample_id_csv = sample_id + '.csv'
        df_save = df.loc[df['Sample_ID'] == sample_id_csv, :]
        #print(df_save)
        filename = os.path.join(output_data_dir,  sample_id + "_" + step_suffix + ".csv")
        df_save.to_csv(filename, index=True, index_label='ID')  # Set index parameter to True to retain the index column
        print("File " + filename + " was created!")

In [ ]:
# Save the dataset as a single file for TSNE/UMAP notebook
filename = "all_Samples_" + project_name + ".csv"
filename = os.path.join(output_data_dir, filename)

if os.path.exists(filename):
    print("File by name "+filename+" already exists.")
else :
    df.to_csv(filename, index = False)
    print("File " + filename + " was created!")